# Introduction

The following notebook orchestrates the migration of ADPDX Accounts into Salesforce.


# Order of Loading

1. Vicariates
1. Organizations
1. Religious Parents
1. Religious Communities
1. Religious Superiors
1. Contacts
1. Contact > Register Entries
1. Contact > Education Affiliations
1. Contact > Ecclesial Affiliations
1. Affiliations



# Setup Enviro


In [15]:
# !conda install -y simple-salesforce
# !conda install -y email_validator
# !conda install -y python-dotenv
# !conda install import-ipynb

In [16]:
# enviro setup

import pandas as pd
import numpy as np

from datetime import datetime
now = datetime.now()

from simple_salesforce import Salesforce

In [17]:
# import environment variables (SF login credentials)
from dotenv import load_dotenv
import os

load_dotenv()

True

In [18]:
# Global Variables { run: "auto", vertical-output: true, display-mode: "both" }

target_enviro = "adpdx_devpro" # @param {type:"string"}

# The `run_upserts` variable controls whether or not upserts to Salesforce are executed when the notebook is run.
run_upserts = "True" # @param ["True", "False"]

In [19]:
# ADPDX dev_pro credentials
adpdx_user = os.getenv('ADPDX_UAT_USER')
print(adpdx_user)
adpdx_pass = os.getenv('ADPDX_UAT_PASS')
print( adpdx_pass)
adpdx_token = os.getenv('ADPDX_UAT_TOKEN')
print(adpdx_token)

# instantiate a SF session object
sf = Salesforce(domain='test', username=adpdx_user, password=adpdx_pass, security_token=adpdx_token)

matt+adpdx@meribahflow.com.uat
CSN?QM3e
97zjin7eBEEHmN5uBLIYWX0J


## UDFs


In [20]:
# General notebook UDFs

import json
import csv
from datetime import datetime
from simple_salesforce import Salesforce

# Job ID Incrementer
def update_job_id(file_name):
    # Open the file in read mode and get the current job ID
    with open(file_name, 'r') as file:
        current_job_id = int(file.readline())

    # Increment the job ID
    new_job_id = current_job_id + 1

    # Open the file in write mode and update the job ID
    with open(file_name, 'w') as file:
        file.write(str(new_job_id))

    # Return the new job ID
    return new_job_id


def concat_columns(df, columns, new_column, separator='_'):
    """
    Concatenates the values from specified columns into a single string
    with the specified separator and populates a new column in the DataFrame.

    Args:
    - df: pandas DataFrame
    - columns: list of column names to concatenate
    - new_column: name of the new column to be created
    - separator: separator to use between concatenated values (default is '_')

    Returns:
    - Updated pandas DataFrame with the new column
    """
    df[new_column] = df[columns].astype(str).apply(lambda x: separator.join(x), axis=1)
    return df


def convert_non_serializables(data):
    """Convert non-serializable objects to serializable formats."""
    for key, value in data.items():
        try:
            if isinstance(value, (datetime, date)):
                data[key] = value.isoformat()
            elif isinstance(value, float) and np.isnan(value):
                data[key] = None
            elif pd.isna(value):
                data[key] = None
            elif isinstance(value, (int, bool, str, bool)):
                data[key] = value
            else:
                data[key] = str(value)  # Convert other types to string
        except Exception as e:
            print(f"Error processing key: {key}, value: {value}, error: {e}")
    return data

In [21]:
# Query, merge data with SF data  

import pandas as pd
from simple_salesforce import Salesforce
from simple_salesforce.exceptions import SalesforceMalformedRequest, SalesforceError

def find_salesforce_record_id(sf, df, column_to_search, sf_object_name, sf_field_name, new_column_name, match_behavior='first'):
    """
    Find Salesforce record IDs for a DataFrame column and add a new column with the Salesforce record IDs.

    Parameters:
    sf (Salesforce): The Salesforce connection instance.
    df (pd.DataFrame): The pandas DataFrame containing data.
    column_to_search (str): The column name in the DataFrame to search against Salesforce.
    sf_object_name (str): The Salesforce object name (e.g., 'Contact').
    sf_field_name (str): The field name in Salesforce to match.
    new_column_name (str): The name for the new DataFrame column to hold Salesforce record IDs.
    match_behavior (str): Behavior when multiple matches found ('first' or 'alert').

    Returns:
    pd.DataFrame: The original DataFrame with the new column containing Salesforce record IDs.

    Example usage:
    df_contact_staging = find_salesforce_record_id(sf, df_contact_staging, 'Link_to_Religious_Community', 'Contact', 'Archdpdx_Migration_Id__c', 'New_Column_Name', match_behavior='alert')

    """
    if column_to_search not in df.columns:
        raise ValueError(f"Column '{column_to_search}' not found in DataFrame.")

    df[new_column_name] = None
    multiple_matches_found = False

    unique_values = df[column_to_search].dropna().unique()
    chunk_size = 1000  # Adjust chunk size as needed

    for start in range(0, len(unique_values), chunk_size):
        chunk_values = unique_values[start:start + chunk_size]
        chunk_values_str = ", ".join([f"'{val}'" for val in chunk_values])

        soql_query = f"SELECT Id, {sf_field_name} FROM {sf_object_name} WHERE {sf_field_name} IN ({chunk_values_str})"
        
        try:
            query_result = sf.query_all(soql_query)
        except SalesforceMalformedRequest as e:
            raise ValueError(f"Malformed request error: {e.content}")
        except SalesforceError as e:
            raise ValueError(f"Salesforce error: {e.content}")

        id_mapping = {}
        for record in query_result['records']:
            key = record[sf_field_name]
            if key in id_mapping:
                multiple_matches_found = True
                if match_behavior == 'first':
                    continue  # Skip subsequent matches if 'first' behavior is selected
            id_mapping[key] = record['Id']

        df[new_column_name] = df[column_to_search].map(id_mapping)

    if multiple_matches_found and match_behavior == 'alert':
        print("Alert: Multiple matches found for some records.")

    return df


def get_recordtype_id(df_recordTypes, developer_name, sobject_type, namespace):
    """
    Retrieves the Record Type ID for a specific Developer Name, SObject Type, and Namespace.

    Parameters:
    df_recordTypes (pd.DataFrame): The DataFrame containing Salesforce Record Types.
    developer_name (str): The DeveloperName to filter by.
    sobject_type (str): The SObjectType to filter by.
    namespace (str): The Namespace to filter by.

    Returns:
    str: The Record Type ID if a match is found, otherwise raises an error.

    Example: 
    religious_recordtype_id = get_recordtype_id(df_sf_recordTypes, 'Religious', 'Account', 'mbfc')
    """
    try:
        recordtype_id = df_recordTypes.loc[
            (df_recordTypes['DeveloperName'] == developer_name) & 
            (df_recordTypes['SobjectType'] == sobject_type) &
            (df_recordTypes['NamespacePrefix'] == namespace),
            'Id'
        ].iloc[0]  # Retrieve the first match
        
        return recordtype_id
    except IndexError:
        raise ValueError(f"No record type found for DeveloperName '{developer_name}', SObjectType '{sobject_type}', and Namespace '{namespace}'")


# Add a Salesforce record ID column to a DataFrame based on matching external ID field values
def add_salesforce_record_ids(sf, dataframe, df_column_name, sf_object_name, sf_external_id_field, new_column_name, chunk_size=1000):
    """
    Add a Salesforce record ID column to a DataFrame based on matching external ID field values.

    Parameters:
    sf (Salesforce): The Salesforce connection instance.
    dataframe (pd.DataFrame): The pandas DataFrame containing data to match.
    df_column_name (str): The column name in the DataFrame to match with Salesforce.
    sf_object_name (str): The Salesforce object name (e.g., 'Contact').
    sf_external_id_field (str): The external ID field in Salesforce to match.
    new_column_name (str): The name for the new DataFrame column to hold Salesforce record IDs.
    chunk_size (int): The number of records to include in each chunk for querying Salesforce.

    Returns:
    pd.DataFrame: The original DataFrame with the new column containing Salesforce record IDs.
    """
    # Ensure the dataframe column name exists in the dataframe
    if df_column_name not in dataframe.columns:
        raise ValueError(f"Column '{df_column_name}' not found in DataFrame.")
    
    # Create a set of unique values from the specified DataFrame column
    unique_values = dataframe[df_column_name].dropna().unique()
    
    id_mapping = {}
    
    # Process the unique values in chunks
    for start in range(0, len(unique_values), chunk_size):
        chunk_values = unique_values[start:start + chunk_size]
        chunk_values_str = ", ".join([f"'{val}'" for val in chunk_values])
        
        soql_query = f"SELECT Id, {sf_external_id_field} FROM {sf_object_name} WHERE {sf_external_id_field} IN ({chunk_values_str})"
        
        try:
            query_result = sf.query_all(soql_query)
        except SalesforceMalformedRequest as e:
            raise ValueError(f"Malformed request error: {e.content}")
        except SalesforceError as e:
            raise ValueError(f"Salesforce error: {e.content}")
        
        # Update the id_mapping with results from the current chunk
        id_mapping.update({record[sf_external_id_field]: record['Id'] for record in query_result['records']})
    
    # Map the Salesforce record IDs to the DataFrame
    dataframe[new_column_name] = dataframe[df_column_name].map(id_mapping)
    
    return dataframe

In [22]:
# Upsert to SF

import pandas as pd
import numpy as np
from simple_salesforce import Salesforce, SalesforceMalformedRequest, SalesforceError
from datetime import datetime, date

# Gets or creates a Diocesan account based on the Account Name
def get_or_create_diocesan_account(sf, account_name):
    """
    Searches for an account by name, returns the ID if found,
    otherwise creates the account with RecordType 'Church' and 'mbfc__Church_Type__c' set to 'Diocese',
    and then returns the new ID.

    Parameters:
    sf (Salesforce): Salesforce connection object
    account_name (str): The name of the account to search for or create

    Returns:
    str: The ID of the found or created account
    """

    # Query for the Record Type ID using the Developer Name 'Church'
    record_type_query = "SELECT Id FROM RecordType WHERE SobjectType = 'Account' AND DeveloperName = 'Church' LIMIT 1"
    record_type_result = sf.query(record_type_query)
    if record_type_result['records']:
        record_type_id = record_type_result['records'][0]['Id']
    else:
        raise ValueError("No RecordType found with DeveloperName 'Church'")

    # Search for the Account by name
    account_query = f"SELECT Id FROM Account WHERE Name = '{account_name}' LIMIT 1"
    account_result = sf.query(account_query)
    
    if account_result['records']:
        # Account found, return the ID
        return account_result['records'][0]['Id']
    else:
        # Account not found, create a new Account
        account_data = {
            'Name': account_name,
            'RecordTypeId': record_type_id,
            'mbfc__Church_Type__c': 'Diocese'
        }
        new_account = sf.Account.create(account_data)
        return new_account['id']
    
    from simple_salesforce import Salesforce

# improved version of the get_or_create_diocesan_account function
def get_or_create_account(sf, account_name, record_type_dev_name, church_type):
    """
    Searches for an account by name, returns the ID if found,
    otherwise creates the account with the specified Record Type and Church Type,
    and then returns the new ID.

    Parameters:
    sf (Salesforce): Salesforce connection object
    account_name (str): The name of the account to search for or create
    record_type_dev_name (str): The developer name of the Record Type to use for creating the account
    church_type (str): The Church Type to set for the new account

    Returns:
    str: The ID of the found or created account

    Example usage: 
    sf = Salesforce(username='your_username', password='your_password', security_token='your_security_token')
    account_id = get_or_create_account(sf, 'Diocese of Calgary', 'Church', 'Diocese')
    print(f"Account ID: {account_id}")
    """

    # Query for the Record Type ID using the provided developer name
    record_type_query = f"SELECT Id FROM RecordType WHERE SobjectType = 'Account' AND DeveloperName = '{record_type_dev_name}' LIMIT 1"
    record_type_result = sf.query(record_type_query)
    if record_type_result['records']:
        record_type_id = record_type_result['records'][0]['Id']
    else:
        raise ValueError(f"No RecordType found with DeveloperName '{record_type_dev_name}'")

    # Search for the Account by name
    account_query = f"SELECT Id FROM Account WHERE Name = '{account_name}' LIMIT 1"
    account_result = sf.query(account_query)
    
    if account_result['records']:
        # Account found, return the ID
        return account_result['records'][0]['Id']
    else:
        # Account not found, create a new Account
        account_data = {
            'Name': account_name,
            'RecordTypeId': record_type_id,
            'mbfc__Church_Type__c': church_type
        }
        new_account = sf.Account.create(account_data)
        return new_account['id']


# def upsert_to_salesforce(sf, dataframe, object_name, external_id_field):
#     """
#     Upsert records to Salesforce from a pandas DataFrame.

#     Parameters:
#     sf (Salesforce): The Salesforce connection instance.
#     dataframe (pd.DataFrame): The pandas DataFrame containing data to upsert.
#     object_name (str): The Salesforce object name (e.g., 'Contact').
#     external_id_field (str): The external ID field used for upserts.
#     """
#     successful_upserts = 0
#     failed_upserts = 0

#     # Replace placeholder values with None in the DataFrame
#     dataframe.replace({None: pd.NA, ' ': None, '': None}, inplace=True)

#     # Convert DataFrame to a list of dictionaries
#     data_to_upsert = dataframe.to_dict(orient='records')

#     for data in data_to_upsert:
#         try:
#             data = convert_non_serializables(data)
#             external_id = data.pop(external_id_field)

#             # Perform upsert using only the External ID
#             response = getattr(sf, object_name).upsert(f'{external_id_field}/{external_id}', data)
#             successful_upserts += 1
#             print(f"Successfully upserted {object_name} with External ID: {external_id}")
#         except SalesforceMalformedRequest as e:
#             failed_upserts += 1
#             print(f"Malformed request error when upserting {object_name} with External ID: {external_id}. Error: {e.content}")
#         except SalesforceError as e:
#             failed_upserts += 1
#             print(f"Salesforce error when upserting {object_name} with External ID: {external_id}. Error: {e.content}")
#         except Exception as e:
#             failed_upserts += 1
#             print(f"Failed to upsert {object_name} with External ID: {external_id}. Error: {e}")

#     print(f"Upsert completed. Successful upserts: {successful_upserts}, Failed upserts: {failed_upserts}")


def upsert_to_salesforce_bulk(sf, dataframe, object_name, external_id_field, results_log_file, batch_size=100):
    """
    Upsert records to Salesforce from a pandas DataFrame using the Bulk API.

    Parameters:
    sf (Salesforce): The Salesforce connection instance.
    dataframe (pd.DataFrame): The pandas DataFrame containing data to upsert.
    object_name (str): The Salesforce object name (e.g., 'Contact').
    external_id_field (str): The external ID field used for upserts.
    results_log_file (str): The file name where the full upsert results will be logged.
    batch_size (int): The number of records to include in each batch.
    """
    successful_upserts = 0
    failed_upserts = 0
    batch_number = 0

    # Replace placeholder values with None in the DataFrame
    dataframe.replace({pd.NA: None, ' ': None, '': None}, inplace=True)

    # Convert DataFrame to a list of dictionaries
    data_to_upsert = dataframe.to_dict(orient='records')

    # Open the results log file in 'write' mode to truncate/overwrite existing data
    with open(results_log_file, 'w') as results_log:
        writer = csv.writer(results_log)
        writer.writerow(['Batch Number', 'Record', 'Success', 'Error'])  # Write the headers

        # Process data in batches
        for i in range(0, len(data_to_upsert), batch_size):
            batch_number += 1
            batch_data = data_to_upsert[i:i + batch_size]
            batch_data = [convert_non_serializables(record) for record in batch_data]

            try:
                # Perform bulk upsert
                response = sf.bulk.__getattr__(object_name).upsert(batch_data, external_id_field=external_id_field)

                for index, res in enumerate(response):
                    if res['success']:
                        successful_upserts += 1
                        writer.writerow([batch_number, json.dumps(batch_data[index]), 'True', ''])
                    else:
                        failed_upserts += 1
                        writer.writerow([batch_number, json.dumps(batch_data[index]), 'False', json.dumps(res['errors'])])

            except SalesforceMalformedRequest as e:
                failed_upserts += len(batch_data)
                writer.writerow([batch_number, '', 'False', f"Malformed request: {e.content}"])
                for record in batch_data:
                    writer.writerow([batch_number, json.dumps(record), 'False', f"Failed record due to malformed request"])

            except SalesforceError as e:
                failed_upserts += len(batch_data)
                writer.writerow([batch_number, '', 'False', f"Salesforce error: {e.content}"])
                for record in batch_data:
                    writer.writerow([batch_number, json.dumps(record), 'False', f"Failed record due to Salesforce error"])

            except Exception as e:
                failed_upserts += len(batch_data)
                writer.writerow([batch_number, '', 'False', f"Unexpected error: {str(e)}"])
                for record in batch_data:
                    writer.writerow([batch_number, json.dumps(record), 'False', f"Failed record due to unexpected error"])

            # Progress monitoring
            print(f"Batch {batch_number} processed: {successful_upserts} successful, {failed_upserts} failed.")

    # Final summary message
    total_records = len(data_to_upsert)
    total_batches = batch_number
    print(f"Upsert completed. Total records processed: {total_records}, Batches: {total_batches}, "
          f"Successful upserts: {successful_upserts}, Failed upserts: {failed_upserts}")

## Extract Salesforce xref data

The following cells downloads all records from the target Salesforce enviro for the following objects:

- RecordTypes
- Users
- Accounts
- Contacts


In [23]:
# Get or create the Diocesan Account and get its ID
diocesan_account_id = get_or_create_account(sf, 'Archdiocese of Portland in Oregon', 'Church', 'Diocese')

print(f"Account ID: {diocesan_account_id}")

Account ID: 001Dx00001HwDsgIAF


In [24]:
# get all ACTIVE SF users

sf_users = sf.query('Select Alias, FirstName, LastName, Username, id from User WHERE IsActive = True')
df_sf_users = pd.DataFrame(sf_users['records'])
df_sf_users = df_sf_users.drop(columns = 'attributes')

In [25]:
# get all SF Record Types
get_all_recordTypes = 'Select Id, Name, DeveloperName, sObjecttype, namespaceprefix from RecordType'

# get list of records, add to dataframe
sf_recordTypes = sf.query(get_all_recordTypes)
df_sf_recordTypes = pd.DataFrame(sf_recordTypes['records'])
df_sf_recordTypes = df_sf_recordTypes.drop(columns = 'attributes')

# Drop NPSP's 'Organization' record type  
df_sf_recordTypes = df_sf_recordTypes[
    ~((df_sf_recordTypes['Name'] == 'Organization') & (df_sf_recordTypes['NamespacePrefix'].isna()))
]

# Create a dictionary mapping 'DeveloperName' to 'Id' for faster lookup
record_types_mapping = df_sf_recordTypes.set_index('DeveloperName')['Id'].to_dict()

In [26]:
# get SF Accounts
get_all_accounts = 'Select id, Name, RecordTypeId, Type, mbfc__Parish_Code__c, Job_Id__c, Archdpdx_Migration_Id__c from Account'

# get list of records, add to dataframe
sf_accounts = sf.query(get_all_accounts)
df_sf_accounts = pd.DataFrame(sf_accounts['records'])
df_sf_accounts = df_sf_accounts.drop(columns = 'attributes')
df_sf_accounts.shape

(2000, 7)

In [27]:
# get SF Contacts
get_all_contacts = 'Select id, Name, npe01__Type_of_Account__c, RecordTypeId, Archdpdx_Migration_Id__c, CreatedById from Contact'

# get list of records, add to dataframe
sf_contacts = sf.query(get_all_contacts)
df_sf_contacts = pd.DataFrame(sf_contacts['records'])
df_sf_contacts = df_sf_contacts.drop(columns = 'attributes')
df_sf_contacts.shape

(2000, 6)

# ACCOUNTS


## Extract


### Load ArchdPDX csvs as DataFrames

ADPDX data for organizations is held in 6 tables, all of which will be migrated into Salesforce's Accounts object.


In [28]:
df_offices = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Offices.csv', skiprows= lambda x: x in [1])
df_offices["src_table"] = 'Offices'
df_offices["AccountRecordType"] = 'Organization'
df_offices.rename({
    "Common Name": "Name",
    "Name": "Formal_Name__c"
    }, axis="columns", inplace=True)

df_offices

Record Number                                               Name  \
0               1                                    Pastoral Center   
1               3                                  Catholic Sentinel   
2               4                                Catholic Cemeteries   
3               6                                     Griffin Center   
4              11                 Providence Portland Medical Center   
5              12              Providence St. Vincent Medical Center   
6              14  National Sanctuary of Our Sorrowful Mother (Th...   
7              18           Southern Oregon VA Rehabilitation Center   
8              21                                      Clergy Office   
9              22                                          Vocations   
10             23                          Our Lady of Peace Retreat   
11             26                          St John Vianney Residence   
12             27                        Father Bernard Youth Center   
13             28            PeaceHealth Sacred Heart Medical Center   
14             32                                   Diaconate Office   
15             33     Department of Veterans’ Affairs Medical Center   
16             34                  Oregon Health Sciences University   
17             35                      Lane County Adult Corrections   
18             36             Shutter Creek Correctional Institution   
19             37             U.S. Veterans’ Administration Hospital   
20             38                   Mill Creek Correctional Facility   
21             39              Oregon State Correctional Institution   
22             40                          Oregon State Penitentiary   
23             41                   Santiam Correctional Institution   
24             42          Federal Correctional Institution Sheridan   
25             43                 Coffee Creek Correctional Facility   
26             44               MacLaren Youth Correctional Facility   
27             53                  Providence Medford Medical Center   
28             54                        Providence Seaside Hospital   
29             55                         USA West Province, Jesuits   
30             56        Providence Milwaukie Hospital Pastoral Care   
31             57    Providence Newberg Medical Center Pastoral Care   
32             58             Office of Marketing and Communications   
33             59                                 Catholic Charities   
34             60                           Bristol Hospice - Eugene   

                                       Formal_Name__c  \
0                                     Pastoral Center   
1                                   Catholic Sentinel   
2                                 Catholic Cemeteries   
3                                      Griffin Center   
4                  Providence Portland Medical Center   
5               Providence St. Vincent Medical Center   
6   National Sanctuary of Our Sorrowful Mother (Th...   
7            Southern Oregon VA Rehabilitation Center   
8                                       Clergy Office   
9                                           Vocations   
10                          Our Lady of Peace Retreat   
11                          St John Vianney Residence   
12                        Father Bernard Youth Center   
13            PeaceHealth Sacred Heart Medical Center   
14                                   Diaconate Office   
15     Department of Veterans’ Affairs Medical Center   
16                  Oregon Health Sciences University   
17                      Lane County Adult Corrections   
18             Shutter Creek Correctional Institution   
19             U.S. Veterans’ Administration Hospital   
20                   Mill Creek Correctional Facility   
21              Oregon State Correctional Institution   
22                          Oregon State Penitentiary   
23                   Santiam Correctional I

In [29]:
df_parishes = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Parishes (3).csv', dtype={'Vicariate': 'object', 'Established': 'str', 'Mission Of': 'str'}, skiprows= lambda x: x in [1])
df_parishes["src_table"] = 'Parishes'
df_parishes["AccountRecordType"] = 'Church'
# df_parishes.rename({"Parish Formal Name": "Account Name"}, axis="columns", inplace=True)
df_parishes.rename({
                    "Parish Formal Name": "Formal_Name__c",
                    "Common Name": "Name",
                    'Mission Of': 'Parent_Parish'
                }, axis="columns", inplace=True)

df_parishes

Record Number                                           Name  \
0                1  Our Lady of Perpetual Help, St Mary’s, Albany   
1                2             St. Andrew Dũng-Lạc Mission, Aloha   
2                3                 St. Elizabeth Ann Seton, Aloha   
3                4     St. Peter the Fisherman Mission, Arch Cape   
4                5              Our Lady of the Mountain, Ashland   
..             ...                                            ...   
146            152         St. John in the Woods Mission, Welches   
147            153                         St. Cyril, Wilsonville   
148            154                             St. Luke, Woodburn   
149            155               St. John the Evangelist, Yamhill   
150            173          St. Thomas More Newman Center, Eugene   

                                      Sort Name Parish Name  \
0    our lady of perpetual help st marys albany         NaN   
1                       st andrew dunglac aloha         NaN   
2                  st elizabeth ann seton aloha         NaN   
3              st peter the fisherman arch cape         NaN   
4              our lady of the mountain ashland         NaN   
..                                          ...         ...   
146                st john in the woods welches         NaN   
147                        st cyril wilsonville         NaN   
148                            st luke woodburn         NaN   
149              st john the evangelist yamhill         NaN   
150         st thomas more newman center eugene         NaN   

                            Formal_Name__c  Parish City  \
0    Our Lady of Perpetual Help, St Mary’s       Albany   
1                      St. Andrew Dũng-Lạc        Aloha   
2                  St. Elizabeth Ann Seton        Aloha   
3                  St. Peter the Fisherman    Arch Cape   
4                 Our Lady of the Mountain      Ashland   
..                                     ...          ...   
146                  St. John in the Woods      Welches   
147                              St. Cyril  Wilsonville   
148                               St. Luke     Woodburn   
149                St. John the Evangelist      Yamhill   
150          St. Thomas More Newman Center       Eugene   

    Archdiocese Assigns Clergy Parent_Parish Established Vicariate  ...  \
0                          Yes             0        1885         1  ...   
1                           No            83           0        13  ...   
2                          Yes             0        1982        16  ...   
3                          Yes           131           0         9  ...   
4                          Yes             0        1887        15  ...   
..                         ...           ...         ...       ...  ...   
146                        Yes           127           0         5  ...   
147                        Yes             0        1926        17  ...   
148                        Yes             0        1899         6  ...   
149                        Yes             0        1910        18  ...   
150                         No             0        1967         7  ...   

         Schedule 4 Head                                    Schedule 4 Text  \
0              Adoration  Wednesday 6:00 pm – 7:00 pm in the Church<br>D...   
1                    NaN                                                NaN   
2    Adoration/Adoración  Sunday 11:00 am–3:00 pm (chapel)<br>Monday–Wed...   
3                    NaN                                                NaN   
4              Adoration  First Friday 9:00 am–6:00 pm<br>or 24 hours pe...   
..                   ...                                                ...   
146                  NaN                                                NaN   
147            Adoration            Thursday 12:30 pm–1:00 pm, 6:00–6:30 pm   
148                  NaN                                                NaN   
149            Ador

In [30]:
df_religious = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/RelCommunities.csv', skiprows= lambda x: x in [1])
df_religious["src_table"] = 'RelCommunities'
df_religious["AccountRecordType"] = 'Religious'
df_religious.rename({
                    "Community Name": "Formal_Name__c",
                    "Common Name": "Name"
                     }, axis="columns", inplace=True)

df_religious.sample(10)

Record Number                                               Name  \
20             30          Adrian Dominican Sisters, Adrian, MI (OP)   
32             42  Sisters of Charity of the Blessed Virgin Mary,...   
34             44  Sisters of the Holy Names of Jesus and Mary, M...   
31             41  Sisters For Christian Community, Hillsboro (SFCC)   
9              13  Canisius Jesuit Community at Jesuit High Schoo...   
39             49               Sisters of Reparation, Portland (SR)   
19             29          Adorers of the Holy Cross, Portland (MTG)   
10             14  Félix Rougier House of Studies, Mount Angel (M...   
12             17      Carmelite House of Studies, Mount Angel (OCD)   
36             46        Sisters of Mary of Kakamega, Portland (SMK)   

                                     Formal_Name__c Community City  \
20                         Adrian Dominican Sisters     Adrian, MI   
32    Sisters of Charity of the Blessed Virgin Mary       Portland   
34      Sisters of the Holy Names of Jesus and Mary     Marylhurst   
31                  Sisters For Christian Community      Hillsboro   
9   Canisius Jesuit Community at Jesuit High School      Beaverton   
39                            Sisters of Reparation       Portland   
19                        Adorers of the Holy Cross       Portland   
10                   Félix Rougier House of Studies    Mount Angel   
12                       Carmelite House of Studies    Mount Angel   
36                      Sisters of Mary of Kakamega       Portland   

   Archdiocese Assigns Clergy  \
20                         No   
32                         No   
34                         No   
31                         No   
9                          No   
39                         No   
19                         No   
10                         No   
12                         No   
36                         No   

                                      Order Full Name  \
20                        Dominican Sisters of Adrian   
32      Sisters of Charity of the Blessed Virgin Mary   
34  Sisters of the Holy Names of Jesus and Mary U....   
31                    Sisters For Christian Community   
9                                       Societas Iesu   
39  Sisters of Reparation of the Sacred Wounds of ...   
19                          Adorers of the Holy Cross   
10                      Misioneros del Espíritu Santo   
12                   Ordo Carmelitarum Discalceatorum   
36                        Sisters of Mary of Kakamega   

                                Order Common Name Order Letters Men or Women  \
20                                     Dominicans            OP        Women   
32  Sisters of Charity of the Blessed Virgin Mary           BVM        Women   
34                             Holy Names Sisters          SNJM        Women   
31                Sisters For Christian Community          SFCC        Women   
9                                         Jesuits            SJ          Men   
39                          Sisters of Reparation            SR        Women   
19                      Adorers of the Holy Cross           MTG        Women   
10                Missionaries of the Holy Spirit          MSpS          Men   
12                     Discalced Carmelite Friars           OCD          Men   
36                    Sisters of Mary of Kakamega           SMK        Women   

   Non-Latin Rite  ... Religious Order Secular Order Diocesan Order  \
20             No  ...              No            No             No   
32             No  ...             Yes           NaN            NaN   
34             No  ...             Yes            No             No   
31             No  ...             NaN           NaN            NaN   
9              No  ...             NaN           NaN            NaN   
39             No  ...             Yes            No            Yes   
19             No  ...             NaN           NaN            NaN   

In [31]:
df_schools = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Schools.csv', skiprows= lambda x: x in [1])
df_schools["src_table"] = 'Schools'
df_schools["AccountRecordType"] = 'Organization'
df_schools.rename({
                    "School Name": "Formal_Name__c",
                    "Common Name": "Name",
                    'Parish Link': 'Parent_Parish'
                    
                    }, axis="columns", inplace=True)

df_schools.sample(10)

Record Number                                              Name  \
46             49                        St. Clare School, Portland   
12             15  La Salle Catholic College Preparatory, Milwaukie   
20             23             Sacred Heart Catholic School, Gervais   
11             14                     Jesuit High School, Beaverton   
29             32                       All Saints School, Portland   
54             57                 Mount Angel Seminary, Mount Angel   
7              10            Valley Catholic High School, Beaverton   
39             42         St. Thomas More Catholic School, Portland   
50             53      Franciscan Montessori Earth School, Portland   
40             43             St. Therese Catholic School, Portland   

                           Formal_Name__c  School City  \
46                       St. Clare School     Portland   
12  La Salle Catholic College Preparatory    Milwaukie   
20           Sacred Heart Catholic School      Gervais   
11                     Jesuit High School    Beaverton   
29                      All Saints School     Portland   
54                   Mount Angel Seminary  Mount Angel   
7             Valley Catholic High School    Beaverton   
39        St. Thomas More Catholic School     Portland   
50     Franciscan Montessori Earth School     Portland   
40            St. Therese Catholic School     Portland   

   Archdiocese Assigns Clergy  Parent_Parish  Vicariate Link  \
46                        Yes             93               0   
12                         No              0               0   
20                        Yes             38               0   
11                         No              0               0   
29                        Yes             75               0   
54                         No              0               0   
7                          No              0               0   
39                        Yes            114               0   
50                         No              0               0   
40                        Yes            113               0   

   Archdiocesan School Code Grades Provided  Established  ...  \
46               12-PDXCLAS             K-8       1914.0  ...   
12               12-MILLASS            9-12          NaN  ...   
20               12-GERSACS            PK-8          NaN  ...   
11               12-PDXJESS            9-12          NaN  ...   
29               12-PDXALLS            PK-8       1936.0  ...   
54                      NaN             NaN       1889.0  ...   
7                12-BEAVALH            9-12          NaN  ...   
39               12-PDXTHOS             K-8       1948.0  ...   
50               12-PDXFMES        Ungraded       1977.0  ...   
40               12-PDXTHES            PS-8          NaN  ...   

   Mailing Address Zip Mailing Address Country         Phone           Fax  \
46               97219                     NaN  503-244-7600  503-293-2076   
12               97222                     NaN  503-659-4155  503-659-2535   
20               97026                     NaN  503-792-4541  503-792-3826   
11               97225                     NaN  503-292-2663  503-291-5464   
29               97232                     NaN  503-236-6205  503-236-0781   
54               97373                     NaN  503-845-3951  503-845-3128   
7                97078                     NaN  503-644-3745  503-646-4054   
39               97221                     NaN  503-222-6105  503-227-5661   
50               97236                     NaN  503-760-8220  800-967-1502   
40               97230                     NaN  503-253-9400  503-253-9571   

                             Email                                   Web Site  \
46             info@stclarepdx.org                https://www.stclarepdx.org/   
12                 info@lsprep.org                    https://www.lsprep.org/   
20          shssecretary@shstl.org                  https://

In [32]:
df_vicariates = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Vicariates.csv', skiprows= lambda x: x in [1])
df_vicariates["src_table"] = 'Vicariates'
df_vicariates["AccountRecordType"] = 'Deanery'
# As we want to designate the Common Name as what will be the Account Name in Salesforce, we are renaming these columns in a different pattern than prior CSVs.
df_vicariates.rename({"Common Name": "Name"}, axis="columns", inplace=True)

df_vicariates.sample(10)

Record Number                                Name  \
6               7       Metropolitan Eugene Vicariate   
12             13  South Portland, Suburban Vicariate   
10             11                   Santiam Vicariate   
5               6             Marion County Vicariate   
15             16           Tualatin Valley Vicariate   
13             14        Southeast Portland Vicariate   
2               3           Columbia County Vicariate   
4               5   East Portland, Suburban Vicariate   
11             12               South Coast Vicariate   
8               9               North Coast Vicariate   

              Vicariate Name Archdiocese Assigns Clergy   src_table  \
6        Metropolitan Eugene                        Yes  Vicariates   
12  South Portland, Suburban                        Yes  Vicariates   
10                   Santiam                        Yes  Vicariates   
5              Marion County                        Yes  Vicariates   
15           Tualatin Valley                        Yes  Vicariates   
13        Southeast Portland                        Yes  Vicariates   
2            Columbia County                        Yes  Vicariates   
4    East Portland, Suburban                        Yes  Vicariates   
11               South Coast                        Yes  Vicariates   
8                North Coast                        Yes  Vicariates   

   AccountRecordType  
6            Deanery  
12           Deanery  
10           Deanery  
5            Deanery  
15           Deanery  
13           Deanery  
2            Deanery  
4            Deanery  
11           Deanery  
8            Deanery

In [33]:
df_newman = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/NewmanCenters.csv', skiprows= lambda x: x in [1])
df_newman["src_table"] = 'NewmanCenters'
df_newman["AccountRecordType"] = 'Organization'
df_newman.rename({
                    "Newman Center Name": "Formal_Name__c",
                    "Common Name": "Name",
                    "Newman Center City": "Mailing Address City2"
                  }, axis="columns", inplace=True)

df_newman

Record Number                                               Name  \
0              1                       OSU Newman Center, Corvallis   
1              2         St. Thomas More (UO) Newman Center, Eugene   
2              3  Walsh Memorial (SOU) Newman Center at Our Lady...   
3              4                  PDX (PSU) Newman Center, Portland   

                                      Formal_Name__c Mailing Address City2  \
0                                  OSU Newman Center             Corvallis   
1                 St. Thomas More (UO) Newman Center                Eugene   
2  Walsh Memorial (SOU) Newman Center at Our Lady...               Ashland   
3                            PDX (PSU) Newman Center              Portland   

  Archdiocese Assigns Clergy  Established  Locator Description  \
0                         No            0                  NaN   
1                         No         1915                  NaN   
2                        Yes            0                  NaN   
3                         No            0                  NaN   

      Mailing Address  Mailing Address 2 Mailing Address City  ...  \
0  2127 NW Monroe Ave                NaN            Corvallis  ...   
1     1850 Emerald St                NaN               Eugene  ...   
2     987 Hillview Dr                NaN              Ashland  ...   
3      424 SW Mill St                NaN             Portland  ...   

  Schedule 4 Head  Schedule 4 Text  Schedule 5 Head  Schedule 5 Text  \
0             NaN              NaN              NaN              NaN   
1             NaN              NaN              NaN              NaN   
2             NaN              NaN              NaN              NaN   
3             NaN              NaN              NaN              NaN   

  Schedule 6 Head Schedule 6 Text Schedule 7 Head Schedule 7 Text  \
0             NaN             NaN             NaN             NaN   
1             NaN             NaN             NaN             NaN   
2             NaN             NaN             NaN             NaN   
3             NaN             NaN             NaN             NaN   

       src_table AccountRecordType  
0  NewmanCenters      Organization  
1  NewmanCenters      Organization  
2  NewmanCenters      Organization  
3  NewmanCenters      Organization  

[4 rows x 37 columns]

Each of the 6 tables has an overlapping but distinct set of columns, making it challenging to conform these tables into a single staging table.

In addition, columns that correspond to the same field in salesforce are named differently in each table (eg. 'Parish City' vs. 'Religious City' vs. 'Newman Center City')


In [34]:
print('TABLE: (ROWS, COLUMNS)\n')

print(f'Offices:    {df_offices.shape}')
print(f'Parishes:   {df_parishes.shape}')
print(f'Religious:  {df_religious.shape}')
print(f'Schools:    {df_schools.shape}')
print(f'Vicariates: {df_vicariates.shape}')
print(f'Newman Ctr: {df_newman.shape}')

TABLE: (ROWS, COLUMNS)

Offices:    (35, 18)
Parishes:   (151, 45)
Religious:  (70, 34)
Schools:    (56, 26)
Vicariates: (18, 6)
Newman Ctr: (4, 37)


### Merge DFs into a single Accounts DF

This step takes 6 different tables and combines them into a single Accounts table for cleaning and staging.


In [35]:
# init list of DataFrames
src_accounts = [df_offices, df_parishes, df_religious, df_schools, df_vicariates, df_newman]

# concats the various Account dataframes into one large table
accounts = pd.concat(src_accounts, ignore_index=True)

## Transform


Time to do some table column renaming and re-organizing!


In [36]:
# renames columns headers to consolidate account names into SF-conformed data model
accounts.rename({"Common Name": "Name, City"}, axis="columns", inplace=True)

accounts.rename(
    columns={
        # 'Account Name': 'Name',
        'Mailing Address': 'BillingStreet1',
        'Mailing Address 2': 'BillingStreet2',
        'Mailing Address City': 'BillingCity',
        'Mailing Address State': 'BillingState',
        'Mailing Address Postal Code': 'BillingPostalCode',
        'Mailing Address Country': 'BillingCountry',
        'Email': 'mbfc__Email__c',
        'Web Site': 'Website',
        'Order Common Name': 'mbfc__Abbreviation__c',
        'Order Letters': 'mbfc__Religious_Suffix__c',
        'Men or Women': 'mbfc__Type_Members__c',
        'Archdiocese Assigns Clergy': 'Archdiocese_Assigns_Clergy__c',
        'Locator Description': 'Locator_Description__c',
        'Established': 'mbfc__Date_Established__c',
        'County': 'County__c',
        'Disabled Access': 'Disabled_Access__c',
        'Sanctuary Capacity': 'Sanctuary_Capacity__c',
        'Miles to Pastoral Centre': 'Miles_to_Pastoral_Centre__c',
        'Archdiocesan School Code': 'Archdiocesan_School_Code__c',
        'Grades Provided': 'Grades_Provided__c'
    },
    inplace=True
)


# reorder column order
col = accounts.pop('Name')
accounts.insert(2, col.name, col)

col = accounts.pop('Parish Name')
accounts.insert(3, col.name, col)

col = accounts.pop('AccountRecordType')
accounts.insert(1, col.name, col)



In [37]:
accounts.columns

Index(['Record Number', 'AccountRecordType', 'Formal_Name__c', 'Name',
       'Parish Name', 'Archdiocese_Assigns_Clergy__c',
       'Locator_Description__c', 'BillingStreet1', 'BillingStreet2',
       'BillingCity', 'BillingState', 'Mailing Address Province',
       'BillingPostalCode', 'BillingCountry', 'Phone', 'Fax', 'mbfc__Email__c',
       'Website', 'src_table', 'Sort Name', 'Parish City', 'Parent_Parish',
       'mbfc__Date_Established__c', 'Vicariate', 'Non-Latin', 'County__c',
       'Disabled_Access__c', 'Sanctuary_Capacity__c',
       'Lat/Long Coordinates Decimal', 'Google Small Embed URL',
       'Miles to Pastoral Center', 'Schedule 1 Head', 'Schedule 1 Text',
       'Schedule 2 Head', 'Schedule 2 Text', 'Schedule 3 Head',
       'Schedule 3 Text', 'Schedule 4 Head', 'Schedule 4 Text',
       'Schedule 5 Head', 'Schedule 5 Text', 'Schedule 6 Head',
       'Schedule 6 Text', 'Schedule 7 Head', 'Schedule 7 Text',
       'Community City', 'Order Full Name', 'mbfc__Abbreviat

In [38]:
accounts[accounts.BillingStreet2.isna() == False]

Record Number AccountRecordType                          Formal_Name__c  \
14              32      Organization                        Diaconate Office   
32              58      Organization  Office of Marketing and Communications   
35               1            Church   Our Lady of Perpetual Help, St Mary’s   
36               2            Church                     St. Andrew Dũng-Lạc   
37               3            Church                 St. Elizabeth Ann Seton   
..             ...               ...                                     ...   
236             62         Religious           Work of Jesus the High Priest   
238             64         Religious                Heralds of the Good News   
239             65         Religious   Missionary Oblates of Mary Immaculate   
247             73         Religious                  Brothers of Saint John   
248             74         Religious                         Society of Mary   

                                                  Name Parish Name  \
14                                    Diaconate Office         NaN   
32              Office of Marketing and Communications         NaN   
35       Our Lady of Perpetual Help, St Mary’s, Albany         NaN   
36                  St. Andrew Dũng-Lạc Mission, Aloha         NaN   
37                      St. Elizabeth Ann Seton, Aloha         NaN   
..                                                 ...         ...   
236      Work of Jesus the High Priest, Gresham (OJSS)         NaN   
238           Heralds of the Good News, Portland (HGN)         NaN   
239  Missionary Oblates of Mary Immaculate, Rome, I...         NaN   
247           Brothers of Saint John, Laredo, TX (CSJ)         NaN   
248               Society of Mary, Washington, DC (SM)         NaN   

    Archdiocese_Assigns_Clergy__c  \
14                            Yes   
32                            Yes   
35                            Yes   
36                             No   
37                            Yes   
..                            ...   
236                            No   
238                            No   
239                            No   
247                            No   
248                            No   

                          Locator_Description__c  \
14                                           NaN   
32                                           NaN   
35   SW Ellsworth St between 8th and 9th Streets   
36    SW Grabhorn Rd/209th Ave and Farmington Rd   
37                                           NaN   
..                                           ...   
236                                          NaN   
238                                          NaN   
239                                          NaN   
247                                          NaN   
248                                          NaN   

                                   BillingStreet1        BillingStreet2  \
14                                Pastoral Center    2838 E Burnside St   
32                                Pastoral Center    2838 E Burnside St   
35   Our Lady of Perpetual Help, St Mary’s Parish  815 Broadalbin St SW   
36                    St. Andrew Dũng-Lạc Mission   7390 SW Grabhorn Rd   
37                 St. Elizabeth Ann Seton Parish     3145 SW 192nd Ave   
..                                            ...                   ...   
236                                OJSS Community         451 NW 1st St   
238                                c/o Chancellor    2838 E Burnside St   
239         Missionary Oblates of Mary Immaculate       Via Aurelia 290   
247                               St. John Priory      505 Century Dr S   
248                 Society of Mary, USA Province      815 Varnum St NE   

    BillingCity  ... Major Superior Phone  Major Superior Email School City  \
14     Portland  ...                  NaN                   NaN         NaN   
32     Portland  ...                  NaN                   NaN         Na

In [39]:
# merge two Non-Latin columns into one 
accounts['Non_Latin__c'] = accounts['Non-Latin'].combine_first(accounts['Non-Latin Rite']) 

# Rename the 'Non_Latin__c' field to 'mbfc__Non_Latin__c'
accounts.rename(columns={'Non_Latin__c': 'mbfc__Non_Latin__c'}, inplace=True)


In [40]:
# export merged tables DESCRIPTION to CSV for mapping
accounts.describe(include='all').transpose().to_csv(f'/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/working/accounts.csv')
accounts.describe(include='all').transpose()

count unique                  top freq          mean  \
Record Number          334.0    NaN                  NaN  NaN          54.5   
AccountRecordType        334      4               Church  151           NaN   
Formal_Name__c           316    273             St. Mary    5           NaN   
Name                     334    334      Pastoral Center    1           NaN   
Parish Name                5      5             St. Anne    1           NaN   
...                      ...    ...                  ...  ...           ...   
Mailing Address 1         56     55  4420 SW St Marys Dr    2           NaN   
Mailing Address Zip     56.0    NaN                  NaN  NaN  97222.446429   
Vicariate Name            18     18     Albany-Corvallis    1           NaN   
Mailing Address City2      4      4            Corvallis    1           NaN   
mbfc__Non_Latin__c       221      2                   No  217           NaN   

                             std      min       25%      50%      75%      max  
Record Number          41.389801      1.0     21.25     45.0    76.75    173.0  
AccountRecordType            NaN      NaN       NaN      NaN      NaN      NaN  
Formal_Name__c               NaN      NaN       NaN      NaN      NaN      NaN  
Name                         NaN      NaN       NaN      NaN      NaN      NaN  
Parish Name                  NaN      NaN       NaN      NaN      NaN      NaN  
...                          ...      ...       ...      ...      ...      ...  
Mailing Address 1            NaN      NaN       NaN      NaN      NaN      NaN  
Mailing Address Zip     124.9586  97005.0  97134.75  97217.5  97301.0  97526.0  
Vicariate Name               NaN      NaN       NaN      NaN      NaN      NaN  
Mailing Address City2        NaN      NaN       NaN      NaN      NaN      NaN  
mbfc__Non_Latin__c           NaN      NaN       NaN      NaN      NaN      NaN  

[70 rows x 11 columns]

In [41]:
# Create a single BillingAddress field

# Concatenate the two columns with CHAR(10) as separator
accounts['BillingStreet'] = accounts[['BillingStreet1', 'BillingStreet2']].apply(lambda x: '\n'.join(x.dropna()), axis=1)

# Drop the original columns
accounts.drop(columns=['BillingStreet1', 'BillingStreet2'], inplace=True)

In [42]:
# Handle boolean fields

boolean_columns_to_convert = [
    'Archdiocese_Assigns_Clergy__c', 
    'mbfc__Non_Latin__c', 
    'Disabled_Access__c', 
    ]

# Convert 'Yes'/'No' to True/False
accounts[boolean_columns_to_convert] = accounts[boolean_columns_to_convert].replace({'Yes': True, 'No': False, None: False})



In [43]:
accounts[boolean_columns_to_convert].sample(10)

Archdiocese_Assigns_Clergy__c  mbfc__Non_Latin__c  Disabled_Access__c
327                           True               False               False
90                            True               False                True
273                           True               False               False
106                           True               False                True
1                            False               False               False
306                          False               False               False
234                          False               False               False
179                           True               False                True
292                           True               False               False
232                          False                True               False

In [44]:
# Religious Order fields > conform to new data model

# Apply logic to create new columns
accounts['Religious_Secular_Order__c'] = accounts.apply(
    lambda x: 'Religious Order' if x['Religious Order'] == 'Yes' else ('Secular Order' if x['Secular Order'] == 'Yes' else None), axis=1
)

accounts['Pontifical_or_Diocesan_Order__c'] = accounts.apply(
    lambda x: 'Diocesan Order' if x['Diocesan Order'] == 'Yes' else ('Pontifical Order' if x['Pontifical Order'] == 'Yes' else None), axis=1
)

accounts.drop(columns=['Religious Order', 'Secular Order', 'Diocesan Order', 'Pontifical Order'], inplace=True)

In [45]:
print(accounts['mbfc__Date_Established__c'].dtype)

object


In [46]:
# Handle Date fields that are only YYYY

# Ensure all values in 'mbfc__Date_Established__c' are strings
accounts['mbfc__Date_Established__c'] = accounts['mbfc__Date_Established__c'].astype(str)

# Define a function to transform valid year values
def transform_year(year):
    if pd.notna(year) and year.replace('.', '', 1).isdigit() and len(year.split('.')[0]) == 4:
        return pd.to_datetime(year.split('.')[0] + '-01-01')
    else:
        return pd.NaT

# Apply the function to the 'mbfc__Date_Established__c' column
accounts['mbfc__Date_Established__c'] = accounts['mbfc__Date_Established__c'].apply(transform_year)


In [47]:
accounts['mbfc__Date_Established__c'].sample(10)

232          NaT
109   1906-01-01
193          NaT
39    1887-01-01
51    1888-01-01
202          NaT
318          NaT
181          NaT
27           NaT
245          NaT
Name: mbfc__Date_Established__c, dtype: datetime64[ns]

In [48]:
accounts[accounts.src_table == 'Schools'].Parent_Parish

256    109
257     11
258    101
259    121
260      9
261      0
262      0
263      0
264      0
265      0
266      0
267      0
268      0
269      0
270      0
271      0
272      0
273      0
274     33
275    149
276     38
277     42
278     46
279     54
280     58
281     59
282     61
283     62
284     73
285     75
286     77
287    154
288    145
289    135
290    126
291    125
292    124
293    123
294    102
295    114
296    113
297    107
298     78
299     79
300     87
301      0
302     93
303     96
304     98
305      0
306      0
307      0
308      0
309      0
310      0
311    147
Name: Parent_Parish, dtype: object

In [49]:
# Format Parent_Parish field

# Remove instances of '0'
accounts.Parent_Parish = accounts.Parent_Parish.apply(lambda x: '' if x == 0 else x)


In [50]:
# Append prefix
accounts['Parent_Parish'] = accounts['Parent_Parish'].apply(lambda x: 'Parishes_' + str(x) if pd.notna(x) and x != '' else x)

In [51]:
# Check final results, in particular the 'Schools' records
accounts.Parent_Parish[(accounts.Parent_Parish.isna() == False) & (accounts["src_table"] == "Schools")].sample(10)

300     Parishes_87
272                
269                
285     Parishes_75
279     Parishes_54
289    Parishes_135
265                
256    Parishes_109
278     Parishes_46
262                
Name: Parent_Parish, dtype: object

In [52]:
# Replace Parent_Parish unique ids with SF records
add_salesforce_record_ids(sf, accounts, "Parent_Parish", "Account", "Archdpdx_Migration_Id__c", "Parent_Parish__c", 10 )

Record Number AccountRecordType  \
0                1      Organization   
1                3      Organization   
2                4      Organization   
3                6      Organization   
4               11      Organization   
..             ...               ...   
329             18           Deanery   
330              1      Organization   
331              2      Organization   
332              3      Organization   
333              4      Organization   

                                        Formal_Name__c  \
0                                      Pastoral Center   
1                                    Catholic Sentinel   
2                                  Catholic Cemeteries   
3                                       Griffin Center   
4                   Providence Portland Medical Center   
..                                                 ...   
329                                                NaN   
330                                  OSU Newman Center   
331                 St. Thomas More (UO) Newman Center   
332  Walsh Memorial (SOU) Newman Center at Our Lady...   
333                            PDX (PSU) Newman Center   

                                                  Name Parish Name  \
0                                      Pastoral Center         NaN   
1                                    Catholic Sentinel         NaN   
2                                  Catholic Cemeteries         NaN   
3                                       Griffin Center         NaN   
4                   Providence Portland Medical Center         NaN   
..                                                 ...         ...   
329                           Yamhill County Vicariate         NaN   
330                       OSU Newman Center, Corvallis         NaN   
331         St. Thomas More (UO) Newman Center, Eugene         NaN   
332  Walsh Memorial (SOU) Newman Center at Our Lady...         NaN   
333                  PDX (PSU) Newman Center, Portland         NaN   

     Archdiocese_Assigns_Clergy__c Locator_Description__c BillingCity  \
0                             True                    NaN    Portland   
1                            False                    NaN    Portland   
2                            False                    NaN    Portland   
3                            False                    NaN   Milwaukie   
4                             True                    NaN    Portland   
..                             ...                    ...         ...   
329                           True                    NaN         NaN   
330                          False                    NaN   Corvallis   
331                          False                    NaN      Eugene   
332                           True                    NaN     Ashland   
333                          False                    NaN    Portland   

    BillingState  Mailing Address Province  ... Grades_Provided__c  \
0             OR                       NaN  ...                NaN   
1             OR                       NaN  ...                NaN   
2             OR                       NaN  ...                NaN   
3             OR                       NaN  ...                NaN   
4             OR                       NaN  ...                NaN   
..           ...                       ...  ...                ...   
329          NaN                       NaN  ...                NaN   
330           OR                       NaN  ...                NaN   
331           OR                       NaN  ...                NaN   
332           OR                       NaN  ...                NaN   
333           OR                       NaN  ...                NaN   

    Mailing Address 1 Mailing Address Zip  Vicariate Name  \
0                 NaN                 NaN             NaN   
1                 NaN                 NaN             NaN   
2                 NaN                 NaN             NaN   
3                 NaN   

In [53]:
# ParentID field

accounts['ParentId'] = accounts['Parent_Parish__c']

# Verify results
accounts[accounts.Parent_Parish__c.isna() == False]


Record Number AccountRecordType  \
36               2            Church   
38               4            Church   
45              13            Church   
47              15            Church   
49              17            Church   
50              18            Church   
56              25            Church   
58              27            Church   
59              28            Church   
69              39            Church   
70              40            Church   
75              45            Church   
77              47            Church   
79              49            Church   
80              50            Church   
87              57            Church   
90              60            Church   
97              67            Church   
104             74            Church   
148            119            Church   
159            130            Church   
165            136            Church   
181            152            Church   
256              1      Organization   
257              2      Organization   
258              3      Organization   
259              5      Organization   
260              6      Organization   
274             21      Organization   
275             22      Organization   
276             23      Organization   
277             24      Organization   
278             25      Organization   
279             26      Organization   
280             27      Organization   
281             28      Organization   
282             29      Organization   
283             30      Organization   
284             31      Organization   
285             32      Organization   
286             33      Organization   
287             34      Organization   
288             35      Organization   
289             36      Organization   
290             37      Organization   
291             38      Organization   
292             39      Organization   
293             40      Organization   
294             41      Organization   
295             42      Organization   
296             43      Organization   
297             44      Organization   
298             45      Organization   
299             46      Organization   
300             47      Organization   
302             49      Organization   
303             50      Organization   
304             51      Organization   
311             58      Organization   

                                        Formal_Name__c  \
36                                 St. Andrew Dũng-Lạc   
38                             St. Peter the Fisherman   
45                                        Holy Trinity   
47                           St. Patrick of the Forest   
49                                St. John the Baptist   
50                                          St. Joseph   
56                                   St. Philip Benizi   
58                                St. Martin de Porres   
59                                           St. Henry   
69                                         Holy Family   
70                                St. Charles Borromeo   
75                                St. Francis de Sales   
77                                           St. Agnes   
79                                          St. Joseph   
80                                          St. Thomas   
87                                         St. Patrick   
90                              St. Catherine of Siena   
97                                Sts. Ann and Michael   
104                               St. John the Baptist   
148                              Our Lady of the River   
159                                        Holy Rosary   
165                              Our Lady of Guadalupe   
181                              St. John in the Woods   
256                                    St. Rose School   
257                                 St. Cecilia School   
258                                   Cathedral School   
259                       St. Francis 

### AccountRecordType & ChurchType


In [54]:
#Sets all rows where AccountRecordType is Church as a Parish.
accounts.loc[accounts['AccountRecordType'] == 'Church', 'mbfc__Church_Type__c'] = 'Parish'
accounts[accounts['AccountRecordType'] == 'Church'].head(5)


Record Number AccountRecordType                         Formal_Name__c  \
35              1            Church  Our Lady of Perpetual Help, St Mary’s   
36              2            Church                    St. Andrew Dũng-Lạc   
37              3            Church                St. Elizabeth Ann Seton   
38              4            Church                St. Peter the Fisherman   
39              5            Church               Our Lady of the Mountain   

                                             Name Parish Name  \
35  Our Lady of Perpetual Help, St Mary’s, Albany         NaN   
36             St. Andrew Dũng-Lạc Mission, Aloha         NaN   
37                 St. Elizabeth Ann Seton, Aloha         NaN   
38     St. Peter the Fisherman Mission, Arch Cape         NaN   
39              Our Lady of the Mountain, Ashland         NaN   

    Archdiocese_Assigns_Clergy__c  \
35                           True   
36                          False   
37                           True   
38                           True   
39                           True   

                         Locator_Description__c BillingCity BillingState  \
35  SW Ellsworth St between 8th and 9th Streets      Albany           OR   
36   SW Grabhorn Rd/209th Ave and Farmington Rd       Aloha           OR   
37                                          NaN       Aloha           OR   
38                              79441 Hwy 101 S     Seaside           OR   
39                                          NaN     Ashland           OR   

    Mailing Address Province  ... Mailing Address Zip Vicariate Name  \
35                       NaN  ...                 NaN            NaN   
36                       NaN  ...                 NaN            NaN   
37                       NaN  ...                 NaN            NaN   
38                       NaN  ...                 NaN            NaN   
39                       NaN  ...                 NaN            NaN   

   Mailing Address City2 mbfc__Non_Latin__c  \
35                   NaN              False   
36                   NaN              False   
37                   NaN              False   
38                   NaN              False   
39                   NaN              False   

                                        BillingStreet  \
35  Our Lady of Perpetual Help, St Mary’s Parish\n...   
36   St. Andrew Dũng-Lạc Mission\n7390 SW Grabhorn Rd   
37  St. Elizabeth Ann Seton Parish\n3145 SW 192nd Ave   
38         St. Peter the Fisherman Mission\nPO Box 29   
39   Our Lady of the Mountain Parish\n987 Hillview Dr   

   Religious_Secular_Order__c Pontifical_or_Diocesan_Order__c  \
35                       None                            None   
36                       None                            None   
37                       None                            None   
38                       None                            None   
39                       None                            None   

      Parent_Parish__c            ParentId mbfc__Church_Type__c  
35                 NaN                 NaN               Parish  
36  001Dx00001HwDzoIAF  001Dx00001HwDzoIAF               Parish  
37                 NaN                 NaN               Parish  
38  001Dx00001HwE0XIAV  001Dx00001HwE0XIAV               Parish  
39                 NaN                 NaN               Parish  

[5 rows x 70 columns]

In [55]:
# Update 'mbfc__organization_type__c' field for rows where the source table is 'Schools'
accounts.loc[accounts['src_table'] == 'Schools', 'mbfc__Organization_Type__c'] = 'School'

### Generate ExternalId


In [56]:
# Generate an External ID
columns_to_concate = ['src_table', 'Record Number']
accounts = concat_columns(accounts, columns_to_concate, 'Archdpdx_Migration_Id__c', separator='_')

In [57]:
# set Deanery RecordTypeId to the Church RecordTypeId
# map in RecordTypeIds
accounts['RecordTypeId'] = accounts['AccountRecordType'].map(record_types_mapping)
record_types_mapping

{'Church': '012Dx0000003p4xIAA',
 'Deanery': '012Dx0000003p4yIAA',
 'Group': '012Dx0000003p4zIAA',
 'Organization': '012Dx0000003p50IAA',
 'Property': '012Dx0000003p51IAA',
 'Religious': '012Dx0000003p5KIAQ',
 'All_Types': '012Dx0000003p53IAA',
 'Any': '012Dx0000003p54IAA',
 'Assignments_Clergy': '012Dx0000003p55IAA',
 'Chancery_Users': '012Dx0000003p56IAA',
 'Clergy_Religious_Residence': '012Dx0000003p57IAA',
 'Diocean_Users': '012Dx0000003p58IAA',
 'Diocesan_Appointment': '012Dx0000003p59IAA',
 'Ecclesial_Affiliation': '012Dx0000003p5AIAQ',
 'Education': '012Dx0000003p5BIAQ',
 'Lay_Person': '012Dx0000003p5HIAQ',
 'Ministerial_Status': '012Dx0000003p5DIAQ',
 'Parish_Affiliations': '012Dx0000003p5EIAQ',
 'Staff': '012Dx0000003p5FIAQ',
 'Consecrated': '012Dx0000003p5GIAQ',
 'Permanent_Deacon': '012Dx0000003p5IIAQ',
 'Priest': '012Dx0000003p5JIAQ',
 'MajorGift': '012Hu000001pkqBIAQ',
 'Grant': '012Hu000001pkqCIAQ',
 'HH_Account': '012Hu000001pkqDIAQ',
 'Donation': '012Hu000001pkqFIAQ',
 

## Load


### Generate a new Job ID


In [58]:
# increment to the job_id
file_name = '/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/jobs/job_id'
curr_job_id = update_job_id(file_name)
print(f"New job ID: {curr_job_id}")

# add/update account DF with job_id
accounts["Job_Id__c"] = curr_job_id


New job ID: 138


### A) Vicariates


In [59]:
# Get Account Group RecordTypeID
deanery_recordTypeId = df_sf_recordTypes.loc[
    (df_sf_recordTypes['DeveloperName'] == 'Deanery') & (df_sf_recordTypes['SobjectType'] == 'Account'),
    'Id'
    ].iloc[0]  # Use .iloc[0] to get the first item if you're expecting exactly one match


# Insert Vicariates holding account
vicariate_account = sf.Account.upsert('Archdpdx_Migration_Id__c/Vicariates_Holding_Acc',
    {
    "Name": "Vicariates",
    "ParentId": diocesan_account_id,
    "mbfc__Diocese__c": diocesan_account_id,
    "RecordTypeId": deanery_recordTypeId,
    # "mbfc__Group_Type__c": 'Office',
    "Job_Id__c": curr_job_id
    }
)

# Get Vicariate Holding Acc's SF ID (as an upsert doesn't return the actual record ID)
vicariate_account = sf.Account.get_by_custom_id('Archdpdx_Migration_Id__c', 'Vicariates_Holding_Acc')
vicariate_account_id = vicariate_account['Id']

vicariate_account_id

'001Dx00001HwDuDIAV'

In [60]:
# Prepare Vicariates staging DF

vicariates = accounts[accounts['AccountRecordType'] == 'Deanery']


vicariates = vicariates[[
    'Record Number',
    'Name',
    # 'AccountRecordType',
    'Job_Id__c',
    'Archdpdx_Migration_Id__c',
    'RecordTypeId'
    ]]

# add parentid
vicariates["mbfc__Diocese__c"] = diocesan_account_id
vicariates['ParentId'] = vicariate_account_id
# vicariates['mbfc__Church_Type__c'] = 'Deanery'
vicariates['RecordTypeId'] = deanery_recordTypeId

vicariates.rename(columns={
        # 'Name, City': 'Name',
        'External_Id': 'Archdpdx_Migration_Id__c'
    }, inplace=True)

vicariates.reset_index()
vicariates.set_index('Record Number', inplace=True)

vicariates

Name  Job_Id__c  \
Record Number                                                  
1                      Albany-Corvallis Vicariate        138   
2                   Beaverton, Suburban Vicariate        138   
3                       Columbia County Vicariate        138   
4                     Downtown Portland Vicariate        138   
5               East Portland, Suburban Vicariate        138   
6                         Marion County Vicariate        138   
7                   Metropolitan Eugene Vicariate        138   
8                    Metropolitan Salem Vicariate        138   
9                           North Coast Vicariate        138   
10                   Northeast Portland Vicariate        138   
11                              Santiam Vicariate        138   
12                          South Coast Vicariate        138   
13             South Portland, Suburban Vicariate        138   
14                   Southeast Portland Vicariate        138   
15                      Southern Oregon Vicariate        138   
16                      Tualatin Valley Vicariate        138   
17              West Portland, Suburban Vicariate        138   
18                       Yamhill County Vicariate        138   

              Archdpdx_Migration_Id__c        RecordTypeId  \
Record Number                                                
1                         Vicariates_1  012Dx0000003p4yIAA   
2                         Vicariates_2  012Dx0000003p4yIAA   
3                         Vicariates_3  012Dx0000003p4yIAA   
4                         Vicariates_4  012Dx0000003p4yIAA   
5                         Vicariates_5  012Dx0000003p4yIAA   
6                         Vicariates_6  012Dx0000003p4yIAA   
7                         Vicariates_7  012Dx0000003p4yIAA   
8                         Vicariates_8  012Dx0000003p4yIAA   
9                         Vicariates_9  012Dx0000003p4yIAA   
10                       Vicariates_10  012Dx0000003p4yIAA   
11                       Vicariates_11  012Dx0000003p4yIAA   
12                       Vicariates_12  012Dx0000003p4yIAA   
13                       Vicariates_13  012Dx0000003p4yIAA   
14                       Vicariates_14  012Dx0000003p4yIAA   
15                       Vicariates_15  012Dx0000003p4yIAA   
16                       Vicariates_16  012Dx0000003p4yIAA   
17                       Vicariates_17  012Dx0000003p4yIAA   
18                       Vicariates_18  012Dx0000003p4yIAA   

                 mbfc__Diocese__c            ParentId  
Record Number                                          
1              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
2              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
3              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
4              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
5              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
6              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
7              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
8              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
9              001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
10             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
11             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
12             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
13             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
14             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
15             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
16             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
17             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV  
18             001Dx00001HwDsgIAF  001Dx00001HwDuDIAV

#### Export Vicariates to CSV


In [61]:
# export to CSV
vicariates.to_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/vicariates_staging.csv')


#### Upsert Vicariates


In [62]:
bulk_data = []
for row in vicariates.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

if run_upserts == 'True':
    vicariate_upsert = sf.bulk.Account.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
    upserts = pd.DataFrame(vicariate_upsert)

    print(upserts)
    

    success  created                  id errors
0      True    False  001Dx00001HwDwnIAF     []
1      True    False  001Dx00001HwDwoIAF     []
2      True    False  001Dx00001HwDwpIAF     []
3      True    False  001Dx00001HwDwqIAF     []
4      True    False  001Dx00001HwDwrIAF     []
5      True    False  001Dx00001HwDwsIAF     []
6      True    False  001Dx00001HwDwtIAF     []
7      True    False  001Dx00001HwDwuIAF     []
8      True    False  001Dx00001HwDwvIAF     []
9      True    False  001Dx00001HwDwwIAF     []
10     True    False  001Dx00001HwDwxIAF     []
11     True    False  001Dx00001HwDwyIAF     []
12     True    False  001Dx00001HwDwzIAF     []
13     True    False  001Dx00001HwDx0IAF     []
14     True    False  001Dx00001HwDx1IAF     []
15     True    False  001Dx00001HwDx2IAF     []
16     True    False  001Dx00001HwDx3IAF     []
17     True    False  001Dx00001HwDx4IAF     []


In [63]:
# Generate an Errors log
import csv

keys = vicariate_upsert[0].keys()

with open('results_files/vicariate_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(vicariate_upsert)

In [64]:
# Get Vicariate records from SF

sf_deaneries = sf.query("SELECT Archdpdx_Migration_Id__c, Id FROM Account WHERE RecordType.DeveloperName = 'Deanery'")

df_sf_deaneries = pd.DataFrame(sf_deaneries['records'])
df_sf_deaneries = df_sf_deaneries.drop(columns = 'attributes')

df_sf_deaneries

# Creates a dict of Vicariate unique ids to the new Salesforce record IDs, so can populate on latter Account records
vicariate_sf_recordids = df_sf_deaneries.set_index('Archdpdx_Migration_Id__c')['Id'].to_dict()
vicariate_sf_recordids

{'Vicariates_Holding_Acc': '001Dx00001HwDuDIAV',
 'Vicariates_1': '001Dx00001HwDwnIAF',
 'Vicariates_2': '001Dx00001HwDwoIAF',
 'Vicariates_3': '001Dx00001HwDwpIAF',
 'Vicariates_4': '001Dx00001HwDwqIAF',
 'Vicariates_5': '001Dx00001HwDwrIAF',
 'Vicariates_6': '001Dx00001HwDwsIAF',
 'Vicariates_7': '001Dx00001HwDwtIAF',
 'Vicariates_8': '001Dx00001HwDwuIAF',
 'Vicariates_9': '001Dx00001HwDwvIAF',
 'Vicariates_10': '001Dx00001HwDwwIAF',
 'Vicariates_11': '001Dx00001HwDwxIAF',
 'Vicariates_12': '001Dx00001HwDwyIAF',
 'Vicariates_13': '001Dx00001HwDwzIAF',
 'Vicariates_14': '001Dx00001HwDx0IAF',
 'Vicariates_15': '001Dx00001HwDx1IAF',
 'Vicariates_16': '001Dx00001HwDx2IAF',
 'Vicariates_17': '001Dx00001HwDx3IAF',
 'Vicariates_18': '001Dx00001HwDx4IAF'}

### B) Parishes, Schools, Organizations


In [65]:
# Create acc_main (accounts excluding Deaneries (already handled) and Religious (to be handled differently, after))
acc_main = accounts[accounts['AccountRecordType'] != 'Deanery']
acc_main = acc_main[acc_main['AccountRecordType'] != 'Religious']

acc_main.loc[acc_main['AccountRecordType'] == 'Church', 'Vicariate_Ext_Id'] = 'Vicariates_' + acc_main['Vicariate']

In [66]:
acc_main.sample(5)

Record Number AccountRecordType                         Formal_Name__c  \
305             52      Organization         Regis St. Mary Catholic School   
296             43      Organization            St. Therese Catholic School   
126             97            Church  St. Irene the Virgin and Great Martyr   
150            121            Church                  St. Francis of Assisi   
283             30      Organization   St. John the Baptist Catholic School   

                                                Name Parish Name  \
305          Regis St. Mary Catholic School, Stayton         NaN   
296            St. Therese Catholic School, Portland         NaN   
126  St. Irene the Virgin and Great Martyr, Portland         NaN   
150                       St. Francis of Assisi, Roy         NaN   
283  St. John the Baptist Catholic School, Milwaukie         NaN   

     Archdiocese_Assigns_Clergy__c Locator_Description__c BillingCity  \
305                           True  St. Mary Campus (K-8)     Stayton   
296                           True                    NaN    Portland   
126                          False                    NaN    Portland   
150                           True                    NaN       Banks   
283                           True                    NaN   Milwaukie   

    BillingState  Mailing Address Province  ... Religious_Secular_Order__c  \
305           OR                       NaN  ...                       None   
296           OR                       NaN  ...                       None   
126           OR                       NaN  ...                       None   
150           OR                       NaN  ...                       None   
283           OR                       NaN  ...                       None   

    Pontifical_or_Diocesan_Order__c    Parent_Parish__c            ParentId  \
305                            None                 NaN                 NaN   
296                            None  001Dx00001HwE0HIAV  001Dx00001HwE0HIAV   
126                            None                 NaN                 NaN   
150                            None                 NaN                 NaN   
283                            None  001Dx00001HwDzVIAV  001Dx00001HwDzVIAV   

    mbfc__Church_Type__c mbfc__Organization_Type__c Archdpdx_Migration_Id__c  \
305                  NaN                     School               Schools_52   
296                  NaN                     School               Schools_43   
126               Parish                        NaN              Parishes_97   
150               Parish                        NaN             Parishes_121   
283                  NaN                     School               Schools_30   

           RecordTypeId Job_Id__c Vicariate_Ext_Id  
305  012Dx0000003p50IAA       138              NaN  
296  012Dx0000003p50IAA       138              NaN  
126  012Dx0000003p4xIAA       138     Vicariates_0  
150  012Dx0000003p4xIAA       138    Vicariates_16  
283  012Dx0000003p50IAA       138              NaN  

[5 rows x 75 columns]

In [67]:
# map in Deaneries
acc_main['mbfc__Deanery__c'] = acc_main.Vicariate_Ext_Id.map(vicariate_sf_recordids)

acc_main[acc_main['AccountRecordType'] == 'Church']['mbfc__Deanery__c']

35     001Dx00001HwDwnIAF
36     001Dx00001HwDwzIAF
37     001Dx00001HwDx2IAF
38     001Dx00001HwDwvIAF
39     001Dx00001HwDx1IAF
              ...        
181    001Dx00001HwDwrIAF
182    001Dx00001HwDx3IAF
183    001Dx00001HwDwsIAF
184    001Dx00001HwDx4IAF
185    001Dx00001HwDwtIAF
Name: mbfc__Deanery__c, Length: 151, dtype: object

In [68]:
# Clean up NaN values

acc_main.fillna('', inplace=True)

In [69]:
# Generate Schedule text from all Schedule columns

def create_account_schedule(row):
    account_schedule = []
    for i in range(1, 8):
        head_col = f'Schedule {i} Head'
        text_col = f'Schedule {i} Text'
        
        head = row[head_col]
        text = row[text_col]
        
        if pd.notnull(head) or pd.notnull(text):
            if pd.notnull(head):
                account_schedule.append(f"<p><strong>{head}</strong></p>")
            if pd.notnull(text):
                account_schedule.append(f"<p>{text}</p>")
            account_schedule.append("<p><br></p>")
    
    # Join all parts into a single string
    return "".join(account_schedule).strip()

acc_main['mbfc__Mass_Times__c'] = acc_main.apply(create_account_schedule, axis=1)



In [70]:
acc_main['mbfc__Mass_Times__c'].sample(15)

289    <p><strong></strong></p><p></p><p><br></p><p><...
144    <p><strong>Weekend Mass</strong></p><p>Saturda...
285    <p><strong></strong></p><p></p><p><br></p><p><...
119    <p><strong>Weekend Mass</strong></p><p>Saturda...
98     <p><strong>Weekend Mass</strong></p><p>Saturda...
72     <p><strong>Weekend Mass</strong></p><p>Saturda...
89     <p><strong>Weekend Mass</strong></p><p>Saturda...
75     <p><strong>Weekend Mass</strong></p><p>Saturda...
161    <p><strong>Weekend Mass</strong></p><p>Saturda...
66     <p><strong>Weekend Mass</strong></p><p>Saturda...
22     <p><strong></strong></p><p></p><p><br></p><p><...
178    <p><strong>Weekend Mass</strong></p><p>Saturda...
153    <p><strong>Weekend Mass</strong></p><p>Saturda...
52     <p><strong>Weekend Mass</strong></p><p>Saturda...
104    <p><strong>Weekend Mass</strong></p><p>Sunday ...
Name: mbfc__Mass_Times__c, dtype: object

In [71]:
acc_main

Record Number AccountRecordType  \
0                1      Organization   
1                3      Organization   
2                4      Organization   
3                6      Organization   
4               11      Organization   
..             ...               ...   
311             58      Organization   
330              1      Organization   
331              2      Organization   
332              3      Organization   
333              4      Organization   

                                        Formal_Name__c  \
0                                      Pastoral Center   
1                                    Catholic Sentinel   
2                                  Catholic Cemeteries   
3                                       Griffin Center   
4                   Providence Portland Medical Center   
..                                                 ...   
311                Resurrection Catholic Parish School   
330                                  OSU Newman Center   
331                 St. Thomas More (UO) Newman Center   
332  Walsh Memorial (SOU) Newman Center at Our Lady...   
333                            PDX (PSU) Newman Center   

                                                  Name Parish Name  \
0                                      Pastoral Center               
1                                    Catholic Sentinel               
2                                  Catholic Cemeteries               
3                                       Griffin Center               
4                   Providence Portland Medical Center               
..                                                 ...         ...   
311      Resurrection Catholic Parish School, Tualatin               
330                       OSU Newman Center, Corvallis               
331         St. Thomas More (UO) Newman Center, Eugene               
332  Walsh Memorial (SOU) Newman Center at Our Lady...               
333                  PDX (PSU) Newman Center, Portland               

     Archdiocese_Assigns_Clergy__c Locator_Description__c BillingCity  \
0                             True                           Portland   
1                            False                           Portland   
2                            False                           Portland   
3                            False                          Milwaukie   
4                             True                           Portland   
..                             ...                    ...         ...   
311                           True                           Tualatin   
330                          False                          Corvallis   
331                          False                             Eugene   
332                           True                            Ashland   
333                          False                           Portland   

    BillingState Mailing Address Province  ...    Parent_Parish__c  \
0             OR                           ...                       
1             OR                           ...                       
2             OR                           ...                       
3             OR                           ...                       
4             OR                           ...                       
..           ...                      ...  ...                 ...   
311           OR                           ...  001Dx00001HwE0mIAF   
330           OR                           ...                       
331           OR                           ...                       
332           OR                           ...                       
333           OR                           ...                       

               ParentId mbfc__Church_Type__c mbfc__Organization_Type__c  \
0                                                                         
1                                                                         
2                                          

In [72]:
# Create 'account_staging' df (drop extraneous columns)

accounts_staging = acc_main[[
    'Name',
    'Formal_Name__c',
    'RecordTypeId',
    'mbfc__Church_Type__c',
    'mbfc__Deanery__c',
    'BillingStreet',
    'BillingCity',
    'BillingState',
    'BillingPostalCode',
    'BillingCountry',
    'Phone',
    'Fax',
    'mbfc__Email__c',
    'Website',
    'mbfc__Mass_Times__c',
    'mbfc__Abbreviation__c',
    'mbfc__Religious_Suffix__c',
    'mbfc__Type_Members__c',
    'Description',
    'Archdiocese_Assigns_Clergy__c', # Boolean fields
    'mbfc__Non_Latin__c', 
    'Disabled_Access__c', 
    'Locator_Description__c',
    'Parent_Parish__c',
    'mbfc__Date_Established__c',
    'County__c',
    'Sanctuary_Capacity__c',
    # 'Miles_to_Pastoral_Centre__c',
    'Religious_Secular_Order__c',
    'Pontifical_or_Diocesan_Order__c',
    'Archdiocesan_School_Code__c',
    'Grades_Provided__c',
    'Job_Id__c',
    'Archdpdx_Migration_Id__c',
    'mbfc__Organization_Type__c',
    'ParentId'  # Later, check whether or not can upsert using external ID using this field


    ]]

In [73]:
accounts_staging

Name  \
0                                      Pastoral Center   
1                                    Catholic Sentinel   
2                                  Catholic Cemeteries   
3                                       Griffin Center   
4                   Providence Portland Medical Center   
..                                                 ...   
311      Resurrection Catholic Parish School, Tualatin   
330                       OSU Newman Center, Corvallis   
331         St. Thomas More (UO) Newman Center, Eugene   
332  Walsh Memorial (SOU) Newman Center at Our Lady...   
333                  PDX (PSU) Newman Center, Portland   

                                        Formal_Name__c        RecordTypeId  \
0                                      Pastoral Center  012Dx0000003p50IAA   
1                                    Catholic Sentinel  012Dx0000003p50IAA   
2                                  Catholic Cemeteries  012Dx0000003p50IAA   
3                                       Griffin Center  012Dx0000003p50IAA   
4                   Providence Portland Medical Center  012Dx0000003p50IAA   
..                                                 ...                 ...   
311                Resurrection Catholic Parish School  012Dx0000003p50IAA   
330                                  OSU Newman Center  012Dx0000003p50IAA   
331                 St. Thomas More (UO) Newman Center  012Dx0000003p50IAA   
332  Walsh Memorial (SOU) Newman Center at Our Lady...  012Dx0000003p50IAA   
333                            PDX (PSU) Newman Center  012Dx0000003p50IAA   

    mbfc__Church_Type__c mbfc__Deanery__c        BillingStreet BillingCity  \
0                                           2838 E Burnside St    Portland   
1                                           2838 E Burnside St    Portland   
2                                          333 SW Skyline Blvd    Portland   
3                                           11957 SE Fuller Rd   Milwaukie   
4                                            4805 NE Glisan St    Portland   
..                   ...              ...                  ...         ...   
311                                                               Tualatin   
330                                         2127 NW Monroe Ave   Corvallis   
331                                            1850 Emerald St      Eugene   
332                                            987 Hillview Dr     Ashland   
333                                             424 SW Mill St    Portland   

    BillingState BillingPostalCode BillingCountry  ... County__c  \
0             OR             97214                 ...             
1             OR             97214                 ...             
2             OR             97221                 ...             
3             OR             97222                 ...             
4             OR             97213                 ...             
..           ...               ...            ...  ...       ...   
311           OR                                   ...             
330           OR             97330                 ...             
331           OR             97403                 ...             
332           OR             97520                 ...             
333           OR             97201                 ...             

    Sanctuary_Capacity__c Religious_Secular_Order__c  \
0                                                      
1                                                      
2                                                      
3                                                      
4                                                      
..                    ...                        ...   
311                                                    
330                                                    
331                                                    
332                                                    
333                                           

#### Create Parishes Holding Acc for acc heirarchy


In [74]:
# Upsert a Parishes holding account

# Get Account Group RecordTypeID
group_recordTypeId = df_sf_recordTypes.loc[
    (df_sf_recordTypes['DeveloperName'] == 'Group') & (df_sf_recordTypes['SobjectType'] == 'Account'),
    'Id'
    ].iloc[0]  # Use .iloc[0] to get the first item if you're expecting exactly one match


# Insert Vicariates holding account
parish_holding_account = sf.Account.upsert('Archdpdx_Migration_Id__c/Parishes_Holding_Acc',
    {
    "Name": "Parishes",
    "ParentId": diocesan_account_id,
    "RecordTypeId": group_recordTypeId,
    "Job_Id__c": curr_job_id,
    "mbfc__Group_Type__c": "Office"
    }
)

# Get Vicariate Holding Acc's SF ID (as an upsert doesn't return the actual record ID)

parish_holding_account = sf.Account.get_by_custom_id('Archdpdx_Migration_Id__c', 'Parishes_Holding_Acc')

parishes_holding_account_id = parish_holding_account['Id']

parishes_holding_account_id

'001Dx00001HwDxKIAV'

In [75]:
# Set the ParentId for all Parish records

# accounts_staging['ParentId'] = None # Commented this out as (a) the field already exists and it was blanking out pre-existing values.

accounts_staging['ParentId']= accounts_staging.apply(
    lambda row: parishes_holding_account_id if row['mbfc__Church_Type__c'] == 'Parish' else row['ParentId'], axis=1
)

accounts_staging.sample(10)


/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_38105/335598879.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  accounts_staging['ParentId']= accounts_staging.apply(


Name  \
55   Our Lady of Perpetual Help, Cottage Grove   
14                            Diaconate Office   
66   St. Mary, Our Lady of the Dunes, Florence   
58        St. Martin de Porres Mission, Dayton   
289      St. Francis Catholic School, Sherwood   
3                               Griffin Center   
291          St. Joseph Catholic School, Salem   
285                All Saints School, Portland   
96                     All Souls, Myrtle Creek   
87                  St. Patrick Mission, Lyons   

                      Formal_Name__c        RecordTypeId mbfc__Church_Type__c  \
55        Our Lady of Perpetual Help  012Dx0000003p4xIAA               Parish   
14                  Diaconate Office  012Dx0000003p50IAA                        
66   St. Mary, Our Lady of the Dunes  012Dx0000003p4xIAA               Parish   
58              St. Martin de Porres  012Dx0000003p4xIAA               Parish   
289      St. Francis Catholic School  012Dx0000003p50IAA                        
3                     Griffin Center  012Dx0000003p50IAA                        
291       St. Joseph Catholic School  012Dx0000003p50IAA                        
285                All Saints School  012Dx0000003p50IAA                        
96                         All Souls  012Dx0000003p4xIAA               Parish   
87                       St. Patrick  012Dx0000003p4xIAA               Parish   

       mbfc__Deanery__c                                      BillingStreet  \
55   001Dx00001HwDwtIAF  Our Lady of Perpetual Help Parish\n1025 N 19th St   
14                                     Pastoral Center\n2838 E Burnside St   
66   001Dx00001HwDwyIAF  St. Mary, Our Lady of the Dunes Parish\n85060 ...   
58   001Dx00001HwDx4IAF           St. Martin de Porres Mission\nPO Box 580   
289                                                                          
3                                                       11957 SE Fuller Rd   
291                                                                          
285                                                                          
96   001Dx00001HwDx1IAF                       All Souls Parish\nPO Box 810   
87   001Dx00001HwDwxIAF             St. Patrick Mission\n39043 Jordan Road   

       BillingCity BillingState BillingPostalCode BillingCountry  ...  \
55   Cottage Grove           OR             97424                 ...   
14        Portland           OR             97214                 ...   
66        Florence           OR             97439                 ...   
58         Yamhill           OR             97148                 ...   
289       Sherwood           OR                                   ...   
3        Milwaukie           OR             97222                 ...   
291          Salem           OR                                   ...   
285       Portland           OR                                   ...   
96    Myrtle Creek           OR             97457                 ...   
87            Scio           OR             97374                 ...   

    County__c Sanctuary_Capacity__c Religious_Secular_Order__c  \
55       Lane                 375.0                              
14                                                               
66       Lane                   0.0                              
58    Yamhill                   0.0                              
289                                                              
3                                                                
291                                                              
285                                                              
96    Douglas                 120.0                              
87       Linn                   0.0                              

    Pontifical_or_Diocesan_Order__c Archdiocesan_School_Code__c  \
55                                                                
14                                                                
66      

#### Upsert Accounts (TBD )


In [76]:
# send accounts_staging to csv
accounts_staging.to_csv('staging_files/accounts_staging.csv', encoding='utf-8-sig')

In [ ]:

# # Rename columns apis
# accounts_staging = accounts_staging.rename(columns={'Parent_Parish__c': 'Parent_Parish__r'})  # Later on, attempt to include 'ParentId' (which, as a standard SF field, might not work)

# # Reformat values to match what SF api requires
# accounts_staging['Parent_Parish__r'] = accounts_staging.apply(lambda x: "{'Archdpdx_Migration_Id__c': '" + x['Parent_Parish__r'] + "'}" if pd.notna(x['Parent_Parish__r']) and x['Parent_Parish__r'] != 'None' and x['Parent_Parish__r'] != '' else None, axis=1)




In [78]:
accounts_staging

Name  \
0                                      Pastoral Center   
1                                    Catholic Sentinel   
2                                  Catholic Cemeteries   
3                                       Griffin Center   
4                   Providence Portland Medical Center   
..                                                 ...   
311      Resurrection Catholic Parish School, Tualatin   
330                       OSU Newman Center, Corvallis   
331         St. Thomas More (UO) Newman Center, Eugene   
332  Walsh Memorial (SOU) Newman Center at Our Lady...   
333                  PDX (PSU) Newman Center, Portland   

                                        Formal_Name__c        RecordTypeId  \
0                                      Pastoral Center  012Dx0000003p50IAA   
1                                    Catholic Sentinel  012Dx0000003p50IAA   
2                                  Catholic Cemeteries  012Dx0000003p50IAA   
3                                       Griffin Center  012Dx0000003p50IAA   
4                   Providence Portland Medical Center  012Dx0000003p50IAA   
..                                                 ...                 ...   
311                Resurrection Catholic Parish School  012Dx0000003p50IAA   
330                                  OSU Newman Center  012Dx0000003p50IAA   
331                 St. Thomas More (UO) Newman Center  012Dx0000003p50IAA   
332  Walsh Memorial (SOU) Newman Center at Our Lady...  012Dx0000003p50IAA   
333                            PDX (PSU) Newman Center  012Dx0000003p50IAA   

    mbfc__Church_Type__c mbfc__Deanery__c        BillingStreet BillingCity  \
0                                           2838 E Burnside St    Portland   
1                                           2838 E Burnside St    Portland   
2                                          333 SW Skyline Blvd    Portland   
3                                           11957 SE Fuller Rd   Milwaukie   
4                                            4805 NE Glisan St    Portland   
..                   ...              ...                  ...         ...   
311                                                               Tualatin   
330                                         2127 NW Monroe Ave   Corvallis   
331                                            1850 Emerald St      Eugene   
332                                            987 Hillview Dr     Ashland   
333                                             424 SW Mill St    Portland   

    BillingState BillingPostalCode BillingCountry  ... County__c  \
0             OR             97214                 ...             
1             OR             97214                 ...             
2             OR             97221                 ...             
3             OR             97222                 ...             
4             OR             97213                 ...             
..           ...               ...            ...  ...       ...   
311           OR                                   ...             
330           OR             97330                 ...             
331           OR             97403                 ...             
332           OR             97520                 ...             
333           OR             97201                 ...             

    Sanctuary_Capacity__c Religious_Secular_Order__c  \
0                                                      
1                                                      
2                                                      
3                                                      
4                                                      
..                    ...                        ...   
311                                                    
330                                                    
331                                                    
332                                                    
333                                           

In [79]:
# accounts_staging[accounts_staging.Parent_Parish__r.isnull() == False]["Parent_Parish__r"]

In [80]:
print(accounts_staging['mbfc__Date_Established__c'].dtype)

datetime64[ns]


In [81]:

# Convert datetime to string in the desired format
accounts_staging['mbfc__Date_Established__c'] = accounts_staging['mbfc__Date_Established__c'].dt.strftime('%Y-%m-%d')

/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_38105/4119055288.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  accounts_staging['mbfc__Date_Established__c'] = accounts_staging['mbfc__Date_Established__c'].dt.strftime('%Y-%m-%d')


In [82]:
# Upsert using new function

accounts_upsert2 = upsert_to_salesforce_bulk(sf, accounts_staging, 'Account', 'Archdpdx_Migration_Id__c', 'results_files/accounts_status', batch_size=100)

/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_38105/3535390447.py:156: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe.replace({pd.NA: None, ' ': None, '': None}, inplace=True)


Batch 1 processed: 100 successful, 0 failed.
Batch 2 processed: 200 successful, 0 failed.
Batch 3 processed: 246 successful, 0 failed.
Upsert completed. Total records processed: 246, Batches: 3, Successful upserts: 246, Failed upserts: 0


In [83]:
# Extract SF Account records

sf_accounts = sf.query('Select id, Name, RecordTypeId, mbfc__Church_Type__c, Archdpdx_Migration_Id__c, Job_Id__c from Account WHERE Job_Id__c != null')
sf_accounts = pd.DataFrame(sf_accounts['records'])
sf_accounts = sf_accounts.drop(columns = 'attributes')
sf_accounts

Id                                               Name  \
0    001Dx00001HwDuDIAV                                         Vicariates   
1    001Dx00001HwDwnIAF                         Albany-Corvallis Vicariate   
2    001Dx00001HwDwoIAF                      Beaverton, Suburban Vicariate   
3    001Dx00001HwDwpIAF                          Columbia County Vicariate   
4    001Dx00001HwDwqIAF                        Downtown Portland Vicariate   
..                  ...                                                ...   
331  001Dx00001HwE5gIAF   Society of the Divine Saviour, Rome, Italy (SDS)   
332  001Dx00001HwE5hIAF  Society of Our Lady of the Most Holy Trinity, ...   
333  001Dx00001HwE5iIAF          Community of St. Thomas More, Eugene (OP)   
334  001Dx00001HwE5jIAF         Saint Benedict Lodge, McKenzie Bridge (OP)   
335  001O300000aKY5dIAG     Congregation of the Holy Cross, Portland (CSC)   

           RecordTypeId mbfc__Church_Type__c Archdpdx_Migration_Id__c  \
0    012Dx0000003p4yIAA                 None   Vicariates_Holding_Acc   
1    012Dx0000003p4yIAA                 None             Vicariates_1   
2    012Dx0000003p4yIAA                 None             Vicariates_2   
3    012Dx0000003p4yIAA                 None             Vicariates_3   
4    012Dx0000003p4yIAA                 None             Vicariates_4   
..                  ...                  ...                      ...   
331  012Dx0000003p52IAA                 None        RelCommunities_78   
332  012Dx0000003p52IAA                 None        RelCommunities_79   
333  012Dx0000003p52IAA                 None        RelCommunities_80   
334  012Dx0000003p52IAA                 None        RelCommunities_81   
335  012Dx0000003p52IAA                 None        RelCommunities_23   

    Job_Id__c  
0         138  
1         138  
2         138  
3         138  
4         138  
..        ...  
331       137  
332       137  
333       137  
334       137  
335       137  

[336 rows x 6 columns]

### C) Religious Institutes (Parents)


This section prepares and upserts parent Religious Congregation accounts for each row in RelCommunities table.

Dataframes >>
- acc_religious
- acc_religious_2
- acc_religious_parents

In [84]:
"""
- 'acc_religious' DF: create unique_id of religious parents
- create 'acc_religious_orders' DF , upsert into SF
- extract accounts from Salesforce, create dict (external_ID : account_ID)
- map parent ids onto religious child accounts DF in main DF
- 'acc_religious' > staging DF ('acc_religious')
    - drop unnecessary columns
    - upsert create DF of religious children, upsert into SF with
"""

# Create a new DF of all Religious accounts
acc_religious = accounts[accounts['AccountRecordType'] == 'Religious']

# Create a simplified external ID field for Parent Accounts
acc_religious['Archdpdx_Migration_Id__c'] = acc_religious['Order Full Name'].apply(
    lambda x: x.lower().replace(' ', '')[:40]
)

acc_religious_2 = acc_religious

# Create a DF for only parent religious order accounts
acc_religious_parents = acc_religious_2[[
    'Order Full Name', 
    # 'Name', 
    'mbfc__Abbreviation__c', 
    'mbfc__Religious_Suffix__c', 
    'mbfc__Type_Members__c', 
    'Archdpdx_Migration_Id__c',
    'Pontifical_or_Diocesan_Order__c',
    'Religious_Secular_Order__c',
    ]]

# Drop duplicate rows of the same parent Religious Order (becuase there are more than 1 local community of a particular order)
acc_religious_parents.drop_duplicates('Order Full Name', inplace=True)

# Manipulate the 'Name' field to remove any comma and subsequent text
# acc_religious_parents['Name'] = acc_religious_parents['Name'].str.split(',').str[0]

# How many remaining rows after dropping duplicates?
print(acc_religious_parents.shape)

# Rename columns
acc_religious_parents = acc_religious_parents.rename(columns={
    # 'Order Full Name': 'Description',
    'Order Full Name': 'Name'
    })

# Drop NA
acc_religious_parents.fillna('', inplace=True)

acc_religious_parents


(62, 7)


/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_38105/3372094970.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acc_religious['Archdpdx_Migration_Id__c'] = acc_religious['Order Full Name'].apply(
/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_38105/3372094970.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acc_religious_parents.drop_duplicates('Order Full Name', inplace=True)


Name  \
186                                 Societas Iesu   
187   Ordo Cisterciensis Strictioris Observantiae   
189                         Ordo Sancti Benedicti   
190                 Misioneros del Espíritu Santo   
191                             Apostles of Jesus   
..                                            ...   
249                 Fraternità san Carlo Borromeo   
250                 Sons of Mary, Mother of Mercy   
251                    Society of the Divine Word   
252                 Society of the Divine Saviour   
253  Society of Our Lady of the Most Holy Trinity   

                                 mbfc__Abbreviation__c  \
186                                            Jesuits   
187                                          Trappists   
189                                       Benedictines   
190  Missionaries of the Holy Spirit, Christ the Pr...   
191                                  Apostles of Jesus   
..                                                 ...   
249                          Fraternity of St. Charles   
250                      Sons of Mary, Mother of Mercy   
251                         Society of the Divine Word   
252                      Society of the Divine Saviour   
253       Society of Our Lady of the Most Holy Trinity   

    mbfc__Religious_Suffix__c mbfc__Type_Members__c  \
186                        SJ                   Men   
187                      OCSO                   Men   
189                       OSB                   Men   
190                      MSpS                   Men   
191                        AJ                   Men   
..                        ...                   ...   
249                      FSCB                   Men   
250                      SMMM                   Men   
251                       SVD                   Men   
252                       SDS                   Men   
253                      SOLT                   Men   

                     Archdpdx_Migration_Id__c Pontifical_or_Diocesan_Order__c  \
186                              societasiesu                                   
187  ordocisterciensisstrictiorisobservantiae                Pontifical Order   
189                       ordosanctibenedicti                                   
190                misionerosdelespíritusanto                                   
191                           apostlesofjesus                  Diocesan Order   
..                                        ...                             ...   
249                fraternitàsancarloborromeo                                   
250                  sonsofmary,motherofmercy                                   
251                    societyofthedivineword                                   
252                 societyofthedivinesaviour                                   
253      societyofourladyofthemostholytrinity                                   

    Religious_Secular_Order__c  
186            Religious Order  
187            Religious Order  
189            Religious Order  
190                             
191            Religious Order  
..                         ...  
249                             
250                             
251                             
252                             
253                             

[62 rows x 7 columns]

In [85]:
acc_religious_parents['mbfc__Religious_Type__c'] = 'Congregation'

In [86]:
# Get Religious RecordTypeId
religious_recordtype_id = get_recordtype_id(df_sf_recordTypes, 'Religious', 'Account', 'mbfc')

religious_recordtype_id

'012Dx0000003p52IAA'

In [87]:
# Set recordType to 'Religious'

religious_recordtype_id = df_sf_recordTypes.loc[
    (df_sf_recordTypes['DeveloperName'] == 'Religious') & (df_sf_recordTypes['SobjectType'] == 'Account'),
    'Id'
    ].iloc[0]  # Use .iloc[0] to get the first item if you're expecting exactly one match

print(religious_recordtype_id)

acc_religious_parents['RecordTypeId'] = religious_recordtype_id

acc_religious_parents.sample(10)

012Dx0000003p52IAA


Name  \
251                         Society of the Divine Word   
187        Ordo Cisterciensis Strictioris Observantiae   
206                        Dominican Sisters of Adrian   
200       Domus Dei Clerical Society of Apostolic Life   
230                                  Sociedad de María   
211  Franciscan Missionary Sisters of Our Lady of S...   
192                Franciscan Sisters of the Eucharist   
225  Sisters of Reparation of the Sacred Wounds of ...   
250                      Sons of Mary, Mother of Mercy   
214                   Maryknoll Sisters of St. Dominic   

                   mbfc__Abbreviation__c mbfc__Religious_Suffix__c  \
251           Society of the Divine Word                       SVD   
187                            Trappists                      OCSO   
206                           Dominicans                        OP   
200                            Domus Dei                       SDD   
230                      Society of Mary                       SdM   
211                          Franciscans                       OSF   
192  Franciscan Sisters of the Eucharist                       FSE   
225                Sisters of Reparation                        SR   
250        Sons of Mary, Mother of Mercy                      SMMM   
214                    Maryknoll Sisters                        MM   

    mbfc__Type_Members__c                  Archdpdx_Migration_Id__c  \
251                   Men                    societyofthedivineword   
187                   Men  ordocisterciensisstrictiorisobservantiae   
206                 Women                  dominicansistersofadrian   
200                   Men    domusdeiclericalsocietyofapostoliclife   
230                 Women                           sociedaddemaría   
211                 Women  franciscanmissionarysistersofourladyofso   
192                 Women           franciscansistersoftheeucharist   
225                 Women  sistersofreparationofthesacredwoundsofje   
250                   Men                  sonsofmary,motherofmercy   
214                 Women              maryknollsistersofst.dominic   

    Pontifical_or_Diocesan_Order__c Religious_Secular_Order__c  \
251                                                              
187                Pontifical Order            Religious Order   
206                Pontifical Order                              
200                                            Religious Order   
230                  Diocesan Order            Religious Order   
211                  Diocesan Order            Religious Order   
192                Pontifical Order            Religious Order   
225                  Diocesan Order            Religious Order   
250                                                              
214                Pontifical Order            Religious Order   

    mbfc__Religious_Type__c        RecordTypeId  
251            Congregation  012Dx0000003p52IAA  
187            Congregation  012Dx0000003p52IAA  
206            Congregation  012Dx0000003p52IAA  
200            Congregation  012Dx0000003p52IAA  
230            Congregation  012Dx0000003p52IAA  
211            Congregation  012Dx0000003p52IAA  
192            Congregation  012Dx0000003p52IAA  
225            Congregation  012Dx0000003p52IAA  
250            Congregation  012Dx0000003p52IAA  
214            Congregation  012Dx0000003p52IAA

In [88]:
# Send to CSV
acc_religious_parents.to_csv('staging_files/religious_order_staging.csv', encoding='utf-8-sig')

In [89]:
# Upsert to Salesforce
bulk_data = []
for row in acc_religious_parents.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

if run_upserts == 'True':
    religious_order_upsert = sf.bulk.Account.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
    df_rel_order_upsert = pd.DataFrame(religious_order_upsert)

df_rel_order_upsert

success  created                  id errors
0      True    False  001Dx00001HwE3TIAV     []
1      True    False  001Dx00001HwE3UIAV     []
2      True    False  001Dx00001HwE3VIAV     []
3      True    False  001Dx00001HwE3WIAV     []
4      True    False  001Dx00001HwE3XIAV     []
..      ...      ...                 ...    ...
57     True    False  001Dx00001HwE4OIAV     []
58     True    False  001Dx00001HwE4PIAV     []
59     True    False  001Dx00001HwE4QIAV     []
60     True    False  001Dx00001HwE4RIAV     []
61     True    False  001Dx00001HwE4SIAV     []

[62 rows x 4 columns]

In [90]:
# Generate an Errors log
import csv

keys = religious_order_upsert[0].keys()

with open('results_files/religious_order_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(religious_order_upsert)

In [91]:
# get SF Accounts
get_all_rel_accounts = f"Select id, Name, RecordTypeId, Type, Archdpdx_Migration_Id__c from Account where RecordTypeID = '{religious_recordtype_id}'"

print(religious_recordtype_id)

# get list of records, add to dataframe
sf_accounts = sf.query(get_all_rel_accounts)
df_sf_accounts = pd.DataFrame(sf_accounts['records'])
df_sf_accounts = df_sf_accounts.drop(columns = 'attributes')

df_sf_accounts.sample(10)

012Dx0000003p52IAA


Id                                               Name  \
225  001O300000aKPITIA4                                 Saint John Society   
16   001Dx00001HwE3iIAF               Ordo Servorum Beatae Mariae Virginis   
71   001Dx00001HwE4lIAF  Blessed Stephen Bellesini Community, c/o Chanc...   
118  001Dx00001HwE5WIAV                Paulist Fathers, New York, NY (CSP)   
98   001Dx00001HwE5CIAV        Sisters of Mary of Kakamega, Portland (SMK)   
17   001Dx00001HwE3jIAF                          Adorers of the Holy Cross   
201  001O300000aK6iuIAC                                   Society of Jesus   
195  001O300000aK42pIAC                                  Domus Dei Society   
194  001O300000aK42oIAC                    Institute of the Incarnate Word   
106  001Dx00001HwE5KIAV                   Society of Mary, Corvallis (SdM)   

           RecordTypeId  Type          Archdpdx_Migration_Id__c  
225  012Dx0000003p52IAA  None                              None  
16   012Dx0000003p52IAA  None  ordoservorumbeataemariaevirginis  
71   012Dx0000003p52IAA  None                 RelCommunities_12  
118  012Dx0000003p52IAA  None                 RelCommunities_68  
98   012Dx0000003p52IAA  None                 RelCommunities_46  
17   012Dx0000003p52IAA  None             adorersoftheholycross  
201  012Dx0000003p52IAA  None                              None  
195  012Dx0000003p52IAA  None                              None  
194  012Dx0000003p52IAA  None                              None  
106  012Dx0000003p52IAA  None                 RelCommunities_54

In [92]:
religious_order_mapping = df_sf_accounts.set_index('Archdpdx_Migration_Id__c')['Id'].to_dict()
# religious_order_mapping

### D) Religious Communities


This section stages the 'relCommunities' tables as Religious Account records. 

Dataframes:
- acc_religious_staging
- acc_religious_staging_2 

In [93]:
acc_religious_staging = (acc_religious
                         .rename(columns={'Archdpdx_Migration_Id__c' : 'Parent_Archdpdx_Migration_Id__c'})
)

acc_religious_staging['ParentId'] = acc_religious_staging['Parent_Archdpdx_Migration_Id__c'].map(religious_order_mapping)

In [94]:
pd.set_option('display.max_columns', None)

In [95]:
# Enrich the data

acc_religious_staging['mbfc__Religious_Type__c'] = 'Local Community'
acc_religious_staging['Archdpdx_Migration_Id__c'] = 'RelCommunities_' + acc_religious_staging['Record Number'].astype('str')
acc_religious_staging['RecordTypeId'] = religious_recordtype_id
# acc_religious_staging.drop(columns='Name', inplace=True)
# acc_religious_staging.rename(columns={
#     'Name, City': 'Name'
# }, inplace=True)

In [96]:
acc_religious_staging.sample(5)

Record Number AccountRecordType  \
200             21         Religious   
238             64         Religious   
233             57         Religious   
235             61         Religious   
201             22         Religious   

                                        Formal_Name__c  \
200        Society of Domus Dei Holy House Monasteries   
238                           Heralds of the Good News   
233                  Priory of Our Lady of Consolation   
235  Society of Christ Fathers Province in the Unit...   
201                                  Franciscan Friars   

                                                  Name Parish Name  \
200  Society of Domus Dei Holy House Monasteries, W...         NaN   
238           Heralds of the Good News, Portland (HGN)         NaN   
233    Priory of Our Lady of Consolation, Amity (OSsS)         NaN   
235  Society of Christ Fathers Province in the Unit...         NaN   
201                   Franciscan Friars, Oakland (OFM)         NaN   

     Archdiocese_Assigns_Clergy__c Locator_Description__c BillingCity  \
200                          False                    NaN   Washougal   
238                          False                    NaN    Portland   
233                          False                    NaN       Amity   
235                          False                    NaN     Lombard   
201                          False                    NaN     Oakland   

    BillingState  Mailing Address Province BillingPostalCode BillingCountry  \
200           WA                       NaN             98671            NaN   
238           OR                       NaN             97214            NaN   
233           OR                       NaN             97101            NaN   
235           IL                       NaN             60148         POLAND   
201           CA                       NaN             94601            NaN   

            Phone           Fax          mbfc__Email__c  \
200  360-835-5358           NaN                     NaN   
238  503-233-8322           NaN  vschueler@archdpdx.org   
233  503-835-8080  503-835-9662    monks@brigittine.org   
235  630-424-0401           NaN                     NaN   
201  510-536-3722           NaN          info@sbofm.org   

                        Website       src_table Sort Name Parish City  \
200         http://nhachua.net/  RelCommunities       NaN         NaN   
238                         NaN  RelCommunities       NaN         NaN   
233  http://www.brigittine.com/  RelCommunities       NaN         NaN   
235          https://tchr.us/en  RelCommunities       NaN         NaN   
201           sbfranciscans.org  RelCommunities       NaN         NaN   

    Parent_Parish mbfc__Date_Established__c Vicariate Non-Latin County__c  \
200           NaN                       NaT       NaN       NaN       NaN   
238           NaN                       NaT       NaN       NaN       NaN   
233           NaN                       NaT       NaN       NaN       NaN   
235           NaN                       NaT       NaN       NaN       NaN   
201           NaN                       NaT       NaN       NaN       NaN   

     Disabled_Access__c  Sanctuary_Capacity__c Lat/Long Coordinates Decimal  \
200               False                    NaN                          NaN   
238               False                    NaN                          NaN   
233               False                    NaN                          NaN   
235               False                    NaN                          NaN   
201               False                    NaN                          NaN   

    Google Small Embed URL  Miles to Pastoral Center Schedule 1 Head  \
200                    NaN                       NaN             NaN   
238                    NaN                       NaN             NaN   
233                    NaN                       NaN             NaN   
235                    NaN                       NaN        

In [97]:
acc_religious_staging_2 = acc_religious_staging[[
    'Name',
    'RecordTypeId',
    'mbfc__Religious_Type__c',
    'BillingStreet',
    'BillingCity',
    'BillingState',
    'BillingPostalCode',
    'BillingCountry',
    'Phone',
    'Fax',
    'mbfc__Email__c',
    'Website',
    'mbfc__Abbreviation__c',
    'mbfc__Religious_Suffix__c',
    'mbfc__Type_Members__c',
    'Description',
    'Job_Id__c',
    'ParentId',
    'Archdpdx_Migration_Id__c'
    ]]

acc_religious_staging_2.sample(5)

Name        RecordTypeId  \
200  Society of Domus Dei Holy House Monasteries, W...  012Dx0000003p52IAA   
227  Sisters of St. Francis of Philadelphia, Portla...  012Dx0000003p52IAA   
228      Sisters of St. Joseph of Peace, Eugene (CSJP)  012Dx0000003p52IAA   
254          Community of St. Thomas More, Eugene (OP)  012Dx0000003p52IAA   
194  Blessed Stephen Bellesini Community, c/o Chanc...  012Dx0000003p52IAA   

    mbfc__Religious_Type__c                           BillingStreet  \
200         Local Community                           462 Hudson Rd   
227         Local Community                        609 S Convent Rd   
228         Local Community  CSJP Western Region Office\nPO Box 248   
254         Local Community                         1386 E 18th Ave   
194         Local Community             3180 University Ave Ste 255   

    BillingCity BillingState BillingPostalCode BillingCountry         Phone  \
200   Washougal           WA             98671            NaN  360-835-5358   
227       Aston           PA             19014            NaN  610-459-4125   
228    Bellevue           WA             98009            NaN  425-467-5400   
254      Eugene           OR             97403            NaN  541-343-0065   
194   San Diego           CA             92104            NaN  619-235-0247   

              Fax               mbfc__Email__c  \
200           NaN                          NaN   
227           NaN  communications@osfphila.org   
228  425-462-9760                          NaN   
254  541-686-8028                          NaN   
194           NaN                          NaN   

                                     Website  \
200                      http://nhachua.net/   
227                    https://osfphila.org/   
228                        https://csjp.org/   
254                             uonewman.org   
194  https://www.californiaaugustinians.org/   

                      mbfc__Abbreviation__c mbfc__Religious_Suffix__c  \
200                               Domus Dei                       SDD   
227  Sisters of St. Francis of Philadelphia                       OSF   
228                   Sisters of St. Joseph                      CSJP   
254                              Dominicans                        OP   
194                            Augustinians                       OSA   

    mbfc__Type_Members__c                                        Description  \
200                   Men  Serving Our Lady of Lavang Parish; Southeast A...   
227                 Women  Serving Ascension Parish, Cathedral of the Imm...   
228                 Women  Serving Sacred Heart RiverBend Medical Center,...   
254                   Men  Serving St. Thomas More Parish and Newman Cent...   
194                   Men  Serving Providence Medford Medical Center as C...   

     Job_Id__c            ParentId Archdpdx_Migration_Id__c  
200        138  001Dx00001HwE3eIAF        RelCommunities_21  
227        138  001Dx00001HwE43IAF        RelCommunities_51  
228        138  001Dx00001HwE44IAF        RelCommunities_52  
254        138  001Dx00001HwE3dIAF        RelCommunities_80  
194        138  001Dx00001HwE3aIAF        RelCommunities_12

In [98]:
# Final Cleanup

acc_religious_staging_2 = acc_religious_staging_2.fillna('')

In [99]:
acc_religious_staging_2

Name        RecordTypeId  \
186         Colombiere Jesuit Community, Portland (SJ)  012Dx0000003p52IAA   
187     Abbey of Our Lady of Guadalupe, Carlton (OCSO)  012Dx0000003p52IAA   
188             JCCU Jesuit Tertianship, Portland (SJ)  012Dx0000003p52IAA   
189  Benedictine Monks of Mount Angel Abbey, Saint ...  012Dx0000003p52IAA   
190  Missionaries of the Holy Spirit Provincial Hou...  012Dx0000003p52IAA   
..                                                 ...                 ...   
251       Society of the Divine Word, Techny, IL (SVD)  012Dx0000003p52IAA   
252   Society of the Divine Saviour, Rome, Italy (SDS)  012Dx0000003p52IAA   
253  Society of Our Lady of the Most Holy Trinity, ...  012Dx0000003p52IAA   
254          Community of St. Thomas More, Eugene (OP)  012Dx0000003p52IAA   
255         Saint Benedict Lodge, McKenzie Bridge (OP)  012Dx0000003p52IAA   

    mbfc__Religious_Type__c                                     BillingStreet  \
186         Local Community                                  3220 SE 43rd Ave   
187         Local Community  Abbey of Our Lady of Guadalupe\n9200 NE Abbey Rd   
188         Local Community                                  3301 SE 45th Ave   
189         Local Community                                        1 Abbey Dr   
190         Local Community                                      PO Box 22387   
..                      ...                                               ...   
251         Local Community      Society of the Divine Word, Chicago Province   
252         Local Community                       Via della Conciliazione, 51   
253         Local Community                                       PO Box 4116   
254         Local Community                                   1386 E 18th Ave   
255         Local Community                                   56630 N Bank Rd   

         BillingCity BillingState BillingPostalCode BillingCountry  \
186         Portland           OR             97206                  
187          Carlton           OR             97111                  
188         Portland           OR             97206                  
189   Saint Benedict           OR             97373                  
190        Milwaukie           OR             97269                  
..               ...          ...               ...            ...   
251                                                                  
252             Roma                        I-00193          ITALY   
253   Corpus Christi           TX             78469                  
254           Eugene           OR             97403                  
255  McKenzie Bridge           OR             97413                  

              Phone           Fax               mbfc__Email__c  \
186    503-595-1941                                              
187    503-852-7174  503-852-7748  community@trappistabbey.org   
188                                  jctertianship@jesuits.org   
189    503-845-3030                      info@mtangelabbey.edu   
190    503-324-2492  503-324-2493                                
..              ...           ...                          ...   
251                                                              
252  +39 06 686 291                                              
253                                                              
254    541-343-0065  541-686-8028                                
255    541-822-3572                         sblodge@opwest.org   

                              Website  \
186      https://www.jesuitswest.org/   
187     http://www.trappistabbey.org/   
188                                     
189  https://www.mountangelabbey.org/   
190                   www.mspscpp.org   
..                                ...   
251       https://www.divineword.org/   
252               http://www.sds.org/   
253                 https://solt.net/   
254                      uonewman.org   
255                sblodge.opwest.org   

             

In [100]:
# Send to CSV
acc_religious_staging_2.to_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/religious_community_staging.csv', encoding='utf-8-sig')

In [101]:
upsert_to_salesforce_bulk(sf, acc_religious_staging_2, 'Account', 'Archdpdx_Migration_Id__c', 'results_files/religious_comm_results.csv', 100)


Batch 1 processed: 70 successful, 0 failed.
Upsert completed. Total records processed: 70, Batches: 1, Successful upserts: 70, Failed upserts: 0


### E) Religious Superiors


In [102]:
acc_rel_superiors = acc_religious_2[[
    'Name',
    'Major Superior Name',
    'Major Superior Phone',
    'Major Superior Email',
    'Archdpdx_Migration_Id__c']].copy()


acc_rel_superiors['AccountId'] = acc_rel_superiors.Archdpdx_Migration_Id__c.map(religious_order_mapping)

acc_rel_superiors.sample(5)

Name Major Superior Name  \
225               Sisters of Reparation, Portland (SR)                 NaN   
250  Sons of Mary, Mother of Mercy, Umuahia, Nigeri...                 NaN   
196  Félix Rougier House of Studies, Mount Angel (M...                 NaN   
240  Order of Friars Minor, Capuchins, Portland (OF...                 NaN   
247           Brothers of Saint John, Laredo, TX (CSJ)                 NaN   

    Major Superior Phone Major Superior Email  \
225                  NaN                  NaN   
250                  NaN                  NaN   
196                  NaN                  NaN   
240                  NaN                  NaN   
247                  NaN                  NaN   

                     Archdpdx_Migration_Id__c           AccountId  
225  sistersofreparationofthesacredwoundsofje  001Dx00001HwE41IAF  
250                  sonsofmary,motherofmercy  001Dx00001HwE4PIAV  
196                misionerosdelespíritusanto  001Dx00001HwE3WIAV  
240              orderoffriarsminor,capuchins  001Dx00001HwE4FIAV  
247                       brothersofsaintjohn  001Dx00001HwE4MIAV

In [103]:
def parse_names(df, column_name):
    # Convert all non-string entries to strings (handling NaN and other data types)
    df[column_name] = df[column_name].fillna('').apply(str)

    # Create a new DataFrame to store the name parts
    name_parts = pd.DataFrame()

    # Parse each name in the column
    name_parts['First Name'] = df[column_name].apply(lambda x: HumanName(x).first if x.strip() != '' else '')
    name_parts['Last Name'] = df[column_name].apply(lambda x: HumanName(x).last if x.strip() != '' else '')
    name_parts['Middle Name'] = df[column_name].apply(lambda x: HumanName(x).middle if x.strip() != '' else '')
    name_parts['Title'] = df[column_name].apply(lambda x: HumanName(x).title if x.strip() != '' else '')
    name_parts['Suffix'] = df[column_name].apply(lambda x: HumanName(x).suffix if x.strip() != '' else '')
    name_parts['Nickname'] = df[column_name].apply(lambda x: HumanName(x).nickname if x.strip() != '' else '')

    # Combine the original DataFrame with the name parts DataFrame
    result_df = pd.concat([df, name_parts], axis=1)
    return result_df



In [104]:
!pip install nameparser
from nameparser import HumanName
from nameparser.config import CONSTANTS

# Add dataset-specific Titles and Suffix constants for parsing
CONSTANTS.titles.add('Rev.', 'Very Rev.', 'Very Rev', 'Sr.', 'Sr. ', 'Very', 'Bishop')
CONSTANTS.suffix_acronyms.add('FRS', 'OMI', 'OSA', 'OCD', 'OFM', 'OP', 'OC', 'FSE', 'OMV', 'SDB', 'SM', 'SFX', 'SP', 'OP', 'O.S.M', 'OSM' 'SNJM', 'OSF', 'HMRF', 'DD', 'CSJP', 'SDD', 'BVM', 'BVM - President', 'SJ')



SetManager({'dmin', 'ea', 'ifgict', 'mai', 'cph', 'chmc', 'faspen', 'cccm', 'smieee', 'cgc', 'apn aprn', 'pa-c', 'arm', 'o.s.m', 'fac-c', 'thm', 'csc', 'rhca', 'cpwa', 'asa', 'fieee', 'msa', 'caha', 'ceh', 'cgsp', 'cpsi', 'mph', 'emt-i/85', 'pt', 'dvm', 'bpi', 'lt', 'cap', 'nmd', 'jd', 'cmp', 'cro', 'kchs/dchs', 'osa', 'cpbe', 'els', 'cgma', 'cna', 'cma', 'cbnt', 'kcmg', 'edd', 'rn', 'kcvo', 'crna', 'cbte', 'ccp-c', 'cet', 'rba', 'fsdp', 'mieee', 'mvo', 'pci', 'mirm', 'diplom', 'uscg', 'gm', 'bts', 'agsf', 'lac', 'bca', 'ccc', 'dpm', 'crma', 'cpl', 'aca', 'cscp', 'uxc', 'fca', 'aia', 'che', 'usa', 'sscp', 'psyd', 'sasm', 'fec', 'rmsks', 'chp', 'drmp', 'tbr-ct', 'ccufc', 'pcc', 'kg', 'sj', 'do', 'ipep', 'cpa', 'cem', 'mpse', 'rfp', 'pe', 'git', 'gsmieee', 'ndtr', 'cmas', 'aqp', 'mem', 'cbv', 'ms', 'rdms', 'cpg', 'lp', 'abpp', 'cgb', 'fcela', 'dcm', 'fd', 'cltd', 'kcie', 'cpacc', 'dss', 'ocm', 'lvt', 'vd', 'cpe', 'cnm', '(vet)', 'asp', 'cera', 'lg', 'cia', 'chpe', 'cipm', 'rcp', 'cfre', 

In [105]:
# Parse Complex Names
acc_rel_superiors_parsed = parse_names(acc_rel_superiors, 'Major Superior Name')

In [106]:
acc_rel_superiors_staging = acc_rel_superiors_parsed.fillna('')

acc_rel_superiors_staging['Archdpdx_Migration_Id__c'] = acc_rel_superiors_staging['Major Superior Name'].apply(lambda x: x.replace(' ','').lower())

# Rename columns
acc_rel_superiors_staging = acc_rel_superiors_staging.rename(columns={
    'Major Superior Phone': 'Phone',
    'Major Superior Email': 'Email',
    'Title': 'Salutation',
    'First Name': 'FirstName',
    'Middle Name': 'MiddleName',
    'Last Name': 'LastName'
})

# Add job id
acc_rel_superiors_staging['Archdpdx_Job_Id__c'] = curr_job_id

# Drop columns
acc_rel_superiors_staging = acc_rel_superiors_staging.drop(columns=['Name', 'Major Superior Name', 'Nickname'])

# Drop empty rows
acc_rel_superiors_staging = acc_rel_superiors_staging[acc_rel_superiors_staging['LastName'].str.strip() != '']

acc_rel_superiors_staging.sample(10)

Phone                    Email  \
214        914-941-7575  maryknoll@mksisters.org   
234                                                
249     +39 06 61571401          pr@sancarlo.org   
203                           ipertine@socsj.org   
238  +91 80 74 51 02 67     rkappumkal@gmail.com   
254        510-658-8722    provincial@opwest.org   
245        617-536-4141        office@omvusa.org   
192        203-238-2243                            
222                                                
198        909-793-0424                            

                   Archdpdx_Migration_Id__c           AccountId    FirstName  \
214        sisterteresahougnon,mm,president  001Dx00001HwE3qIAF       Teresa   
234                      rev.seancarroll,sj  001Dx00001HwE3TIAV         Sean   
249                     fr.paolosottopietra  001Dx00001HwE4OIAV        Paolo   
203                         rev.ivanpertine  001Dx00001HwE3hIAF         Ivan   
238                      fr.kappumkalthomas  001Dx00001HwE4DIAV    Kappumkal   
254  veryrev.christopherfadok,op,provincial  001Dx00001HwE3dIAF  Christopher   
245                       fr.jimwalther,omv  001Dx00001HwE4KIAV          Jim   
192               mothermiriamseiferman,fse  001Dx00001HwE3YIAV       Miriam   
222                            sr.josephine  001Dx00001HwE3yIAF                
198               fr.matthewwilliams,o.c.d.  001Dx00001HwE3cIAF      Matthew   

        LastName MiddleName Salutation          Suffix  Archdpdx_Job_Id__c  
214      Hougnon                Sister   MM, President                 138  
234      Carroll                  Rev.              SJ                 138  
249  Sottopietra                   Fr.                                 138  
203      Pertine                  Rev.                                 138  
238       Thomas                   Fr.                                 138  
254        Fadok             Very Rev.  OP, Provincial                 138  
245      Walther                   Fr.             OMV                 138  
192    Seiferman                Mother             FSE                 138  
222    Josephine                   Sr.                                 138  
198     Williams                   Fr.          O.C.D.                 138

In [107]:
acc_rel_superiors_staging.sample(10)

Phone                      Email  \
222                                            
243                                            
207                                            
206                                            
224                                            
235  630-424-0401           schprov@ aol.com   
254  510-658-8722      provincial@opwest.org   
228                                            
191  610-502-1732    ajregionalusa@gmail.com   
210  973-403-3331  dominicans@caldwellop.org   

                      Archdpdx_Migration_Id__c           AccountId  \
222                               sr.josephine  001Dx00001HwE3yIAF   
243                               rogériogomes  001Dx00001HwE4IIAV   
207  sr.janehibbard,snjmmonasteryadministrator  001Dx00001HwE3VIAV   
206           sr.elisegarcía,opchapterprioress  001Dx00001HwE3kIAF   
224        sisterbarbaraschamber,sp,provinical  001Dx00001HwE40IAF   
235                         fr.jacekwalkiewicz  001Dx00001HwE4AIAV   
254     veryrev.christopherfadok,op,provincial  001Dx00001HwE3dIAF   
228                    sisterandreanenzel,csjp  001Dx00001HwE44IAF   
191                      reverendaugustineidra  001Dx00001HwE3XIAV   
210                           sr.luellaramm,op  001Dx00001HwE3mIAF   

       FirstName          LastName               MiddleName Salutation  \
222                      Josephine                                 Sr.   
243      Rogério             Gomes                                       
207         SNJM  Sr. Jane Hibbard  Monastery Administrator              
206           OP  Sr. Elise García         Chapter Prioress              
224      Barbara          Schamber                              Sister   
235        Jacek        Walkiewicz                                 Fr.   
254  Christopher             Fadok                           Very Rev.   
228       Andrea            Nenzel                              Sister   
191    Augustine              Idra                            Reverend   
210       Luella              Ramm                                 Sr.   

             Suffix  Archdpdx_Job_Id__c  
222                                 138  
243                                 138  
207                                 138  
206                                 138  
224  SP, Provinical                 138  
235                                 138  
254  OP, Provincial                 138  
228            CSJP                 138  
191                                 138  
210              OP                 138

In [108]:
# Send to CSV
acc_rel_superiors_staging.to_csv('staging_files/religious_superiors_staging.csv', encoding='utf-8-sig')

In [109]:
# Upsert to Salesforce

def find_existing_contact(sf, first_name, last_name):
    query = f"SELECT Id, Archdpdx_Migration_Id__c FROM Contact WHERE FirstName = '{first_name}' AND LastName = '{last_name}'"
    result = sf.query(query)
    return result['records']



bulk_data = []
for row in acc_rel_superiors_staging.itertuples(index=False):
    d = row._asdict()
    existing_contacts = find_existing_contact(sf, d['FirstName'], d['LastName'])
    if existing_contacts:
        # Update existing contact with external ID
        d['Id'] = existing_contacts[0]['Id']
        bulk_data.append(d)
    else:
        bulk_data.append(d)


if run_upserts == 'True':
    religious_superior_upsert = sf.bulk.Contact.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
    df_rel_superior_upsert = pd.DataFrame(religious_superior_upsert)

df_rel_superior_upsert

success  created                  id  \
0     False    False                None   
1      True    False  003Dx00000nKikgIAC   
2      True    False  003Dx00000nKikhIAC   
3      True    False  003Dx00000nKikiIAC   
4     False     True                None   
5      True    False  003Dx00000nKikjIAC   
6      True    False  003Dx00000nKikkIAC   
7     False    False                None   
8      True    False  003Dx00000nKiklIAC   
9      True    False  003Dx00000nKikmIAC   
10     True    False  003Dx00000nKiknIAC   
11     True    False  003Dx00000nKikoIAC   
12     True    False  003Dx00000nKikpIAC   
13     True    False  003Dx00000nKikqIAC   
14     True    False  003Dx00000nKikrIAC   
15     True    False  003Dx00000nKiksIAC   
16     True    False  003Dx00000nKiktIAC   
17     True    False  003Dx00000nKikuIAC   
18     True    False  003Dx00000nKikvIAC   
19     True    False  003Dx00000nKikwIAC   
20     True    False  003Dx00000nKikxIAC   
21     True    False  003Dx00000nKikyIAC   
22     True    False  003Dx00000nKikzIAC   
23     True    False  003Dx00000nKil0IAC   
24     True    False  003Dx00000nKil1IAC   
25     True    False  003Dx00000nKil2IAC   
26     True    False  003Dx00000nKil3IAC   
27    False     True                None   
28    False    False                None   
29    False     True                None   
30     True    False  003Dx00000nKil4IAC   
31     True    False  003Dx00000nKil5IAC   
32     True    False  003Dx00000nKil6IAC   
33     True    False  003Dx00000nKil7IAC   
34     True    False  003Dx00000nKil8IAC   
35     True    False  003Dx00000nKil9IAC   
36     True    False  003Dx00000nKilAIAS   
37     True    False  003Dx00000nKilBIAS   
38     True    False  003Dx00000nKilCIAS   
39     True    False  003Dx00000nKilDIAS   
40     True    False  003Dx00000nKilEIAS   
41    False    False                None   

                                               errors  
0   [{'statusCode': 'DUPLICATE_VALUE', 'message': ...  
1                                                  []  
2                                                  []  
3                                                  []  
4   [{'statusCode': 'INVALID_EMAIL_ADDRESS', 'mess...  
5                                                  []  
6                                                  []  
7   [{'statusCode': 'DUPLICATE_VALUE', 'message': ...  
8                                                  []  
9                                                  []  
10                                                 []  
11                                                 []  
12                                                 []  
13                                                 []  
14                                                 []  
15                                                 []  
16                                                 []  
17                                                 []  
18                                                 []  
19                                                 []  
20                                                 []  
21                                                 []  
22                                                 []  
23                                                 []  
24                                                 []  
25                                                 []  
26                                                 []  
27  [{'statusCode': 'STRING_TOO_LONG', 'message': ...  
28  [{'statusCode': 'DUPLICATE_VALUE', 'message': ...  
29  [{'statusCode': 'INVALID_EMAIL_ADDRESS', 'mess...  
30                                                 []  
31                                                 []  
32                                                 []  
33                                                 []  
34                                                 []  
35                                                 []  
36                                     

# CONTACTS


## Extract


In [111]:
import pandas as pd
df_contacts = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .set_index('Record Number', verify_integrity=True)
               .drop(index='recNum') # Drops the extra row that replicates the labels
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
)

df_contacts.sample(10)


Common_Name          Sort_Name  \
Record Number                                                 
2945                   Ms. Tanya Salazar      salazar tanya   
3109                       Mr. Ron Boyce   boyce ron joseph   
2690             Sr. Carole Strawn, SNJM      strawn carole   
1039                    Rev. Dirk Dunfee        dunfee dirk   
638                  Rev. Stephen Fister     fister stephen   
1678              Ms. Jenny Lopez-Garcia  lopezgarcia jenny   
1465                   Ms. Carmen Gaston      gaston carmen   
2431           Sr. Angela Mary Aldi, OSF   aldi angela mary   
740                     Rev. Karl Schray        schray karl   
1284           Rev. Anthony Patalano, OP   patalano anthony   

                          Type(s)    Clergy_Status Religious_Status Login_ID  \
Record Number                                                                  
2945                        Staff              NaN              NaN      NaN   
3109           Diaconate Inquirer              NaN              NaN   rboyce   
2690                    Religious              NaN           Active      NaN   
1039                       Priest  Transferred Out              NaN      NaN   
638                        Priest    Senior Status              NaN  ffister   
1678                        Staff              NaN              NaN      NaN   
1465                        Staff              NaN              NaN      NaN   
2431                    Religious              NaN           Active      NaN   
740                        Priest           Active              NaN  kschray   
1284             Priest,Religious  Transferred Out  Transferred Out      NaN   

                                                        Password  \
Record Number                                                      
2945                                                         NaN   
3109           1fe97d2547343488ec6876c77b8d4050ae52e281b4fdb8...   
2690                                                         NaN   
1039                                                         NaN   
638            bc7030a6b916b8f84f8109ca10bfb209ead1ce9f9ca949...   
1678                                                         NaN   
1465                                                         NaN   
2431                                                         NaN   
740            92f43484361a556913fe7362c8e89dca9979e502f0328b...   
1284                                                         NaN   

              Password_Must_be_Changed Access_Permission Spouse Title  \
Record Number                                                           
2945                               NaN               NaN      0   Ms.   
3109                               Yes               NaN   3110   Mr.   
2690                               NaN               NaN      0   Sr.   
1039                               NaN               NaN      0  Rev.   
638                                 No               NaN      0  Rev.   
1678                               NaN               NaN      0   Ms.   
1465                               NaN               NaN      0   Ms.   
2431                               NaN               NaN      0   Sr.   
740                                 No               NaN      0  Rev.   
1284                               NaN               NaN      0  Rev.   

              Salutation Christian_Name Nickname Middle_Name(s)       Surname  \
Record Number                                                                   
2945                 Ms.          Tanya      NaN            NaN       Salazar   
3109                 Mr.         Ronald      Ron         Joseph         Boyce   
2690                 Sr.         Carole      NaN            NaN        Strawn   
1039                 Fr.           Dirk      NaN            NaN        Dunfee   
638                  Fr.        Stephen      NaN            NaN        Fister   
1678                 Ms.          Jenny      NaN  

#### Get Photos


In [112]:
import os
import pandas as pd

# def list_jpeg_files(directory):
#     data = []
#     for filename in os.listdir(directory):
#         if filename.endswith(".jpeg") or filename.endswith(".jpg"):  # Checking for jpeg files
#             full_path = os.path.join(directory, filename)
#             data.append({'Filename': filename, 'Full Path': full_path})
#     return pd.DataFrame(data)

# # Specify your directory
# directory = '/content/drive/Shareddrives/Clients/ADPDX (Portland)/Data/Clergy DB/sql_backup/archdpdx.info backups/public_html/people/graphics/portraits/large'
# jpeg_files_df = list_jpeg_files(directory)


In [113]:
# # Query for the Library
# library_query = "SELECT Id, Name FROM ContentWorkspace WHERE Name = 'ADPDX Person Profile Photos'"
# library_result = sf.query(library_query)

# # Check if the library exists and get its ID
# if library_result['records']:
#     library_id = library_result['records'][0]['Id']
#     print(f"Library ID: {library_id}")

#     # Query for the Folder within the Library
#     folder_query = f"SELECT Id, Name FROM ContentFolder WHERE ParentContentFolderId = '{library_id}'"
#     folder_result = sf.query(folder_query)

#     # Check if the folder exists and get its ID
#     if folder_result['records']:
#         folder_id = folder_result['records'][0]['Id']
#         print(f"Folder ID: {folder_id}")
#     else:
#         print("Folder 'Large JPEGs' not found in the library.")
# else:
#     print("Library 'ADPDX Person Profile Photos' not found.")

## Analysis

Here we check the various columns and their types, count where values exist, count of unique values, sample data, etc.

DF shape:

- 142 columns
- 3017 rows


In [114]:
# Check the original shape of the imported CSV
print(f"Shape of original data set: {df_contacts.shape}")

# export to csv a list of the contact fields with count, unique, top, freq
contacts_describe = df_contacts.describe(include='all').transpose()
contacts_describe.to_csv(f'/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/analysis/contacts_describe.csv')

df_contacts.describe(include='all').transpose()  #initial analysis of the Contacts table

Shape of original data set: (3016, 141)


count unique                top  freq
Common_Name       3016   3011   Ms. Leslie Jones     2
Sort_Name         3016   3009     nguyen anthony     3
Type(s)           3016     29              Staff  1139
Clergy_Status     1138      8    Transferred Out   462
Religious_Status   902      4             Active   456
...                ...    ...                ...   ...
Place_of_Work      269    133  Mount Angel Abbey    37
Volunteer_Place     54     47       Mary’s Woods     4
Type_of_Work       276    117  Pastoral Ministry    30
Work_Load          262      2          Full Time   230
Work_Title         262    163           Reverend    26

[141 rows x 4 columns]

In [115]:
#How many spousal links are there? 

spouses_count = df_contacts[(df_contacts['Spouse'].notna()) & (df_contacts['Spouse'] != '0')].shape[0]
spouses_count

240

In [116]:
unique_reg_parishes = df_contacts['Registered_Parish'].value_counts()
unique_reg_parishes


0      2966
62        4
65        3
11        3
139       2
109       2
42        2
55        2
46        2
83        2
70        1
120       1
3         1
14        1
73        1
93        1
103       1
68        1
44        1
40        1
145       1
23        1
30        1
91        1
7         1
122       1
125       1
16        1
33        1
99        1
84        1
135       1
53        1
26        1
124       1
29        1
142       1
54        1
Name: Registered_Parish, dtype: int64

In [117]:
unique_languages = df_contacts['Languages'].unique()
unique_languages

array([nan, 'English,Spanish', 'Igbo', 'English, Spanish',
       'Spanish, Mayaqeqchi', 'Spanish (Mass only)',
       'Latin Mass and written translation. Read French, Italian, Spanish.',
       'Spanish', 'Hindi, Konkani, Tamil',
       'French (fluent), Spanish (beginner), Latin (beginner)',
       'German, Spanish, Italian, French', 'Kiswahili, Kichagga',
       'Spanish (English is second language)',
       'German, Spanish, Italian, Latin Mass',
       'English, Spanish, Italian', 'Spanish, Italian', 'English',
       'Bicolango, Tagalog, Spanish', 'Spanish, Italian, Latin Mass',
       'Italian', 'Tagalog, English, Spanish',
       'French, Italian, Aramaic (modern), Spanish', 'Vietnamese',
       'German, Spanish', 'English,Spanish,Italian',
       'Conversant in Italian and Spanish, some facility with Latin and German',
       'English, Spanish, Latin Mass', 'Italian, Spanish',
       'Konkani, Hindi, Marathi, Spanish',
       'Tagalog, Bicol, Spanish (Mass only)', 'Spanish, E

In [118]:
# import re
# import numpy as np


# def deduplicate_languages(list_languages):
#     # Define a regular expression pattern to match periods and punctuation
#     punctuation_pattern = r'[.,!?;:"]'

#     # Flatten the array and filter out NaN values
#     flattened_languages = [re.sub(punctuation_pattern, '', lang) for sublist in list_languages if pd.notna(sublist) for lang in sublist.split(',')]

#     # Deduplicate the list of languages
#     unique_languages = list(set(flattened_languages))

#     return unique_languages


# # Example usage:
# unique_languages = deduplicate_languages(unique_languages)
# print(unique_languages)


## Transform


In [119]:
# list of columns NOT to be migrated as Contact attributes
misc_columns_to_drop = [
    'Password',
    'Password_Must_be_Changed',
    'Sort_Name'
]

affiliation_columns = [
    'Baptism_Date',
    'Place_of_Baptism',
    'Confirmation_Date',
    'Place_of_Confirmation',
    'Received_Date',
    'Parish_of_Record',
    'Marriage_Date',
    'Place_of_Marriage',
    'Date_of_First_Vows',
    'Date_of_Final_Vows',
    'Reader_Date',
    'Acolyte_Date',
    'Bachelor_Degree_Year',
    'Bachelor_Degree_Type',
    'Bachelor_Degree_Institution',
    'Graduate_1_Degree_Institution',
    'Graduate_1_Degree_Type',
    'Graduate_1_Degree_Year',
    'Graduate_2_Degree_Institution',
    'Graduate_2_Degree_Type',
    'Graduate_2_Degree_Year',
    'Graduate_3_Degree_Institution',
    'Graduate_3_Degree_Type',
    'Graduate_3_Degree_Year',
    'Graduate_4_Degree_Institution',
    'Graduate_4_Degree_Type',
    'Graduate_4_Degree_Year',
    'Diaconal_Ordination_Date',
    'Diaconal_Ordination_Place',
    'Diaconal_Ordination_Prelate',
    'Presbyteral_Ordination_Date',
    'Presbyteral_Ordination_Place',
    'Presbyteral_Ordination_Prelate',
    'Episcopal_Ordination_Date',
    'Episcopal_Ordination_Place',
    'Episcopal_Ordination_Prelate',
    'Incardinated_From_Date',
    'Incardinated_From_Diocese',
    'Excardinated_To_Diocese',
    'Excardinated_To_Date',
    'Faculties',
    'Faculties_Granted_Date',
    'Faculties_Restricted_Date',
    'Faculties_Withdrawn_Date',
]

# These fields need to be KEPT but while building the SF upsert flow these are dropped temporarily until mapping logic is included.
# TODO

fields_not_yet_mapped = [
    'Common_Name', # is a concat, does not need to be mapped
    'Mailing_Address_Province', # non-impactful, can leave as dropped
    'Private_Address_Province', # non-impactful, can leave as dropped
    #'Social_Security_Account_Number__c',  # The data is encrypted
    'Serving_Now', # TBD - not sure if this is a field that needs to be migrated
    'Ordination_Diocese', # TBD... isn't this covered by Reg. Entry records? 
    'Registered_Parish' # decided will not migration on 2/21/2025

]

In [120]:
# UDF to combine multiple Mailing Street Address lines into one
def combine_addresses(row, *columns):
    address_parts = []
    for col in columns:
        value = row[col]
        if pd.notnull(value):  # Check for non-null values
            address_parts.append(str(value))  # Convert to string
    return '\n'.join(address_parts)  # '\n' for line break

In [121]:
df_contact_staging = (df_contacts
                      .drop(columns='Salutation')
                      .rename(columns={
                          'Clergy_Status' : 'ADPDX_Clergy_Status__c',
                          'Religious_Status' : 'ADPDX_Religious_Status__c',
                          'Login_ID' : 'ADPDX_Login_ID__c',
                          'Access_Permission': 'ADPDX_Access_Permission__c',
                          'Title': 'Salutation',
                          'Christian_Name': 'FirstName',
                          'Middle_Name(s)': 'MiddleName',
                          'Surname': 'LastName',
                          'Suffix': 'Suffix',
                          'Preferred_Address': 'Preferred_Address__c',
                          'Mailing_Address_City': 'MailingCity',
                          'Mailing_Address_State': 'MailingState',
                          'Mailing_Address_Postal_Code': 'MailingPostalCode',
                          'Mailing_Address_Country': 'MailingCountry',
                          'Private_Address_City': 'OtherCity',
                          'Private_Address_State': 'OtherState',
                          'Private_Address_Postal_Code': 'OtherPostalCode',
                          'Private_Address_Country': 'OtherCountry',
                          'Work_Phone': 'npe01__WorkPhone__c',
                          'Home_Phone': 'HomePhone',
                          'Cell_Phone': 'MobilePhone',
                          'Preferred_Phone': 'npe01__PreferredPhone__c',
                          # IF Preferred phone contains, 'do not publish'
                          'Work_Email' : 'npe01__WorkEmail__c',
                          'Archdiocesan_Email': 'npe01__AlternateEmail__c',
                          'Home_Email': 'npe01__HomeEmail__c',
                          'Preferred_Email': 'npe01__Preferred_Email__c',
                          # IF Preferred email contains 'do not publish''
                          'Directory_Include': 'Directory_Include__c',
                          'Directory_Include_Middle_Name': 'Directory_Include_Middle_Name__c',
                          'Directory_Include_Suffix': 'Directory_Include_Suffix__c',
                          'Suppress_From_Reports': 'Suppress_From_Reports__c',
                          'Send_Group_Mail_and_Email': 'Send_Group_Mail_and_Email__c',
                          'Birth_Date': 'Birthdate',
                          'Place_of_Birth': 'mbfc__Place_of_Birth__c',
                          'Foreign_Born': 'Foreign_Born__c',
                          'Foreign_Citizenship': 'Foreign_Citizenship__c',
                          'Immigration_Status': 'Immigration_Status__c',
                          'Passport/Visa_Expiration_Date': 'Passport_Visa_Expiration_Date__c',
                          'Social_Security_Account_Number': 'Social_Security_Number__c',
                          'Deceased_Date': 'mbfc__Date_of_Death__c',
                          'Out_of_Diocese_Date': 'mbfc__Date_Left_Diocese__c', 
                          'CARA_Ethnicity': 'adpdx_CARA_Ethnicity__c',
                          'Seminarian_Status': 'adpdx_Seminarian_Status__c',
                          'Other_Diaconal_Ministry': 'adpdx_Other_Diaconal_Ministry__c',
                          'Spiritual_Director_Authorized': 'adpdx_Spiritual_Director_Authorized__c',
                          'Place_of_Work': 'adpdx_Place_of_Work__c',
                          'Volunteer_Place': 'adpdx_Volunteer_Place__c',
                          'Type_of_Work': 'adpdx_Type_of_Work__c',
                          'Work_Load': 'adpdx_Work_Load__c',
                          'Work_Title': 'adpdx_Work_Title__c',
                          'Coverage_Availability': 'adpdx_Coverage_Availability__c', 
                          'Advanced_Directive_Date': 'adpdx_Advanced_Directive_Date__c',
                          'End_of_Life_Plan_Date': 'adpdx_End_of_Life_Plan_Date__c',
                          'Will_Date': 'adpdx_Will_Date__c',
                          'Will_Note': 'adpdx_Will_Note__c',
                          'CIC_489_File': 'adpdx_CIC_489_File__c',
                          'Senior_Status_Date': 'adpdx_Senior_Status_Date__c', 
                          'Laicized_Date': 'adpdx_Laicized_Date__c',
                          'Seminarian_Student_Debt': 'adpdx_Seminarian_Student_Debt__c',
                          'Seminarian_Medical_Benefits': 'adpdx_Seminarian_Medical_Benefits__c',
                          'Candidacy_Date': 'adpdx_Candidacy_Date__c',
                          'Accepted_to_Formation_Date': 'adpdx_Accepted_to_Formation_Date__c',
                          'Formation_Withdrawn_Date': 'adpdx_Formation_Withdrawn_Date__c',
                          'Formation_Deferred_Date': 'adpdx_Formation_Deferred_Date__c',
                          'Formation_Terminated_Date': 'adpdx_Formation_Terminated_Date__c',
                          'Terminate_or_Defer_Note': 'adpdx_Terminate_or_Defer_Note__c',
                          'CARA_Highest_Ed_Level': 'adpdx_CARA_Highest_Ed_Level__c',
                          'Letter_of_Good_Standing_Date': 'adpdx_Letter_of_Good_Standing__c',
                          'Religious_In_Archdiocese_Date': 'mbfc__Date_of_Arrival_in_Diocese__c',
                          'Last_Retreat_Date': 'adpdx_Last_Retreat_Date__c',
                          'Last_Educ_Requirement_Date': 'adpdx_Last_Educ_Requirement_Date__c',
                          'Policy_Manual_Acknowledgement_Date': 'adpdx_Policy_Manual_Acknowledgement_Date__c',
                          'Harassment_Prevention_Course_Date': 'adpdx_Harassment_Prevention_Course_Date__c',
                          'Standards_of_Conduct_Date': 'adpdx_Standards_of_Conduct_Date__c',
                          'Last_Background_Check_Date': 'adpdx_Last_Background_Check_Date__c',
                          'Last_Child_Protection_Training_Date': 'adpdx_Last_Child_Protection_Training__c',
                          'Languages': 'Languages__c',
                          'Nickname': 'adpdx_Preferred_Name__c',
                          'Father_Full_Name': 'Father_Full_Name__c',
                          'Mother_Full_Maiden_Name': 'Mother_Full_Maiden_Name__c'

                          })
                      .assign(Bi_Ritual__c=lambda x: x['Type(s)'].str.contains('Biritual'))
                      .assign(Non_Latin_Rite__c=lambda x: x['Type(s)'].str.contains('Non-Latin Rite'))
                      .assign(adpdx_Discerner_Aspirant_for_Diaconate__c=lambda x: x['Type(s)'].str.contains('Diaconate'))
                      .assign(adpdx_Is_Seminarian__c=lambda x: x['Type(s)'].str.contains('Seminar'))
                      
                      .assign(Archdpdx_Migration_Id__c=lambda x: x.index)
                      .assign(MailingStreet=lambda x: x.apply(lambda row: combine_addresses(row, 'Mailing_Address', 'Mailing_Address_2'), axis=1))
                      .drop(columns=['Mailing_Address', 'Mailing_Address_2'])  # Optional: Drop original columns if not needed
                      .assign(OtherStreet=lambda x: x.apply(lambda row: combine_addresses(row, 'Private_Address', 'Private_Address_2'), axis=1))
                      .drop(columns=['Private_Address', 'Private_Address_2'])  # Optional: Drop original columns if not needed
                      .drop(columns=misc_columns_to_drop)
                      .drop(columns=affiliation_columns)
                      .drop(columns=fields_not_yet_mapped)

        )


In [122]:
# For use in the 'Contacts > Spouses' section
df_contact_staging_spouses = df_contact_staging.copy(deep=True)


In [123]:
df_contact_staging_spouses['Spouse']

Record Number
2766    0
2337    0
3244    0
3295    0
2164    0
       ..
1670    0
2755    0
1962    0
2202    0
1866    0
Name: Spouse, Length: 3016, dtype: object

In [124]:
df_contact_staging.drop(columns=['Spouse'], inplace=True)

In [125]:
df_contact_staging.columns

Index(['Type(s)', 'ADPDX_Clergy_Status__c', 'ADPDX_Religious_Status__c',
       'ADPDX_Login_ID__c', 'ADPDX_Access_Permission__c', 'Salutation',
       'FirstName', 'adpdx_Preferred_Name__c', 'MiddleName', 'LastName',
       'Suffix', 'MailingCity', 'MailingState', 'MailingPostalCode',
       'MailingCountry', 'OtherCity', 'OtherState', 'OtherPostalCode',
       'OtherCountry', 'Preferred_Address__c', 'npe01__WorkPhone__c',
       'HomePhone', 'MobilePhone', 'npe01__PreferredPhone__c',
       'npe01__WorkEmail__c', 'npe01__AlternateEmail__c',
       'npe01__HomeEmail__c', 'npe01__Preferred_Email__c',
       'Directory_Include__c', 'Directory_Include_Middle_Name__c',
       'Directory_Include_Suffix__c', 'Suppress_From_Reports__c',
       'adpdx_Seminarian_Student_Debt__c',
       'adpdx_Seminarian_Medical_Benefits__c', 'Send_Group_Mail_and_Email__c',
       'Birthdate', 'mbfc__Place_of_Birth__c', 'Foreign_Born__c',
       'Father_Full_Name__c', 'Mother_Full_Maiden_Name__c',
       'For

In [126]:
df_contact_staging.MailingStreet.sample(10)

Record Number
80                                                  
179                                                 
236                                                 
2163                 St. Henry Parish\n346 NW 1st St
889                                                 
3185    St. Andre Bessette Parish\n601 W Burnside St
3133               Ascension Parish\n743 SE 76th Ave
2389                St. Luke Parish\n417 Harrison St
1501        Gethsemani Cemetery\n11666 SE Stevens Rd
2328       The Madeleine School\n3240 NE 23rd Avenue
Name: MailingStreet, dtype: object

### Gender

In [127]:
# Function to determine gender based on 'Type(s)' field
def determine_gender(row):
    if any(x in row['Type(s)'] for x in ['Bishop', 'Priest', 'Transitional Deacon', 'Permanent Deacon', 'Diaconate Formation', 'Diaconate Inquirer', 'Seminarian', 'Seminary Applicant']):
        return 'Male'
    elif 'Religious' in row['Type(s)'] and 'Br.' in row['Salutation']:
        return 'Male'
    elif 'Wife' in row['Type(s)'] or ('Religious' in row['Type(s)'] and 'Sr.' in row['Salutation']):
        return 'Female'
    elif any(x in row['Type(s)'] for x in ['Staff', 'Archive']):
        if row['Salutation'] == 'Ms.':
            return 'Female'
        elif row['Salutation'] == 'Mr.':
            return 'Male'
    else:
        return ''

In [128]:
# Apply the function to the DataFrame to create the new column
df_contact_staging['mbfc__gender__c'] = df_contact_staging.apply(determine_gender, axis=1)


In [129]:
df_contact_staging['mbfc__gender__c'].value_counts()

Male      1715
Female    1272
             3
Name: mbfc__gender__c, dtype: int64

### Languages


In [130]:
# # Define a function to clean the 'languages' column

# import re
# def clean_languages(text):
#     if pd.isna(text):
#         return text
#     # Remove text inside parentheses
#     text = re.sub(r'\(.*?\)', '', text)
#     # Replace ' & ' or ' and ' with ';'
#     text = re.sub(r' & | and ', ';', text)
#     # Replace commas with semicolons
#     text = text.replace(',', ';')
#     # Remove spaces before and after semicolons
#     text = re.sub(r'\s*;\s*', ';', text)
#     return text.strip(';')

# # Apply the cleaning function to the 'languages' column
# df_contact_staging['Languages__c'] = df_contact_staging['Languages__c'].apply(clean_languages)


### Private Address Handling


In [131]:
# If 'OtherStreet' is not null, then set Secondary Address Type to 'Private'.  This is because the 'OtherAddress' fields all come from the 'Private' address fields in source system. 
df_contact_staging['npe01__Secondary_Address_Type__c'] = df_contact_staging['OtherStreet'].apply(lambda x: 'Private' if pd.notnull(x) else None)


### Handle Boolean Fields


In [132]:
boolean_columns_to_convert = ['Foreign_Born__c', 'Directory_Include__c', 'Directory_Include_Middle_Name__c', 'Directory_Include_Suffix__c',
       'Suppress_From_Reports__c', 'Send_Group_Mail_and_Email__c', ]

df_contact_staging[boolean_columns_to_convert] = df_contact_staging[boolean_columns_to_convert].replace({'Yes': True, 'No': False})


In [133]:
df_contact_staging[boolean_columns_to_convert] = df_contact_staging[boolean_columns_to_convert].fillna(False)

df_contact_staging[boolean_columns_to_convert].sample(5)

Foreign_Born__c  Directory_Include__c  \
Record Number                                          
2933                     False                 False   
2161                     False                 False   
1434                     False                 False   
2478                     False                  True   
32                       False                 False   

               Directory_Include_Middle_Name__c  Directory_Include_Suffix__c  \
Record Number                                                                  
2933                                      False                        False   
2161                                      False                        False   
1434                                      False                        False   
2478                                      False                        False   
32                                        False                        False   

               Suppress_From_Reports__c  Send_Group_Mail_and_Email__c  
Record Number                                                          
2933                              False                          True  
2161                              False                          True  
1434                              False                         False  
2478                              False                          True  
32                                False                         False

### Set Contact Record Type


In [134]:
# Set Record Type

# Go down row by row and check the 'Type(s)' columns, check for certain words that are keys in a dictionary, and
# the that row's 'Type(s)' field contains a string that is in the a key in a dictionary the update another columns
# called 'ContactRecordType' with the paired value.

contact_type_map = {
    'Bishop': 'Priest',
    'Priest': 'Priest',
    'Transitional Deacon': 'Permanent_Deacon',
    'Permanent Deacon': 'Permanent_Deacon',
    'Seminarian': 'Lay_Person',
    'Diaconate Formation': 'Lay_Person',
    'Seminary Applicant': 'Lay_Person',
    'Diaconate Inquirer': 'Lay_Person',
    'Wife': 'Lay_Person',
    'Religious': 'Religious',
    'Staff': 'Lay_Person',
    'Seminary Applicant': 'Lay_Person',
    'Archive': 'Lay_Person'
}

def update_contact_record_type(row):
    for key, value in contact_type_map.items():
        if key in row['Type(s)']:
            return value
    return None

df_contact_staging['ContactRecordType'] = df_contact_staging.apply(update_contact_record_type, axis=1)

In [135]:
# Set Candidate_Type__c field

candidate_types = ['Seminary Applicant', 'Diaconate Inquirer', 'Diaconate Formation', 'Seminarian']

# Function to update the 'candidate_type__c' column based on 'Type(s)' field
def update_candidate_type(row):
    if row['Type(s)'] in candidate_types:
        return row['Type(s)']
    return ''

# Apply the function to the DataFrame to create the new column
df_contact_staging['candidate_type__c'] = df_contact_staging.apply(update_candidate_type, axis=1)


In [136]:
# Map in the RecordTypeIDs
df_contact_staging['RecordTypeID'] = df_contact_staging['ContactRecordType'].map(record_types_mapping)

### Ecclesial Status & Ministerial Status


In [137]:
df_contact_staging

Type(s) ADPDX_Clergy_Status__c ADPDX_Religious_Status__c  \
Record Number                                                               
2766              Priest        Transferred Out                       NaN   
2337               Staff                    NaN                       NaN   
3244               Staff                    NaN                       NaN   
3295               Staff                    NaN                       NaN   
2164               Staff                    NaN                       NaN   
...                  ...                    ...                       ...   
1670               Staff                    NaN                       NaN   
2755           Religious                    NaN                    Active   
1962               Staff                    NaN                       NaN   
2202               Staff                    NaN                       NaN   
1866               Staff                    NaN                       NaN   

              ADPDX_Login_ID__c ADPDX_Access_Permission__c Salutation  \
Record Number                                                           
2766                   sabukaka                        NaN       Rev.   
2337                        NaN                        NaN        Mr.   
3244                        NaN                        NaN        Mr.   
3295                        NaN                        NaN        Ms.   
2164                        NaN                        NaN        Ms.   
...                         ...                        ...        ...   
1670                        NaN                        NaN        Ms.   
2755                  dzorrilla                        NaN        Br.   
1962                        NaN                        NaN        Ms.   
2202                        NaN                        NaN        Ms.   
1866                        NaN                        NaN        Ms.   

              FirstName adpdx_Preferred_Name__c MiddleName  LastName Suffix  \
Record Number                                                                 
2766            Stephen                     NaN    Ozovehe  Abaukaka    NaN   
2337            Rogelio                     NaN        NaN   Acevedo    NaN   
3244               Sean                     NaN        NaN   Ackroyd    NaN   
3295            Sherril                     NaN        NaN     Acton    NaN   
2164            Barbara                     NaN        NaN     Adams    NaN   
...                 ...                     ...        ...       ...    ...   
1670              Jenny                     NaN        NaN  Zomerdyk    NaN   
2755             Daniel                     NaN        NaN  Zorrilla    NaN   
1962                Kim                     NaN        NaN     Zuber    NaN   
2202              Agnes                     NaN        NaN    Zueger    NaN   
1866             Laurie                     NaN        NaN    Zupsic    NaN   

                  MailingCity MailingState MailingPostalCode MailingCountry  \
Record Number                                                                 
2766                 Tualatin           OR             97062            NaN   
2337                 Portland           OR             97229            NaN   
3244                Corvallis           OR             97330            NaN   
3295                   Eugene           OR             97401            NaN   
2164                  Gresham           OR             97030            NaN   
...                       ...          ...               ...            ...   
1670            Central Point           OR             97502            NaN   
2755           Saint Benedict           OR             97373            NaN   
1962                Sublimity           OR             97385            NaN   
2202              Lake Oswego           OR             97034            NaN   
1866                 Portland           OR             97219            NaN   

         

In [ ]:
def determine_ecclesial_status(df):
    def ecclesial_status(row):
        if pd.notna(row['ADPDX_Clergy_Status__c']) and 'Laicized' in row['ADPDX_Clergy_Status__c']:
            return 'Laicized'
        # elif pd.notna(row['ADPDX_Clergy_Status__c']) and 'Faculties Withdrawn' in row['ADPDX_Clergy_Status__c']:
        #     return 'Faculties Withdrawn'
        elif pd.notna(row['Type(s)']) and 'Bishop' in row['Type(s)']:
            return 'Bishop/Archbishop'
        elif pd.notna(row['Type(s)']) and 'Priest,Religious' in row['Type(s)']:
            return 'Priest - Religious'
        elif pd.notna(row['Type(s)']) and 'Priest' in row['Type(s)'] and (not pd.isna(row['Foreign_Citizenship__c']) or row['Incardinated_Now'] != 'Archdiocese of Portland in Oregon'):
            return 'Priest - Extern'
        elif pd.notna(row['Type(s)']) and 'Priest' in row['Type(s)'] and (pd.isna(row['Foreign_Citizenship__c']) and row['Incardinated_Now'] == 'Archdiocese of Portland in Oregon'):
            return 'Priest - Diocesan'
        elif pd.notna(row['Type(s)']) and 'Transitional Deacon' in row['Type(s)']:
            return 'Transitional Deacon'
        elif pd.notna(row['Type(s)']) and row['Type(s)'] == 'Permanent Deacon':
            return 'Permanent Deacon'
        elif pd.notna(row['Type(s)']) and row['Type(s)'] == 'Religious' and row['Salutation'] == 'Br.':
            return 'Professed Male Religious (Non-Priest)'
        elif pd.notna(row['Type(s)']) and row['Type(s)'] == 'Religious' and row['Salutation'] == 'Sr.':
            return 'Professed Female Religious'
        elif pd.notna(row['Type(s)']) and row['Type(s)'] == 'Religious,Staff' and row['Salutation'] == 'Sr.':
            return 'Professed Female Religious'
        elif pd.notna(row['Type(s)']) and row['Type(s)'] == 'Wife':
            return 'Lay Person'
        elif row['Salutation'] == 'Mr.':
            return 'Lay Person'
        elif row['Salutation'] == 'Ms.':
            return 'Lay Person'
        elif row['Salutation'] == 'Mrs.':
            return 'Lay Person'
        elif row['Salutation'] == 'Rev.':
            return 'Unknown'
        else:
            return None

    df['mbfc__Ecclesial_Status__c'] = df.apply(ecclesial_status, axis=1)
    return df


df_contact_staging = determine_ecclesial_status(df_contact_staging)

In [139]:
df_contact_staging.sample(20)

Type(s) ADPDX_Clergy_Status__c  \
Record Number                                            
70                         Wife                    NaN   
2720                  Religious                    NaN   
1879                      Staff                    NaN   
1655                      Staff                    NaN   
2749           Priest,Religious        Transferred Out   
3297                      Staff                    NaN   
1673                      Staff                    NaN   
996            Priest,Religious        Transferred Out   
6                          Wife                    NaN   
2562                  Religious                    NaN   
1552                    Archive                    NaN   
1579                      Staff                    NaN   
2693                  Religious                    NaN   
3251                      Staff                    NaN   
2495                  Religious                    NaN   
1249           Priest,Religious        Transferred Out   
229                     Archive                    NaN   
1027           Priest,Religious        Transferred Out   
1084           Priest,Religious        Transferred Out   
2660                  Religious                    NaN   

              ADPDX_Religious_Status__c ADPDX_Login_ID__c  \
Record Number                                               
70                                  NaN         bespinoza   
2720                             Active               NaN   
1879                                NaN               NaN   
1655                                NaN               NaN   
2749                    Transferred Out            jmejia   
3297                                NaN               NaN   
1673                                NaN               NaN   
996                     Transferred Out               NaN   
6                                   NaN          pacramer   
2562                             Active               NaN   
1552                                NaN               NaN   
1579                                NaN          agodfrey   
2693                             Active               NaN   
3251                                NaN               NaN   
2495                             Active               NaN   
1249                    Transferred Out               NaN   
229                                 NaN               NaN   
1027                    Transferred Out               NaN   
1084                    Transferred Out               NaN   
2660                             Active               NaN   

                                      ADPDX_Access_Permission__c Salutation  \
Record Number                                                                 
70                                                           NaN       Mrs.   
2720                                                         NaN        Sr.   
1879                                                         NaN        Ms.   
1655                                                         NaN        Ms.   
2749                                                         NaN       Rev.   
3297                                                         NaN        Ms.   
1673                                                         NaN        Ms.   
996                                                          NaN       Rev.   
6                                                            NaN       Mrs.   
2562                                                         NaN        Sr.   
1552                                                         NaN        Mr.   
1579           clergy,newman-*,office-*,parish-*,rel-*,vicari...       Mrs.   
2693                                                         NaN        Sr.   
3251                                                         NaN        Mr.   
2495                                                         NaN        Sr.   
1249                                                         

In [140]:
# This function is no longer used due to ADPDX's custom enhancement in which a Flow automatically updates this status. 

def determine_ministerial_status(df):
    def ministerial_status(row):
        if row['ADPDX_Clergy_Status__c'] == 'Deceased':
            return 'Deceased'
        elif row['ADPDX_Clergy_Status__c'] == 'Active':
            return 'Active in Ministry'
        elif row['ADPDX_Clergy_Status__c'] == 'Inactive':
            return 'Inactive'
        elif row['ADPDX_Clergy_Status__c'] == 'Senior Status':
            return 'Senior Status'
        elif row['ADPDX_Clergy_Status__c'] == 'Faculties Withdrawn':
            return 'Faculties Withdrawn'
        elif row['ADPDX_Clergy_Status__c'] == 'Transferred Out':
            return 'Left Diocese'
        elif row['ADPDX_Clergy_Status__c'] == 'Unassigned':
            return 'Unassigned'
        elif row['ADPDX_Clergy_Status__c'] == 'Laicized':
            return 'Laicized'
        else:
            return 'Unknown'
        
    df['mbfc__Ministerial_Status__c'] = df.apply(ministerial_status, axis=1)
    return df

# df_contact_staging = determine_ministerial_status(df_contact_staging)

### Preferred Phone & Email


In [141]:
df_contact_staging['npe01__PreferredPhone__c'] = df_contact_staging['npe01__PreferredPhone__c'].fillna('Work')
df_contact_staging['npe01__Preferred_Email__c'] = df_contact_staging['npe01__Preferred_Email__c'].fillna('Work')

### Remove Addresses for Lay People


In [142]:
def remove_mailing_address_for_lay_person(row):
    if row['ContactRecordType'] == 'Lay_Person':
        row['MailingStreet'] = ''
        row['MailingCity'] = ''
        row['MailingState'] = ''
        row['MailingPostalCode'] = ''
        row['MailingCountry'] = ''
    return row

df_contact_staging = df_contact_staging.apply(remove_mailing_address_for_lay_person, axis=1)

### Religious Congregation

In this section, for those Contacts who have a value in the `Link to Religious Community` source field we need to populate the `mbfc__Religious_Order__c` target field in Salesforce with the correct Religious Community's parent account - the Religious Congregation.

NOTE: In the source data, there is no differentiation between a child Religious Community and a parent Religious Order, there is only one record for the Religious Comnmunity. In MF360 we represent these Accounts separately so we need to first (a) get the Religious Community record using the `Link to Religious Community` value but transforming it (adding 'RelCommunities\_' in front of the value) so it matches the Archdpdx_Migration_Id\_\_c in Salesforce.

Once acquired, (b) we need to get the value of the `ParentID` field on the Religious Community which is the ID of the Religious Congregation record. That ID is the value we then want to populate in the `mbfc__Religious_Order__c` field.


In [143]:
# get SF Account
get_all_accounts = 'Select Id, Name, RecordTypeId, Type, mbfc__Parish_Code__c, Job_Id__c, Archdpdx_Migration_Id__c, ParentID from Account WHERE Archdpdx_Migration_Id__c != null'

# get list of records, add to dataframe
sf_accounts = sf.query(get_all_accounts)
df_sf_accounts = pd.DataFrame(sf_accounts['records'])
df_sf_accounts = df_sf_accounts.drop(columns = 'attributes')

# create a dict in order to apply later
accounts_id_map = df_sf_accounts.set_index('Archdpdx_Migration_Id__c')['Id'].to_dict()

In [144]:
df_sf_accounts[df_sf_accounts['Archdpdx_Migration_Id__c'].str.contains('RelCommunities', na=False)]

Id                                               Name  \
228  001Dx00001HwE4dIAF         Colombiere Jesuit Community, Portland (SJ)   
229  001Dx00001HwE4jIAF  Franciscan Sisters of the Eucharist, Bridal Ve...   
230  001Dx00001HwE4kIAF          Apostolic Life Community, Portland (ALCP)   
231  001Dx00001HwE4lIAF  Blessed Stephen Bellesini Community, c/o Chanc...   
232  001Dx00001HwE4mIAF  Canisius Jesuit Community at Jesuit High Schoo...   
..                  ...                                                ...   
293  001Dx00001HwE5hIAF  Society of Our Lady of the Most Holy Trinity, ...   
294  001Dx00001HwE4hIAF  Missionaries of the Holy Spirit Provincial Hou...   
295  001Dx00001HwE5iIAF          Community of St. Thomas More, Eugene (OP)   
296  001Dx00001HwE5jIAF         Saint Benedict Lodge, McKenzie Bridge (OP)   
297  001Dx00001HwE4iIAF                  Apostles of Jesus, Beaverton (AJ)   

           RecordTypeId  Type mbfc__Parish_Code__c Job_Id__c  \
228  012Dx0000003p52IAA  None                 None       138   
229  012Dx0000003p52IAA  None                 None       138   
230  012Dx0000003p52IAA  None                 None       138   
231  012Dx0000003p52IAA  None                 None       138   
232  012Dx0000003p52IAA  None                 None       138   
..                  ...   ...                  ...       ...   
293  012Dx0000003p52IAA  None                 None       138   
294  012Dx0000003p52IAA  None                 None       138   
295  012Dx0000003p52IAA  None                 None       138   
296  012Dx0000003p52IAA  None                 None       138   
297  012Dx0000003p52IAA  None                 None       138   

    Archdpdx_Migration_Id__c            ParentId  
228         RelCommunities_1  001Dx00001HwE3TIAV  
229        RelCommunities_10  001Dx00001HwE3YIAV  
230        RelCommunities_11  001Dx00001HwE3ZIAV  
231        RelCommunities_12  001Dx00001HwE3aIAF  
232        RelCommunities_13  001Dx00001HwE3TIAV  
..                       ...                 ...  
293        RelCommunities_79  001Dx00001HwE4SIAV  
294         RelCommunities_8  001Dx00001HwE3WIAV  
295        RelCommunities_80  001Dx00001HwE3dIAF  
296        RelCommunities_81  001Dx00001HwE3dIAF  
297         RelCommunities_9  001Dx00001HwE3XIAV  

[70 rows x 8 columns]

In [145]:
# applies a lambda function to each element in the ‘Link_to_Religious_Community’ column, prefixing the value with 'RelCommunities_'
def transform_religious_community_link(df):
    df['Link_to_Religious_Community'] = df['Link_to_Religious_Community'].apply(
        lambda x: None if x == '0' else f'RelCommunities_{x}'
    )
    return df

# This function searches for a record in the sf_accounts DataFrame where the ‘Archdpdx_Migration_Id__c’ column matches the given archdpdx_migration_id
def get_parent_id_from_salesforce(sf_accounts, archdpdx_migration_id):
    print(f"Searching for: {archdpdx_migration_id}")  # Debug print
    matching_record = sf_accounts[sf_accounts['Archdpdx_Migration_Id__c'] == archdpdx_migration_id]
    if not matching_record.empty:
        print(f"Found: {matching_record['ParentId'].values[0]}")  # Debug print
        return matching_record['ParentId'].values[0]
    print("Not found")  # Debug print
    return None

# uses the get_parent_id_from_salesforce function to find the ‘ParentId’ from the sf_accounts DataFrame
def update_religious_order(df, sf_accounts):
    df['mbfc__Religious_Order__c'] = df.apply(
        lambda row: get_parent_id_from_salesforce(sf_accounts, row['Link_to_Religious_Community']) 
        if row['Link_to_Religious_Community'] is not None else None, axis=1
    )
    return df


# run the transform_religious_community_link and update_religious_order functions
df_contact_staging = transform_religious_community_link(df_contact_staging)

df_contact_staging = update_religious_order(df_contact_staging, df_sf_accounts)

Searching for: RelCommunities_60
Found: 001Dx00001HwE3TIAV
Searching for: RelCommunities_53
Found: 001Dx00001HwE45IAF
Searching for: RelCommunities_9
Found: 001Dx00001HwE3XIAV
Searching for: RelCommunities_4
Found: 001Dx00001HwE3VIAV
Searching for: RelCommunities_8
Found: 001Dx00001HwE3WIAV
Searching for: RelCommunities_35
Found: 001Dx00001HwE3nIAF
Searching for: RelCommunities_1
Found: 001Dx00001HwE3TIAV
Searching for: RelCommunities_23
Found: 001Dx00001HwE3gIAF
Searching for: RelCommunities_56
Found: 001Dx00001HwE48IAF
Searching for: RelCommunities_23
Found: 001Dx00001HwE3gIAF
Searching for: RelCommunities_53
Found: 001Dx00001HwE45IAF
Searching for: RelCommunities_60
Found: 001Dx00001HwE3TIAV
Searching for: RelCommunities_1
Found: 001Dx00001HwE3TIAV
Searching for: RelCommunities_27
Found: 001Dx00001HwE3iIAF
Searching for: RelCommunities_44
Found: 001Dx00001HwE3wIAF
Searching for: RelCommunities_23
Found: 001Dx00001HwE3gIAF
Searching for: RelCommunities_44
Found: 001Dx00001HwE3wIAF
Se

In [146]:
df_contact_staging[df_contact_staging.mbfc__Religious_Order__c.isna() == False]

Type(s) ADPDX_Clergy_Status__c  \
Record Number                                            
671            Priest,Religious        Transferred Out   
2430                  Religious                    NaN   
1584           Priest,Religious                 Active   
912            Priest,Religious        Transferred Out   
913            Priest,Religious        Transferred Out   
...                         ...                    ...   
2884           Priest,Religious        Transferred Out   
1434           Priest,Religious               Deceased   
1435           Priest,Religious        Transferred Out   
787            Priest,Religious          Senior Status   
2755                  Religious                    NaN   

              ADPDX_Religious_Status__c ADPDX_Login_ID__c  \
Record Number                                               
671                     Transferred Out            jadams   
2430                             Active               NaN   
1584                             Active            makuti   
912                     Transferred Out               NaN   
913                     Transferred Out               NaN   
...                                 ...               ...   
2884                    Transferred Out             pyoun   
1434                           Deceased               NaN   
1435                    Transferred Out               NaN   
787                             Retired           nzodrow   
2755                             Active         dzorrilla   

              ADPDX_Access_Permission__c Salutation  FirstName  \
Record Number                                                    
671                                  NaN       Rev.         J.   
2430                                 NaN        Sr.    Delores   
1584                                 NaN       Rev.  Macdonald   
912                                  NaN   Rt. Rev.      James   
913                                  NaN       Rev.       Jose   
...                                  ...        ...        ...   
2884                                 NaN       Rev.       Pius   
1434                                 NaN       Rev.     Jerome   
1435                                 NaN       Rev.     Robert   
787                                  NaN   Rt. Rev.     Nathan   
2755                                 NaN        Br.     Daniel   

              adpdx_Preferred_Name__c MiddleName  LastName Suffix  \
Record Number                                                       
671                              J.K.         K.     Adams    III   
2430                              NaN        NaN   Adelman    NaN   
1584                              NaN        NaN     Akuti    NaN   
912                               NaN        NaN    Albers    NaN   
913                               NaN        NaN   Alberto    NaN   
...                               ...        ...       ...    ...   
2884                              NaN        NaN      Youn    NaN   
1434                              NaN        NaN     Young    NaN   
1435                              NaN        NaN     Young    NaN   
787                               NaN        NaN    Zodrow    NaN   
2755                              NaN        NaN  Zorrilla    NaN   

                  MailingCity MailingState MailingPostalCode MailingCountry  \
Record Number                                                                 
671                       NaN          NaN               NaN            NaN   
2430                Beaverton           OR             97078            NaN   
1584                 Rockaway           OR             97136            NaN   
912                       NaN          NaN               NaN            NaN   
913                       NaN          NaN               NaN            NaN   
...                       ...          ...               ...            ...   
2884                   Eugene           OR             97403            NaN   
1434   

### Registered Parish

In this section we populate the 'Home Parish' target field for Contacts who have a 'Registered Parish' in the source system.

DONE: Check to see if the Registered Parish data is worth importing. Currently, 'Registered Parish' is only populated on 51 rows, and 32 of those rows in the 'Types' field are listed as 'Archive'. In other words, **only 19 of the 51 rows have a 'Registered Parish' value that might be meaningful.**


### Diocese of Incardination


In [147]:
df_contact_staging['Incardinated_Now'].sample(10)

Record Number
1102               Society of Jesus, USA West Province
2076                                               NaN
671                                                NaN
2867    Western Dominican Province, Order of Preachers
2063                      Dominicans, Western Province
2930                                               NaN
2524                                               NaN
713                  Archdiocese of Portland in Oregon
2232                                               NaN
835                  Archdiocese of Portland in Oregon
Name: Incardinated_Now, dtype: object

In [148]:
# Need to look for, then create a new Account that corresponds to a given 'Diocese of Incardination', then populate with record Id. 

def update_incardinated_accounts(sf, df, column_name, record_type_dev_name, church_type, new_column_name):
    """
    Update the DataFrame by getting or creating Salesforce accounts for the values in the specified column.
    
    For each account name:
      - If the name contains "Diocese" or "Archdiocese":
          record_type_dev_name is set to "Church" and church_type is set to "Diocese".
      - Otherwise:
          record_type_dev_name is set to "Religious" (with no church_type)
          and the account's 'mbfc__Religious_Type__c' field is updated to "Congregation".
    
    Parameters:
      sf (Salesforce): Salesforce connection object.
      df (pd.DataFrame): The DataFrame to update.
      column_name (str): The name of the column containing account names.
      record_type_dev_name (str): (Unused parameter in this updated logic)
      church_type (str): (Unused parameter in this updated logic)
      new_column_name (str): The name of the new column to store the Salesforce account IDs.
    
    Returns:
      pd.DataFrame: The updated DataFrame with the new column containing Salesforce account IDs.
    """
    df[new_column_name] = None

    for index, row in df.iterrows():
        account_name = row[column_name]
        if pd.notna(account_name):
            if "Diocese" in account_name or "Archdiocese" in account_name:
                # If the account name contains "Diocese" or "Archdiocese"
                account_id = get_or_create_account(sf, account_name, 'Church', 'Diocese')
            else:
                # For all other accounts, use "Religious" as the record type and update the Religious Type field.
                account_id = get_or_create_account(sf, account_name, 'Religious', None)
                # Update the account to set 'mbfc__Religious_Type__c' to "Congregation"
                sf.Account.update(account_id, {'mbfc__Religious_Type__c': 'Congregation'})
            
            df.at[index, new_column_name] = account_id
    
    return df

# Example usage
# sf = Salesforce(username='your_username', password='your_password', security_token='your_security_token')
df_contact_staging = update_incardinated_accounts(sf, df_contact_staging, 'Incardinated_Now', 'Church', 'Diocese', 'mbfc__Diocese_of_Incardination__c')

# This cell takes >6m to run

In [149]:
df_contact_staging[['mbfc__Diocese_of_Incardination__c', 'Incardinated_Now']].sample(20)

mbfc__Diocese_of_Incardination__c  \
Record Number                                     
1464                                       None   
3138                                       None   
2465                                       None   
2232                                       None   
592                          001O300000aJylSIAS   
1498                                       None   
140                                        None   
247                          001Dx00001HwDsgIAF   
1002                                       None   
1580                         001O300000aK3d1IAC   
3031                                       None   
1157                                       None   
1958                                       None   
766                                        None   
800                          001O300000aK5ofIAC   
3267                                       None   
1980                                       None   
365                                        None   
1557                                       None   
1679                                       None   

                                                Incardinated_Now  
Record Number                                                     
1464                                                         NaN  
3138                                                         NaN  
2465                                                         NaN  
2232                                                         NaN  
592                                           Diocese of Oakland  
1498                                                         NaN  
140                                                          NaN  
247                            Archdiocese of Portland in Oregon  
1002                                                         NaN  
1580           Society of the Missionaries of St. Francis Xav...  
3031                                                         NaN  
1157                                                         NaN  
1958                                                         NaN  
766                                                          NaN  
800                                     Diocese of Orlu, Nigeria  
3267                                                         NaN  
1980                                                         NaN  
365                                                          NaN  
1557                                                         NaN  
1679                                                         NaN

In [150]:
# Drop the 'Incardinated Now' column 
del df_contact_staging['Incardinated_Now']


### Deceased & Date of Death

ADPDX does not have a 'Deceased' boolean other than whether or not the Date of Death column has been populated. The target application functions based on both a 'Deceased' boolean and, optionally, a 'Date of Death.'


In [151]:
# Create a new column 'npsp__Deceased__c' and set its value to True when there is a value in 'mbfc__Date_of_Death__c'
df_contact_staging['npsp__Deceased__c'] = df_contact_staging['mbfc__Date_of_Death__c'].notna()


### Final Dataframe Cleanup


In [152]:
# drop columns that are no longer needed
# del df_contact_staging['Type(s)']  # Commented this out as we want to KEEP the field and migrated to 'ADPDX Contact Type'
del df_contact_staging['ContactRecordType']
del df_contact_staging['Link_to_Religious_Community']

In [153]:
df_contact_staging = df_contact_staging.rename(columns={'Type(s)': 'ADPDX_Contact_Type__c'})

In [154]:
# convert '' to NaN
df_contact_staging.replace("", np.nan, inplace=True)

# convert NaN to None
df_contact_staging = df_contact_staging.where(df_contact_staging.notnull(), None)


In [155]:
df_contact_staging['Languages__c'].sample(20)

Record Number
1712                         None
1977                         None
1698                         None
2121                         None
2189                         None
1945                         None
710     English, Spanish, Italian
565                          None
2784                         None
476                          None
951                          None
3128                         None
2402                         None
626                          None
2460                         None
2618                         None
2173                         None
3243                         None
2903                         None
1482                         None
Name: Languages__c, dtype: object

In [156]:
# df_contact_staging_2 = df_contact_staging.where(df_contact_staging.notnull(), None)

## Load


In [157]:
df_contact_staging['Archdpdx_Job_Id__c'] = curr_job_id

In [158]:
# generate CSV for manual loading
df_contact_staging.to_csv(f'/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/df_contacts_staging.csv', encoding='utf-8-sig')
df_contact_staging.to_csv('staging_files/contacts_staging.csv', encoding='utf-8-sig')


In [159]:
# upsert Contact records into SF using Bulk api

from simple_salesforce.exceptions import SalesforceMalformedRequest

bulk_data = []
for row in df_contact_staging.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

try:
    # Attempt to upsert Contact records into SF using Bulk API
    contact_upsert = sf.bulk.Contact.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=500, use_serial=False)
    contact_upsert_results = pd.DataFrame(contact_upsert)
except SalesforceMalformedRequest as e:
    # If a SalesforceMalformedRequest error occurs, print the error message and response content
    print(f"SalesforceMalformedRequest error: {e}")
    print(f"Response content: {e.content}")

In [160]:
# Print upsert results to local file

keys = contact_upsert[0].keys()
with open('results_files/contact_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(contact_upsert)


# CONTACT > SPOUSES


In [161]:
# Step 1: Query Salesforce to get the mapping of Archdpdx_Migration_Id__c to Salesforce Contact IDs
query = "SELECT Id, Archdpdx_Migration_Id__c, AccountId FROM Contact WHERE Archdpdx_Migration_Id__c != null"
sf_contacts = sf.query_all(query)
sf_contacts_df = pd.DataFrame(sf_contacts['records']).drop(columns='attributes')

# Step 2: Create a dictionary from this mapping
contact_id_mapping = sf_contacts_df.set_index('Archdpdx_Migration_Id__c')['Id'].to_dict()
account_id_mapping = sf_contacts_df.set_index('Id')['AccountId'].to_dict()

# Step 3: Merge df_contact_staging_spouses with sf_contacts_df to get the 'Id' column
df_contact_staging_spouses = df_contact_staging_spouses.merge(sf_contacts_df, on='Archdpdx_Migration_Id__c', how='left')

df_contact_staging_spouses

Type(s) ADPDX_Clergy_Status__c ADPDX_Religious_Status__c  \
0        Priest        Transferred Out                       NaN   
1         Staff                    NaN                       NaN   
2         Staff                    NaN                       NaN   
3         Staff                    NaN                       NaN   
4         Staff                    NaN                       NaN   
...         ...                    ...                       ...   
3011      Staff                    NaN                       NaN   
3012  Religious                    NaN                    Active   
3013      Staff                    NaN                       NaN   
3014      Staff                    NaN                       NaN   
3015      Staff                    NaN                       NaN   

     ADPDX_Login_ID__c ADPDX_Access_Permission__c Spouse Salutation FirstName  \
0             sabukaka                        NaN      0       Rev.   Stephen   
1                  NaN                        NaN      0        Mr.   Rogelio   
2                  NaN                        NaN      0        Mr.      Sean   
3                  NaN                        NaN      0        Ms.   Sherril   
4                  NaN                        NaN      0        Ms.   Barbara   
...                ...                        ...    ...        ...       ...   
3011               NaN                        NaN      0        Ms.     Jenny   
3012         dzorrilla                        NaN      0        Br.    Daniel   
3013               NaN                        NaN      0        Ms.       Kim   
3014               NaN                        NaN      0        Ms.     Agnes   
3015               NaN                        NaN      0        Ms.    Laurie   

     adpdx_Preferred_Name__c MiddleName  LastName Suffix     MailingCity  \
0                        NaN    Ozovehe  Abaukaka    NaN        Tualatin   
1                        NaN        NaN   Acevedo    NaN        Portland   
2                        NaN        NaN   Ackroyd    NaN       Corvallis   
3                        NaN        NaN     Acton    NaN          Eugene   
4                        NaN        NaN     Adams    NaN         Gresham   
...                      ...        ...       ...    ...             ...   
3011                     NaN        NaN  Zomerdyk    NaN   Central Point   
3012                     NaN        NaN  Zorrilla    NaN  Saint Benedict   
3013                     NaN        NaN     Zuber    NaN       Sublimity   
3014                     NaN        NaN    Zueger    NaN     Lake Oswego   
3015                     NaN        NaN    Zupsic    NaN        Portland   

     MailingState MailingPostalCode MailingCountry OtherCity OtherState  \
0              OR             97062            NaN  Portland         OR   
1              OR             97229            NaN       NaN        NaN   
2              OR             97330            NaN       NaN        NaN   
3              OR             97401            NaN       NaN        NaN   
4              OR             97030            NaN       NaN        NaN   
...           ...               ...            ...       ...        ...   
3011           OR             97502            NaN       NaN        NaN   
3012           OR             97373            NaN       NaN        NaN   
3013           OR             97385            NaN       NaN        NaN   
3014           OR             97034            NaN       NaN        NaN   
3015           OR             97219            NaN       NaN        NaN   

     OtherPostalCode OtherCountry Preferred_Address__c npe01__WorkPhone__c  \
0              97202          NaN              Mailing        503-430-7699   
1                NaN          NaN                  NaN        503-644-5264   
2                NaN          NaN                  NaN        541-757-1988   
3                NaN          NaN                  NaN  541-686-2234 x1524   
4             

In [162]:

# Step 4: Filter the DataFrame to only select records where the gender is male
df_contact_staging_spouses = df_contact_staging_spouses[df_contact_staging_spouses['Type(s)'] != 'Wife']

# Step 5: Use this dictionary to update the mbfc__Wife__c field in the df_contact_staging_spouses DataFrame
def update_spouse_id(row):
    spouse_id = row['Spouse']
    if pd.notna(spouse_id) and spouse_id in contact_id_mapping:
        return contact_id_mapping[spouse_id]
    return None

# Update the mbfc__Wife__c field in the df_contact_staging_spouses DataFrame
df_contact_staging_spouses['mbfc__Wife__c'] = df_contact_staging_spouses.apply(update_spouse_id, axis=1)

# Step 6: Prepare the data for the bulk update
update_data = []
for row in df_contact_staging_spouses.itertuples(index=False):
    if pd.notna(row.mbfc__Wife__c):
        update_data.append({
            'Id': row.Id,
            'mbfc__Wife__c': row.mbfc__Wife__c,
            'AccountId': account_id_mapping.get(row.mbfc__Wife__c)
        })

# Step 7: Perform the bulk update
try:
    update_results = sf.bulk.Contact.update(update_data, batch_size=100)
    update_results_df = pd.DataFrame(update_results)
    print(update_results_df)

    # Print upsert results to local file
    keys = update_results[0].keys()
    with open('results_files/spouse_update_results.csv', 'w', newline='') as csv_file:
        writer = csv.DictWriter(csv_file, keys)
        writer.writeheader()
        writer.writerows(update_results)

    # Convert the error messages to a DataFrame for better readability
    error_messages = []
    for result in update_results:
        if not result['success']:
            for error in result['errors']:
                error_messages.append({
                    'Id': result['id'],
                    'StatusCode': error['statusCode'],
                    'Message': error['message']
                })

    error_df = pd.DataFrame(error_messages)
    print(error_df)

    # Verify the updates
    df_contact_staging_spouses[['Spouse', 'mbfc__Wife__c']].sample(10)

except SalesforceMalformedRequest as e:
    print(f"SalesforceMalformedRequest error: {e}")
    print(f"Response content: {e.content}")

# cell takes > 1m to run

/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_38105/3293580140.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_contact_staging_spouses['mbfc__Wife__c'] = df_contact_staging_spouses.apply(update_spouse_id, axis=1)


     success  created                  id  \
0       True    False  003Dx00000nKiqnIAC   
1       True    False  003Dx00000nKir2IAC   
2       True    False  003Dx00000nKir8IAC   
3       True    False  003Dx00000nKirIIAS   
4      False    False  003Dx00000nKisgIAC   
..       ...      ...                 ...   
119     True    False  003Dx00000nKjOWIA0   
120     True    False  003Dx00000nKjOnIAK   
121     True    False  003Dx00000nKjXdIAK   
122     True    False  003Dx00000nKjY2IAK   
123     True    False  003Dx00000nKjYEIA0   

                                                errors  
0                                                   []  
1                                                   []  
2                                                   []  
3                                                   []  
4    [{'statusCode': 'CANNOT_EXECUTE_FLOW_TRIGGER',...  
..                                                 ...  
119                                                 []  
120

# CONTACTS > PHOTOS

#TODO: Contact Photos


# CONTACT > REGISTER ENTRIES


In [163]:
import pandas as pd

# Load CSV
df = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
               .drop(index=0) # Drops the extra row that replicates the labels
)

df

Record_Number                Common_Name                 Sort_Name  \
1             2766      Rev. Stephen Abaukaka  abaukaka stephen ozovehe   
2             2337        Mr. Rogelio Acevedo           acevedo rogelio   
3             3244           Mr. Sean Ackroyd              ackroyd sean   
4             3295          Ms. Sherril Acton             acton sherril   
5             2164          Ms. Barbara Adams             adams barbara   
...            ...                        ...                       ...   
3012          1670         Ms. Jenny Zomerdyk            zomerdyk jenny   
3013          2755  Br. Daniel Zorrilla, MSpS           zorrilla daniel   
3014          1962              Ms. Kim Zuber                 zuber kim   
3015          2202           Ms. Agnes Zueger              zueger agnes   
3016          1866          Ms. Laurie Zupsic             zupsic laurie   

        Type(s)    Clergy_Status Religious_Status   Login_ID  \
1        Priest  Transferred Out              NaN   sabukaka   
2         Staff              NaN              NaN        NaN   
3         Staff              NaN              NaN        NaN   
4         Staff              NaN              NaN        NaN   
5         Staff              NaN              NaN        NaN   
...         ...              ...              ...        ...   
3012      Staff              NaN              NaN        NaN   
3013  Religious              NaN           Active  dzorrilla   
3014      Staff              NaN              NaN        NaN   
3015      Staff              NaN              NaN        NaN   
3016      Staff              NaN              NaN        NaN   

                                               Password  \
1     def2a990be60a7998b1ed7c820101f3bd02d33b8992518...   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
5                                                   NaN   
...                                                 ...   
3012                                                NaN   
3013  391eedf7c936f63d3d0a7d9ea7e506a84709662fd31ba9...   
3014                                                NaN   
3015                                                NaN   
3016                                                NaN   

     Password_Must_be_Changed Access_Permission Spouse Title Salutation  \
1                         Yes               NaN      0  Rev.        Fr.   
2                         NaN               NaN      0   Mr.        Mr.   
3                         NaN               NaN      0   Mr.        Mr.   
4                         NaN               NaN      0   Ms.        Ms.   
5                         NaN               NaN      0   Ms.        Ms.   
...                       ...               ...    ...   ...        ...   
3012                      NaN               NaN      0   Ms.        Ms.   
3013                      Yes               NaN      0   Br.        Br.   
3014                      NaN               NaN      0   Ms.        Ms.   
3015                      NaN               NaN      0   Ms.        Ms.   
3016                      NaN               NaN      0   Ms.        Ms.   

     Christian_Name Nickname Middle_Name(s)   Surname Suffix  \
1           Stephen      NaN        Ozovehe  Abaukaka    NaN   
2           Rogelio      NaN            NaN   Acevedo    NaN   
3              Sean      NaN            NaN   Ackroyd    NaN   
4           Sherril      NaN            NaN     Acton    NaN   
5           Barbara      NaN            NaN     Adams    NaN   
...             ...      ...            ...       ...    ...   
3012          Jenny      NaN            NaN  Zomerdyk    NaN   
3013         Daniel      NaN            NaN  Zorrilla    NaN   
3014            Kim      NaN            NaN     Zuber    NaN   
3015          Agnes      NaN            NaN    Zueger    NaN   
3016         Laurie  

In [164]:
# Import all Contact fields that actually map to Register Entry records

import pandas as pd

# Define the structure of your column sets with correct attribute names
column_sets = [
    {'date': 'Baptism_Date', 'place': 'Place_of_Baptism', 'notation_type': 'Proof of Baptism'},
    {'date': 'Confirmation_Date', 'place': 'Place_of_Confirmation', 'notation_type': 'Notice of Confirmation'},
    {'date': 'Received_Date', 'place': 'Parish_of_Record', 'notation_type': 'Notice of Profession of Faith'},
    {'date': 'Marriage_Date', 'place': 'Place_of_Marriage', 'notation_type': 'Notice of Matrimony', 'spouse': 'Spouse'},
    {'date': 'Diaconal_Ordination_Date', 'place': 'Diaconal_Ordination_Place', 'prelate': 'Diaconate_Ordination_Prelate', 'notation_type': 'Notice of Holy Orders', 'ordination_type': 'Diaconate'},
    {'date': 'Presbyteral_Ordination_Date', 'place': 'Presbyteral_Ordination_Place', 'prelate': 'Presbyteral_Ordination_Prelate', 'notation_type': 'Notice of Holy Orders', 'ordination_type': 'Presbyteral'},
    {'date': 'Episcopal_Ordination_Date', 'place': 'Episcopal_Ordination_Place', 'prelate': 'Episcopal_Ordination_Prelate', 'notation_type': 'Notice of Holy Orders', 'ordination_type': 'Episcopal'}
]

# New DataFrame for entries
register_entries = pd.DataFrame(columns=['RecordNumber', 'mbfc__Register_Entry_Type__c', 'mbfc__Type__c', 'mbfc__Notation_Type__c', 'mbfc__Ordination_Type__c', 'Date', 'Place', 'Prelate', 'mbfc__Matrimonial_Wife__c'])
new_entries = []  # List to store entries before final concatenation

# Processing rows
for row in df.itertuples():
    for column_set in column_sets:
        date_value = getattr(row, column_set['date'], None)
        if pd.notna(date_value):  # Check if date field is not NaN
            entry = {
                'RecordNumber': getattr(row, 'Record_Number', None),
                'Date': date_value,
                'Place': getattr(row, column_set['place'], None)
            }
            # Add Prelate if applicable
            if 'prelate' in column_set:
                entry['Prelate'] = getattr(row, column_set['prelate'], None)

            # Set 'mbfc__Register_Entry_Type__c', and conditionally add 'mbfc__Type__c' or 'mbfc__Notation_Type__c'
            if 'sacrament_type' in column_set:
                entry['mbfc__Type__c'] = column_set['sacrament_type']
                entry['mbfc__Register_Entry_Type__c'] = 'Sacrament'
            if 'notation_type' in column_set:
                entry['mbfc__Notation_Type__c'] = column_set['notation_type']
                entry['mbfc__Register_Entry_Type__c'] = 'Notation'

            # Handle ordination type specific updates
            if 'ordination_type' in column_set:
                entry['mbfc__Ordination_Type__c'] = column_set['ordination_type']

            # Add Spouse if applicable
            if 'spouse' in column_set:
                entry['mbfc__Matrimonial_Wife__c'] = getattr(row, column_set['spouse'], None)

            new_entries.append(entry)
    
    # Add entries for 'Reader Date'
    # reader_date = getattr(row, 'Reader_Date', None)
    # if pd.notna(reader_date):
    #     entry = {
    #         'RecordNumber': getattr(row, 'Record_Number', None),
    #         'Date': reader_date,
    #         'mbfc__Notation_Type__c': 'Notice of Holy Orders',
    #         'mbfc__Ordination_Type__c': 'Minor Order: Reader',
    #         'mbfc__Register_Entry_Type__c': 'Notation'
    #     }
    #     new_entries.append(entry)
    
    # # Add entries for 'Acolyte Date'
    # acolyte_date = getattr(row, 'Acolyte_Date', None)
    # if pd.notna(acolyte_date):
    #     entry = {
    #         'RecordNumber': getattr(row, 'Record_Number', None),
    #         'Date': acolyte_date,
    #         'mbfc__Notation_Type__c': 'Notice of Holy Orders',
    #         'mbfc__Ordination_Type__c': 'Minor Order: Acolyte',
    #         'mbfc__Register_Entry_Type__c': 'Notation'
    #     }
    #     new_entries.append(entry)

# Concatenate all new entries to the DataFrame at once
if new_entries:
    register_entries = pd.concat([register_entries, pd.DataFrame(new_entries)], ignore_index=True)

print(f"Total records added: {len(register_entries)}")

# Optionally, save the new DataFrame to a CSV
register_entries.to_csv('Register_Entries.csv', index=False)

# Display the DataFrame
register_entries.sample(10)


Total records added: 1534


RecordNumber mbfc__Register_Entry_Type__c mbfc__Type__c  \
225          3076                     Notation           NaN   
1035         2813                     Notation           NaN   
6             557                     Notation           NaN   
152           428                     Notation           NaN   
666            26                     Notation           NaN   
154           428                     Notation           NaN   
637           298                     Notation           NaN   
490          3007                     Notation           NaN   
891           223                     Notation           NaN   
739           255                     Notation           NaN   

      mbfc__Notation_Type__c mbfc__Ordination_Type__c        Date  \
225         Proof of Baptism                      NaN  1978-02-26   
1035  Notice of Confirmation                      NaN  2016-05-25   
6      Notice of Holy Orders                Diaconate  2015-05-23   
152   Notice of Confirmation                      NaN  1982-04-28   
666      Notice of Matrimony                      NaN  2004-11-26   
154      Notice of Matrimony                      NaN  1992-06-20   
637    Notice of Holy Orders                Diaconate  1997-11-29   
490    Notice of Holy Orders              Presbyteral  2020-05-02   
891         Proof of Baptism                      NaN  1944-04-15   
739      Notice of Matrimony                      NaN  1972-06-24   

                                                  Place Prelate  \
225                     St. Mary Parish, Farmington, NM     NaN   
1035                            St. Mary’s , Eugene, OR     NaN   
6     Cathedral of the Immaculate Conception, Portla...    None   
152                                                 NaN     NaN   
666                                                 NaN     NaN   
154                                                 NaN     NaN   
637   Cathedral of the Immaculate Conception, Portla...    None   
490            St. Stephen Byzantine Catholic Cathedral     NaN   
891   Parroquia de San Miguelito, San Luis Potosí, M...     NaN   
739                                                 NaN     NaN   

     mbfc__Matrimonial_Wife__c  
225                        NaN  
1035                       NaN  
6                          NaN  
152                        NaN  
666                          0  
154                          0  
637                        NaN  
490                        NaN  
891                        NaN  
739                         55

### Populate Lookup for Prelate


In [165]:
from nameparser import HumanName
from nameparser.config import CONSTANTS

# Add dataset-specific Titles and Suffix constants for parsing
CONSTANTS.titles.add('Very', 'Rev.', 'Very Rev.', 'Sr.', 'Most Rev.')
CONSTANTS.suffix_acronyms.add('FRS', 'J.C.L.', 'J.C.L., D.D.', 'D.D.', 'OMI', 'OSA', 'OCD', 'OP', 'OC', 'FSE', 'OMV', 'SDB', 'SM', 'SFX', 'SP', 'OP', 'O.S.M', 'SNJM', 'OSF', 'HMRF', 'DD', 'CSJP', 'SDD', 'BVM', 'BVM - President', 'SJ', 'SL', 'IX', 'SSJ', 'J.C.L.', 'J.C.L', 'OFM', 'MSpS', 'Fco.' )


def parse_name(name):
    if pd.isna(name):  # Checks if the name is NaN or None
        return {
            'Salutation': '',
            'FirstName': '',
            'MiddleName': '',
            'LastName': '',
            'Suffix': ''
        }
    else:
        name = HumanName(name)
        return {
            'Salutation': name.title,
            'FirstName': name.first,
            'MiddleName': name.middle,
            'LastName': name.last,
            'Suffix': name.suffix
        }

# Apply the parsing function only where 'Prelate' exists and is not NaN
for entry in new_entries:
    if 'Prelate' in entry and pd.notna(entry['Prelate']):
        parsed_name = parse_name(entry['Prelate'])
        entry.update(parsed_name)

# Ensure the DataFrame creation from new_entries includes checks for existence of keys:
register_entries = pd.DataFrame(new_entries)
if 'Prelate' in register_entries.columns:
    register_entries['Salutation'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['Salutation'] if pd.notna(x) else '')
    register_entries['FirstName'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['FirstName'] if pd.notna(x) else '')
    register_entries['MiddleName'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['MiddleName'] if pd.notna(x) else '')
    register_entries['LastName'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['LastName'] if pd.notna(x) else '')
    register_entries['Suffix'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['Suffix'] if pd.notna(x) else '')


# Display the DataFrame
print(f"Total records added: {len(register_entries)}")
register_entries.sample(10)



Total records added: 1534


RecordNumber        Date  \
966           664  2017-06-03   
686          1144  1970-06-13   
107           757  1980-05-31   
566          1532  1995-02-18   
1067           75  1973-04-21   
1165           38  1973-12-15   
404          3316  1979-10-18   
574           697  2013-06-08   
422           456  1963-01-20   
1442         2866  2003-07-05   

                                                  Place  \
966   Cathedral of the Immaculate Conception, Portla...   
686                                  St. Charles Parish   
107                                     Santa Maria, CA   
566                                                 NaN   
1067                                                NaN   
1165                                                NaN   
404                                                 NaN   
574   Cathedral of the Immaculate Conception, Portla...   
422                                St. Mark, Eugene, OR   
1442                      St. Joseph, Big Bear City, CA   

                                          Prelate mbfc__Notation_Type__c  \
966   Most Rev. Alexander K. Sample, J.C.L., D.D.  Notice of Holy Orders   
686                        Most Rev. Robert Dwyer  Notice of Holy Orders   
107                    Most Rev. Thaddeus Shubsda  Notice of Holy Orders   
566                                           NaN    Notice of Matrimony   
1067                                          NaN    Notice of Matrimony   
1165                                          NaN    Notice of Matrimony   
404                                           NaN       Proof of Baptism   
574   Most Rev. Alexander K. Sample, J.C.L., D.D.  Notice of Holy Orders   
422                                           NaN       Proof of Baptism   
1442                                          NaN       Proof of Baptism   

     mbfc__Register_Entry_Type__c mbfc__Ordination_Type__c Salutation  \
966                      Notation              Presbyteral              
686                      Notation              Presbyteral  Most Rev.   
107                      Notation              Presbyteral  Most Rev.   
566                      Notation                      NaN              
1067                     Notation                      NaN              
1165                     Notation                      NaN              
404                      Notation                      NaN              
574                      Notation              Presbyteral              
422                      Notation                      NaN              
1442                     Notation                      NaN              

     FirstName MiddleName                       LastName Suffix  \
966     J.C.L.             Most Rev. Alexander K. Sample   D.D.   
686     Robert                                     Dwyer          
107   Thaddeus                                   Shubsda          
566                                                               
1067                                                              
1165                                                              
404                                                               
574     J.C.L.             Most Rev. Alexander K. Sample   D.D.   
422                                                               
1442                                                              

     mbfc__Matrimonial_Wife__c  
966                        NaN  
686                        NaN  
107                        NaN  
566                          0  
1067                       315  
1165                       102  
404                        NaN  
574                        NaN  
422                        NaN  
1442                       NaN

In [166]:
# Query Salesforce for existing contacts and create a dictionary for mapping

from simple_salesforce import Salesforce

query = """
SELECT Id, Archdpdx_Migration_Id__c
FROM Contact
"""
result = sf.query_all(query)
contact_map = {rec['Archdpdx_Migration_Id__c']: rec['Id'] for rec in result['records']}


In [167]:
# Get RecordTypeId for Contact.Priest
priest_contact_recordtype_id = get_recordtype_id(df_sf_recordTypes, 'Priest', 'Contact', 'mbfc')

priest_contact_recordtype_id

'012Dx0000003p5JIAQ'

In [168]:
# Get RecordID for Prelates by querying for Contacts by FirstName and LastName and, if not found, Create New Contacts

from simple_salesforce import SFType, SalesforceResourceNotFound

contact = SFType('Contact', sf.session_id, sf.sf_instance)
for index, row in register_entries.iterrows():
    first_name, last_name = row.get('FirstName'), row.get('LastName')

    if pd.isna(first_name) or pd.isna(last_name) or first_name.strip() == '' or last_name.strip() == '':
        # If either first name or last name is missing or empty, skip this row or handle as needed
        print(f"Skipping row {index} due to missing name information.")
        continue

    try:
        # Search for contact by First and Last Name
        query = f"SELECT Id FROM Contact WHERE FirstName = '{first_name}' AND LastName = '{last_name}'"
        result = sf.query(query)
        if result['totalSize'] > 0:
            contact_id = result['records'][0]['Id']
        else:
            # Create a new contact if no match found
            new_contact = {
                'Salutation': "Most Rev.",
                'FirstName': first_name,
                'LastName': last_name,
                'Archdpdx_Job_Id__c': curr_job_id,
                'RecordTypeId': priest_contact_recordtype_id,
                'mbfc__Ecclesial_Status__c': "Bishop/Archbishop"
            }
            create_result = contact.create(new_contact)
            contact_id = create_result['id']

        # Update DataFrame with the Salesforce Contact ID
        register_entries.at[index, 'mbfc__Celebrant__c'] = contact_id

    except SalesforceException as e:
        print(f"Error processing row {index}: {e}")

# cell tak

Skipping row 2 due to missing name information.
Skipping row 3 due to missing name information.
Skipping row 4 due to missing name information.
Skipping row 5 due to missing name information.
Skipping row 6 due to missing name information.
Skipping row 8 due to missing name information.
Skipping row 9 due to missing name information.
Skipping row 10 due to missing name information.
Skipping row 11 due to missing name information.
Skipping row 12 due to missing name information.
Skipping row 13 due to missing name information.
Skipping row 16 due to missing name information.
Skipping row 17 due to missing name information.
Skipping row 18 due to missing name information.
Skipping row 19 due to missing name information.
Skipping row 20 due to missing name information.
Skipping row 21 due to missing name information.
Skipping row 22 due to missing name information.
Skipping row 23 due to missing name information.
Skipping row 24 due to missing name information.
Skipping row 26 due to miss

### Prepare to Upsert


In [169]:
# Map Contact IDs to Register Entries

register_entries_2 = register_entries

register_entries_2['mbfc__Contact__c'] = register_entries['RecordNumber'].map(contact_map)


In [170]:
# Append Job_Id__c
register_entries_2['Archdpdx_Job_Id__c'] = curr_job_id

In [171]:
# Generate an External ID
def create_external_id(row):
    record_number = str(row['RecordNumber']).replace(' ', '').replace('-', '')
    entry_type = str(row['mbfc__Register_Entry_Type__c']).replace(' ', '').replace('-', '')

    # Check whether to use Type or Notation Type based on what's available
    if 'mbfc__Type__c' in row and not pd.isna(row['mbfc__Type__c']):
        type_field = str(row['mbfc__Type__c']).replace(' ', '').replace('-', '')
    elif 'mbfc__Notation_Type__c' in row and not pd.isna(row['mbfc__Notation_Type__c']):
        type_field = str(row['mbfc__Notation_Type__c']).replace(' ', '').replace('-', '') + str(row['mbfc__Ordination_Type__c']).replace(' ', '').replace('-', '')
    else:
        type_field = 'Unknown'

    return f"{record_number}_{entry_type}_{type_field}"

In [172]:
# Assuming your DataFrame is named `register_entries`
register_entries_2['Archdpdx_Migration_Id__c'] = register_entries.apply(create_external_id, axis=1)

if register_entries['Archdpdx_Migration_Id__c'].duplicated().any():
    print("Warning: There are duplicate external IDs.")
    # Optionally, show the duplicates
    duplicates = register_entries[register_entries['external_id'].duplicated(keep=False)]
    print(duplicates)
else:
    print("All external IDs are unique.")


All external IDs are unique.


In [173]:
# Drop unnecessary columns:
register_entries_2.drop(['RecordNumber', 'Prelate', 'Salutation', 'FirstName', 'MiddleName', 'LastName', 'Suffix'], axis=1, inplace=True)

In [174]:
register_entries_staging = register_entries_2

In [175]:
# Remove all NaN values:
register_entries_staging.fillna('', inplace=True)

# Rename columns
register_entries_staging = register_entries_staging.rename(columns={
    'Place': 'mbfc__Location_text__c',
    'Date': 'mbfc__Event_Date__c'
})


In [176]:
# What is this checking for?... Why did I include this?
register_entries_staging[register_entries_staging.mbfc__Contact__c == '003Dx00000m0OtXIAU']


Empty DataFrame
Columns: [mbfc__Event_Date__c, mbfc__Location_text__c, mbfc__Notation_Type__c, mbfc__Register_Entry_Type__c, mbfc__Ordination_Type__c, mbfc__Matrimonial_Wife__c, mbfc__Celebrant__c, mbfc__Contact__c, Archdpdx_Job_Id__c, Archdpdx_Migration_Id__c]
Index: []

In [177]:
# generate CSV for manual loading
register_entries_staging.to_csv('staging_files/reg_entry_staging.csv', encoding='utf-8-sig')


In [178]:
# Upsert Register Entry Records

bulk_data = []
for row in register_entries_staging.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

# Keep the batch <100 as I've been getting an exceptionCode: 'InvalidBatch', 'exceptionMessage': 'Records not processed'
reg_entry_upsert = sf.bulk.mbfc__Register_Entry__c.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
reg_entry_upsert_results = pd.DataFrame(reg_entry_upsert)

In [179]:
# Print upsert results to local file

keys = reg_entry_upsert[0].keys()

with open('results_files/register_entry_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(reg_entry_upsert)

# CONTACT > AFFILIATIONS


In [180]:
# Function to create a unique ID based on Person's Name + completion date or start date + affiliation type
def create_unique_id(row):
    # Get values, handling NaNs
    person_id = str(row.get('mbfc__Person__c', '')).strip()
    
    # Check for completion date, and if it's blank, use the start date
    completion_date = row.get('mbfc__Completion_Date__c', '')
    if pd.isna(completion_date) or completion_date == '':
        completion_date = row.get('mbfc__Start_Date__c', '')
    
    completion_date = str(completion_date).strip()
    affiliation = str(row.get('mbfc__Affiliation__c', '')).strip()
    
    # Concatenate the three fields
    combined = f"{person_id}{completion_date}{affiliation}"
    
    # Remove unwanted characters and convert to lowercase
    clean_id = ''.join(combined.split()).replace('-', '').replace('.', '').lower()
    
    # Limit the string to 50 characters
    return clean_id[:50]

## Education Affiliations

This section takes multiple sets of columns (all related to a person's education) from the Contacts table, and combines them into a single set of columns in a new dataframe for insertion into Salesforce as Affiliation records.


In [181]:
# Parse and stage Education Affiliation records
import pandas as pd
from functools import lru_cache

# Load CSV
df = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
               .drop(index=0) # Drops the extra row that replicates the labels
)


# Define the structure of your column sets with correct attribute names
degree_sets = [
    {'year': 'Bachelor_Degree_Year', 'type': 'Bachelor_Degree_Type', 'institution': 'Bachelor_Degree_Institution'},
    {'year': 'Graduate_1_Degree_Year', 'type': 'Graduate_1_Degree_Type', 'institution': 'Graduate_1_Degree_Institution'},
    {'year': 'Graduate_2_Degree_Year', 'type': 'Graduate_2_Degree_Type', 'institution': 'Graduate_2_Degree_Institution'},
    {'year': 'Graduate_3_Degree_Year', 'type': 'Graduate_3_Degree_Type', 'institution': 'Graduate_3_Degree_Institution'},
    {'year': 'Graduate_4_Degree_Year', 'type': 'Graduate_4_Degree_Type', 'institution': 'Graduate_4_Degree_Institution'}
]

# Query for the Record Type ID for 'Organization'
record_type_result = sf.query("SELECT Id FROM RecordType WHERE SobjectType = 'Account' AND DeveloperName = 'Organization' AND NamespacePrefix = 'mbfc'")
organization_record_type_id = record_type_result['records'][0]['Id'] if record_type_result['records'] else None

# Initialize the DataFrame for the staging table
education_staging = pd.DataFrame()

# Function to check and create institution account
@lru_cache(maxsize=None)
def get_or_create_institution_account(institution_name):
    if pd.isna(institution_name):
        return None  # Return None or handle as appropriate if institution name is NaN

    # Query Salesforce to find the institution
    query = f"SELECT Id, Name FROM Account WHERE Name = '{institution_name}' LIMIT 1"
    results = sf.query(query)
    
    # If exists, return the ID
    if results['records']:
        return results['records'][0]['Id']
    else:
        # Ensure no NaN values are sent to Salesforce
        account_data = {
            'Name': institution_name if pd.notna(institution_name) else "Default Name",  # Provide a default if NaN
            'RecordTypeId': organization_record_type_id,
            'mbfc__Organization_Type__c': 'School'
        }
        # Remove keys with None values to avoid JSON serialization issues
        account_data = {k: v for k, v in account_data.items() if v is not None}
        
        new_account = sf.Account.create(account_data)
        return new_account['id']

# Get Contact record ID from Salesforce
@lru_cache(maxsize=None)
def get_contact_id_by_record_number(record_number):
    if pd.isna(record_number):
        return None
    query = f"SELECT Id FROM Contact WHERE Archdpdx_Migration_Id__c = '{record_number}'"
    results = sf.query(query)
    if results['records']:
        return results['records'][0]['Id']
    return None


# Initialize an empty list to collect DataFrames or dictionaries
new_entries = []

# Process each row and each degree set
for index, row in df.iterrows():
    for degree_set in degree_sets:
        year = row[degree_set['year']]
        if pd.notna(year):  # Only proceed if the year column is not NaN
            formatted_year = f"{int(year)}-01-01"  # Convert year to YYYY-MM-DD format
            institution_name = row[degree_set['institution']]
            account_id = get_or_create_institution_account(institution_name)
            contact_id = get_contact_id_by_record_number(row['Record_Number'])
            
            # Create a record for the staging table
            affiliation_record = {
                'mbfc__Person__c': contact_id,
                'mbfc__Completion_Date__c': formatted_year,
                'mbfc__Context__c': account_id,
                'mbfc__Category__c': 'Education/Studies',
                'mbfc__Affiliation__c': row[degree_set['type']]
            }
            new_entries.append(affiliation_record)

# Convert all collected records to a DataFrame in one go
education_staging = pd.DataFrame(new_entries)


#FIXME: There are 4 rows where no INSTITUTION is listed. This makes it impossible to import an Affiliation record. Need to figure out how to handle this with Client. 
#FIXME: There are about 15 rows where no DEGREE is listed. This makes it impossible to import an Affiliation record. Need to figure out how to handle this with Client. 

# Cell takes approx. 2m to run

In [182]:
# Apply the function to each row and create a new column with the unique ID
education_staging['Archdpdx_Migration_Id__c'] = education_staging.apply(create_unique_id, axis=1)

# Check the first few rows to verify the new column
education_staging.head()

mbfc__Person__c mbfc__Completion_Date__c    mbfc__Context__c  \
0  003Dx00000nKiqAIAS               1996-01-01                None   
1  003Dx00000nKiqAIAS               2013-01-01  001Dx00001HwExyIAF   
2  003Dx00000nKiqFIAS               1976-01-01  001Dx00001HwF0RIAV   
3  003Dx00000nKiqFIAS               1980-01-01  001Dx00001HwF0WIAV   
4  003Dx00000nKiqUIAS               2004-01-01  001Dx00001HwF0bIAF   

   mbfc__Category__c  mbfc__Affiliation__c  \
0  Education/Studies              Theology   
1  Education/Studies   MA Pastoral Studies   
2  Education/Studies       BA Liberal Arts   
3  Education/Studies                M.Div.   
4  Education/Studies  Bachelor, Philosophy   

                        Archdpdx_Migration_Id__c  
0             003dx00000nkiqaias19960101theology  
1    003dx00000nkiqaias20130101mapastoralstudies  
2        003dx00000nkiqfias19760101baliberalarts  
3                 003dx00000nkiqfias19800101mdiv  
4  003dx00000nkiquias20040101bachelor,philosophy

In [183]:
# Fill any NaN values
education_staging = education_staging.fillna('')

In [184]:
# Save the staging table to CSV
education_staging.to_csv('staging_files/education_staging.csv', index=False)


In [185]:
import pandas as pd
import numpy as np
from simple_salesforce import Salesforce, SalesforceMalformedRequest, SalesforceError
from datetime import datetime, date



# def upsert_to_salesforce(sf, dataframe, object_name, external_id_field):
#     """
#     Upsert records to Salesforce from a pandas DataFrame.

#     Parameters:
#     sf (Salesforce): The Salesforce connection instance.
#     dataframe (pd.DataFrame): The pandas DataFrame containing data to upsert.
#     object_name (str): The Salesforce object name (e.g., 'Contact').
#     external_id_field (str): The external ID field used for upserts.
#     """
#     successful_upserts = 0
#     failed_upserts = 0

#     # Replace placeholder values with None in the DataFrame
#     dataframe.replace({None: pd.NA, ' ': None, '': None}, inplace=True)

#     # Convert DataFrame to a list of dictionaries
#     data_to_upsert = dataframe.to_dict(orient='records')

#     for data in data_to_upsert:
#         try:
#             data = convert_non_serializables(data)
#             external_id = data.pop(external_id_field)

#             # Perform upsert using only the External ID
#             response = getattr(sf, object_name).upsert(f'{external_id_field}/{external_id}', data)
#             successful_upserts += 1
#             print(f"Successfully upserted {object_name} with External ID: {external_id}")
#         except SalesforceMalformedRequest as e:
#             failed_upserts += 1
#             print(f"Malformed request error when upserting {object_name} with External ID: {external_id}. Error: {e.content}")
#         except SalesforceError as e:
#             failed_upserts += 1
#             print(f"Salesforce error when upserting {object_name} with External ID: {external_id}. Error: {e.content}")
#         except Exception as e:
#             failed_upserts += 1
#             print(f"Failed to upsert {object_name} with External ID: {external_id}. Error: {e}")

#     print(f"Upsert completed. Successful upserts: {successful_upserts}, Failed upserts: {failed_upserts}")

# def convert_non_serializables(data):
#     """Convert non-serializable objects to serializable formats."""
#     for key, value in data.items():
#         try:
#             if isinstance(value, (datetime, date)):
#                 data[key] = value.isoformat()
#             elif isinstance(value, float) and np.isnan(value):
#                 data[key] = None
#             elif pd.isna(value):
#                 data[key] = None
#             elif isinstance(value, (int, bool, str)):
#                 data[key] = value
#             else:
#                 data[key] = str(value)  # Convert other types to string
#         except Exception as e:
#             print(f"Error processing key: {key}, value: {value}, error: {e}")
#     return data

# def upsert_to_salesforce_bulk(sf, dataframe, object_name, external_id_field, failed_log_file, batch_size=10000):
#     """
#     Upsert records to Salesforce from a pandas DataFrame using the Bulk API.

#     Parameters:
#     sf (Salesforce): The Salesforce connection instance.
#     dataframe (pd.DataFrame): The pandas DataFrame containing data to upsert.
#     object_name (str): The Salesforce object name (e.g., 'Contact').
#     external_id_field (str): The external ID field used for upserts.
#     failed_log_file (str): The file name where failed upsert records will be logged.
#     batch_size (int): The number of records to include in each batch.
#     """
#     successful_upserts = 0
#     failed_upserts = 0

#     # Replace placeholder values with None in the DataFrame
#     dataframe.replace({None: pd.NA, ' ': None, '': None}, inplace=True)

#     # Convert DataFrame to a list of dictionaries
#     data_to_upsert = dataframe.to_dict(orient='records')

#     with open(failed_log_file, 'a') as log_file:
#         # Process data in batches
#         for i in range(0, len(data_to_upsert), batch_size):
#             batch_data = data_to_upsert[i:i + batch_size]
#             batch_data = [convert_non_serializables(record) for record in batch_data]

#             try:
#                 # Perform bulk upsert
#                 response = sf.bulk.__getattr__(object_name).upsert(batch_data, external_id_field=external_id_field)

#                 for res in response:
#                     if res['success']:
#                         successful_upserts += 1
#                     else:
#                         failed_upserts += 1
#                         log_file.write(f"Failed to upsert record: {res}\n")

#             except SalesforceMalformedRequest as e:
#                 failed_upserts += len(batch_data)
#                 log_file.write(f"Malformed request error when upserting batch. Error: {e.content}\n")
#             except SalesforceError as e:
#                 failed_upserts += len(batch_data)
#                 log_file.write(f"Salesforce error when upserting batch. Error: {e.content}\n")
#             except Exception as e:
#                 failed_upserts += len(batch_data)
#                 log_file.write(f"Failed to upsert batch. Error: {e}\n")

#     print(f"Upsert completed. Successful upserts: {successful_upserts}, Failed upserts: {failed_upserts}")


In [186]:
# Upsert Education Affiliation records

# upsert_to_salesforce(sf, education_staging, 'mbfc__Affiliation__c', 'Archdpdx_Migration_Id__c')
upsert_to_salesforce_bulk(sf, education_staging, 'mbfc__Affiliation__c', 'Archdpdx_Migration_Id__c', 'results_files/education_affil', batch_size=1000)


Batch 1 processed: 669 successful, 29 failed.
Upsert completed. Total records processed: 698, Batches: 1, Successful upserts: 669, Failed upserts: 29


In [187]:

#FIXME: A number of Education Affiliation records are missing either an Affiliation title or a Context

In [188]:
# Upsert Education Affiliation records [DEP]

# bulk_data = []
# for row in education_staging.itertuples(index=False):
#     d = row._asdict()
#     # del d['Index']
#     bulk_data.append(d)

# try:
#     # Attempt to upsert Education Affiliation records into SF using Bulk API
    # education_affil_upsert = sf.bulk.mbfc__Affiliation__c.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=500, use_serial=False)
    

# except SalesforceMalformedRequest as e:
#     # If a SalesforceMalformedRequest error occurs, print the error message and response content
#     print(f"SalesforceMalformedRequest error: {e}")
#     print(f"Response content: {e.content}")

# Send results to CSV
# education_affil_upsert_results = pd.DataFrame(education_affil_upsert)
# education_affil_upsert_results.to_csv('results_files/education_affil_upsert_results')

## Ecclesial Affiliations

This section handles individual Contact source table FIELDS that map to Affiliation RECORDS in the target system.

As the source data model and target data model are substantially different, this section groups together source columns into what will become individual records in the new system and populates missing information based on or required by the target system.

Example: each affiliation record in the target system requires a Context. In certain cases this data does not exist in the source or it is found in another column:

| Affiliation            | Context                   | Completion Date           |
| ---------------------- | ------------------------- | ------------------------- |
| First Vows             | Religious Order           | Date of First Vows        |
| Final Vows             | Religious Order           | Date of Final Vows        |
| Incardination          | Incardinated from Diocese | Incardinated From Date    |
| Faculties (Type)       | Local Diocese             | Faculties Granted Date    |
| Faculties (Restricted) | Local Diocese             | Faculties Restricted Date |
| Faculties (Withdrawn)  | Local Diocese             | Faculties Withdrawn Date  |
| Excardinated           | Excardinated To Diocese   | Excardinated To Date      |

Other examples of columns that need to be populated:

- RecordTypeId
- Category
- Start Date
- Completion Date

Depending on which column is being migrated, the date value might be considered to be a Start Date or a Completion Date in the target system, and needs to be staged accordingly.


In [189]:
# Generate a staging DF of Ecclesial Affiliations out of a handful of fields in the source data, each of which is to be converted into a new row in the staging DF.

# FIXME: There are a number of rows where a Faculties Granted is missing a date, and conversely, where there is a Faculties Granted Date but no description of the Faculties granted. This is a problem, because the application requires a date for when Faculties were granted.


import pandas as pd
from functools import lru_cache
from simple_salesforce import Salesforce

# Load CSV
df = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
               .drop(index=0) # Drops the extra row that replicates the labels
)

# Define the structure of your column sets with correct attribute names
column_sets = [
    {'year': 'Incardinated_From_Date', 'context': 'Incardinated_From_Diocese'},
    {'year': 'Excardinated_To_Date', 'context': 'Excardinated_To_Diocese'},
    {'year': 'Faculties_Granted_Date', 'affiliation': 'Faculties'},
    {'year': 'Faculties_Restricted_Date'},
    {'year': 'Faculties_Withdrawn_Date'},
    {'year': 'Reader_Date'},  # Add Reader Date
    {'year': 'Acolyte_Date'},  # Add Acolyte Date
    {'year': 'Candidacy_Date'}  # Add Candidate Date
]



In [190]:

# Query for the Record Type IDs of Church, Religious    
record_type_query = "SELECT Id, DeveloperName FROM RecordType WHERE SobjectType = 'Account' AND DeveloperName IN ('Church', 'Religious')"
record_type_result = sf.query(record_type_query)
record_type_ids = {record['DeveloperName']: record['Id'] for record in record_type_result['records']}

church_record_type_id = record_type_ids.get('Church')
religious_record_type_id = record_type_ids.get('Religious')

# Query for the Record Type IDs for 'Ecclesial_Affiliation' and 'Ministerial_Status' for mbfc__Affiliation__c object
record_type_query = "SELECT Id, DeveloperName FROM RecordType WHERE SobjectType = 'mbfc__Affiliation__c' AND DeveloperName IN ('Ecclesial_Affiliation', 'Ministerial_Status')"
record_type_result = sf.query(record_type_query)
record_type_ids = {record['DeveloperName']: record['Id'] for record in record_type_result['records']}

ecclesial_affiliation_record_type_id = record_type_ids.get('Ecclesial_Affiliation')
ministerial_status_record_type_id = record_type_ids.get('Ministerial_Status')

# Check if any of the required Record Types are missing
if not ecclesial_affiliation_record_type_id:
    raise ValueError("No RecordType found for Ecclesial Affiliation on mbfc__Affiliation__c object.")
if not ministerial_status_record_type_id:
    raise ValueError("No RecordType found for Ministerial Status on mbfc__Affiliation__c object.")

In [191]:

# Initialize the DataFrame for the staging table
ecclesial_affiliation_staging = pd.DataFrame()

# Function to check and create institution account
@lru_cache(maxsize=None)
def get_or_create_church_account(context):
    if pd.isna(context):
        return None  # Return None or handle as appropriate if institution name is NaN

    # Query Salesforce to find the institution
    query = f"SELECT Id, Name FROM Account WHERE Name = '{context}' LIMIT 1"
    results = sf.query(query)
    
    # If exists, return the ID
    if results['records']:
        return results['records'][0]['Id']
    else:
        # Ensure no NaN values are sent to Salesforce
        if 'Diocese' in context or 'Archdiocese' in context:
            account_data = {
                'Name': context if pd.notna(context) else "Church Name Missing",  # Provide a default if NaN
                'RecordTypeId': church_record_type_id,
                'mbfc__Church_Type__c': 'Diocese'
            }
        else:
            account_data = {
                'Name': context if pd.notna(context) else "Religious Name Missing",  # Provide a default if NaN
                'RecordTypeId': religious_record_type_id
            }

        # Remove keys with None values to avoid JSON serialization issues
        account_data = {k: v for k, v in account_data.items() if v is not None}
        
        new_account = sf.Account.create(account_data)
        return new_account['id']

# Get Contact record ID from Salesforce
@lru_cache(maxsize=None)
def get_contact_id_by_record_number(record_number):
    if pd.isna(record_number):
        return None
    query = f"SELECT Id FROM Contact WHERE Archdpdx_Migration_Id__c = '{record_number}'"
    results = sf.query(query)
    if results['records']:
        return results['records'][0]['Id']
    return None

# Initialize an empty list to collect DataFrames or dictionaries
new_entries = []

# Process each row and each degree set
for index, row in df.iterrows():
    for col_set in column_sets:
        date = row[col_set['year']]
        if pd.notna(date):  # Only proceed if the year column is not NaN
            context = row.get(col_set.get('context'), None)
            account_id = get_or_create_church_account(context)
            contact_id = get_contact_id_by_record_number(row['Record_Number'])
            
            # Initialize all necessary variables with None
            start_date = None
            completion_date = None
            affiliation = None
            record_type_id = None
            category = None

            # Determine the mbfc__Affiliation__c value
            if 'Incardinated_From_Date' in col_set['year']:
                affiliation = 'Incardinated'
                completion_date = date
                record_type_id = ecclesial_affiliation_record_type_id
                category = 'Ecclesial Affiliations'
            elif 'Excardinated_To_Date' in col_set['year']:
                affiliation = 'Excardinated'
                completion_date = date
                record_type_id = ecclesial_affiliation_record_type_id
                category = 'Ecclesial Affiliations'
            elif 'Faculties_Granted_Date' in col_set['year']:
                faculties_value = row.get(col_set.get('affiliation', ''))
                if pd.isna(faculties_value):
                    affiliation = 'Faculties'
                else:
                    affiliation = f"Faculties ({faculties_value})"
                account_id = diocesan_account_id  # Override account ID for faculties
                start_date = date
                record_type_id = ministerial_status_record_type_id
                category = 'Faculties'
            elif 'Faculties_Restricted_Date' in col_set['year']:
                affiliation = 'Faculties (Restricted)'
                account_id = diocesan_account_id  # Override account ID for faculties
                completion_date = date
                record_type_id = ministerial_status_record_type_id
                category = 'Faculties'
            elif 'Faculties_Withdrawn_Date' in col_set['year']:
                affiliation = 'Faculties (Withdrawn)'
                account_id = diocesan_account_id  # Override account ID for faculties
                completion_date = date
                record_type_id = ministerial_status_record_type_id
                category = 'Faculties'
            elif 'Date_of_First_Vows' in col_set['year']:
                affiliation = 'First Vows'
                completion_date = date
                record_type_id = ecclesial_affiliation_record_type_id
                category = 'Ecclesial Affiliations'
            elif 'Date_of_Final_Vows' in col_set['year']:
                affiliation = 'Final Vows'
                completion_date = date
                record_type_id = ecclesial_affiliation_record_type_id
                category = 'Ecclesial Affiliations'
            elif 'Reader_Date' in col_set['year']:
                affiliation = 'Reader Installation'
                completion_date = date
                record_type_id = ecclesial_affiliation_record_type_id
                category = 'Installations'
                account_id = diocesan_account_id
            elif 'Acolyte_Date' in col_set['year']:
                affiliation = 'Acolyte Installation'
                completion_date = date
                record_type_id = ecclesial_affiliation_record_type_id
                category = 'Installations'
                account_id = diocesan_account_id
            elif 'Candidacy_Date' in col_set['year']:
                affiliation = 'Candidate Installation'
                completion_date = date
                record_type_id = ecclesial_affiliation_record_type_id
                category = 'Installations'
                account_id = diocesan_account_id

            else:
                affiliation = row.get(col_set.get('affiliation', ''), None)
            
            # Create a record for the staging table
            affiliation_record = {
                'RecordTypeId': record_type_id,
                'mbfc__Person__c': contact_id,
                'mbfc__Completion_Date__c': completion_date,
                'mbfc__Start_Date__c': start_date,
                'mbfc__Context__c': account_id,
                'mbfc__Category__c': category,
                'mbfc__Affiliation__c': affiliation
            }
            new_entries.append(affiliation_record)

# Convert all collected records to a DataFrame in one go
ecclesial_affiliations_staging = pd.DataFrame(new_entries)

# Takes approx. 1.5 minutes to run

In [192]:
ecclesial_affiliations_staging.sample(20)

RecordTypeId     mbfc__Person__c mbfc__Completion_Date__c  \
897  012Dx0000003p5DIAQ  003Dx00000nKj65IAC                     None   
749  012Dx0000003p5DIAQ  003Dx00000nKjJTIA0                     None   
759  012Dx0000003p5AIAQ  003Dx00000nKjJkIAK               2020-02-11   
227  012Dx0000003p5DIAQ  003Dx00000nKiojIAC                     None   
199  012Dx0000003p5AIAQ  003Dx00000nKinaIAC               2021-03-10   
469  012Dx0000003p5AIAQ  003Dx00000nKj8gIAC               2008-10-25   
906  012Dx0000003p5DIAQ  003Dx00000nKjMdIAK                     None   
9    012Dx0000003p5DIAQ  003Dx00000nKiqVIAS                     None   
85   012Dx0000003p5DIAQ  003Dx00000nKjA7IAK                     None   
853  012Dx0000003p5AIAQ  003Dx00000nKj3hIAC               1981-01-23   
772  012Dx0000003p5AIAQ  003Dx00000nKjKGIA0               1999-10-23   
583  012Dx0000003p5AIAQ  003Dx00000nKjFwIAK               1999-10-23   
553  012Dx0000003p5DIAQ  003Dx00000nKixxIAC                     None   
365  012Dx0000003p5DIAQ  003Dx00000nKitiIAC                     None   
700  012Dx0000003p5DIAQ  003Dx00000nKj0uIAC                     None   
934  012Dx0000003p5AIAQ  003Dx00000nKjOHIA0               2020-11-04   
132  012Dx0000003p5DIAQ  003Dx00000nKjC6IAK                     None   
15   012Dx0000003p5AIAQ  003Dx00000nKiqcIAC               2005-12-16   
254  012Dx0000003p5DIAQ  003Dx00000nKipbIAC                     None   
910  012Dx0000003p5DIAQ  003Dx00000nKjMmIAK                     None   

    mbfc__Start_Date__c    mbfc__Context__c       mbfc__Category__c  \
897          2005-06-11  001Dx00001HwDsgIAF               Faculties   
749          2018-03-19  001Dx00001HwDsgIAF               Faculties   
759                None  001Dx00001HwDsgIAF           Installations   
227          2014-02-28  001Dx00001HwDsgIAF               Faculties   
199                None  001Dx00001HwDsgIAF           Installations   
469                None  001Dx00001HwDsgIAF           Installations   
906          2014-06-06  001Dx00001HwDsgIAF               Faculties   
9            2012-06-09  001Dx00001HwDsgIAF               Faculties   
85           2022-07-01  001Dx00001HwDsgIAF               Faculties   
853                None  001Dx00001HwDsgIAF           Installations   
772                None  001Dx00001HwDsgIAF           Installations   
583                None  001Dx00001HwDsgIAF           Installations   
553          2002-12-23  001Dx00001HwDsgIAF               Faculties   
365          2020-08-01  001Dx00001HwDsgIAF               Faculties   
700          2019-10-26  001Dx00001HwDsgIAF               Faculties   
934                None  001Dx00001HwDsgIAF           Installations   
132          2014-06-14  001Dx00001HwDsgIAF               Faculties   
15                 None  001Dx00001HwFExIAN  Ecclesial Affiliations   
254          2023-10-28  001Dx00001HwDsgIAF               Faculties   
910          2023-08-01  001Dx00001HwDsgIAF               Faculties   

         mbfc__Affiliation__c  
897       Faculties (General)  
749                 Faculties  
759      Acolyte Installation  
227      Faculties (Diaconal)  
199       Reader Installation  
469      Acolyte Installation  
906       Faculties (General)  
9         Faculties (General)  
85   Faculties (Confessional)  
853       Reader Installation  
772      Acolyte Installation  
583      Acolyte Installation  
553      Faculties (Diaconal)  
365  Faculties (Confessional)  
700      Faculties (Diaconal)  
934      Acolyte Installation  
132  Faculties (Confessional)  
15               Incardinated  
254  Faculties (Confessional)  
910       Faculties (General)

In [193]:
# Apply the function to each row and create a new column with the unique ID
ecclesial_affiliations_staging['Archdpdx_Migration_Id__c'] = ecclesial_affiliations_staging.apply(create_unique_id, axis=1)

# Check for duplicates
ecclesial_affiliations_staging['Archdpdx_Migration_Id__c'].duplicated().value_counts()

False    985
Name: Archdpdx_Migration_Id__c, dtype: int64

In [194]:
# Send the new DataFrame to a CSV
ecclesial_affiliations_staging.to_csv('staging_files/Ecclesial_Affiliations_Staging.csv', index=False, encoding='utf-8-sig')

In [198]:
ecclesial_affiliations_staging

RecordTypeId     mbfc__Person__c mbfc__Completion_Date__c  \
0    012Dx0000003p5DIAQ  003Dx00000nKiqAIAS                     None   
1    012Dx0000003p5DIAQ  003Dx00000nKiqFIAS               2010-06-30   
2    012Dx0000003p5DIAQ  003Dx00000nKiqRIAS                     None   
3    012Dx0000003p5AIAQ  003Dx00000nKiqRIAS               2013-04-10   
4    012Dx0000003p5AIAQ  003Dx00000nKiqRIAS               2013-04-10   
..                  ...                 ...                      ...   
980  012Dx0000003p5DIAQ  003Dx00000nKjZ2IAK                     None   
981  012Dx0000003p5DIAQ  003Dx00000nKjZ8IAK                     None   
982  012Dx0000003p5AIAQ  003Dx00000nKjZ9IAK               2007-11-26   
983  012Dx0000003p5DIAQ  003Dx00000nKimjIAC                     None   
984  012Dx0000003p5DIAQ  003Dx00000nKimkIAC                     None   

    mbfc__Start_Date__c    mbfc__Context__c       mbfc__Category__c  \
0            2021-11-02  001Dx00001HwDsgIAF               Faculties   
1                  None  001Dx00001HwDsgIAF               Faculties   
2            2016-06-04  001Dx00001HwDsgIAF               Faculties   
3                  None  001Dx00001HwDsgIAF           Installations   
4                  None  001Dx00001HwDsgIAF           Installations   
..                  ...                 ...                     ...   
980          2022-06-01  001Dx00001HwDsgIAF               Faculties   
981          1976-06-05  001Dx00001HwDsgIAF               Faculties   
982                None  001Dx00001HwFHDIA3  Ecclesial Affiliations   
983          1979-10-05  001Dx00001HwDsgIAF               Faculties   
984          1997-07-12  001Dx00001HwDsgIAF               Faculties   

         mbfc__Affiliation__c  \
0    Faculties (Confessional)   
1       Faculties (Withdrawn)   
2         Faculties (General)   
3         Reader Installation   
4        Acolyte Installation   
..                        ...   
980       Faculties (General)   
981       Faculties (General)   
982              Incardinated   
983       Faculties (General)   
984       Faculties (General)   

                              Archdpdx_Migration_Id__c  
0    003dx00000nkiqaias20211102faculties(confessional)  
1       003dx00000nkiqfias20100630faculties(withdrawn)  
2         003dx00000nkiqrias20160604faculties(general)  
3         003dx00000nkiqrias20130410readerinstallation  
4        003dx00000nkiqrias20130410acolyteinstallation  
..                                                 ...  
980       003dx00000nkjz2iak20220601faculties(general)  
981       003dx00000nkjz8iak19760605faculties(general)  
982             003dx00000nkjz9iak20071126incardinated  
983       003dx00000nkimjiac19791005faculties(general)  
984       003dx00000nkimkiac19970712faculties(general)  

[985 rows x 8 columns]

In [195]:
# upsert Ecclesial Affiliation records
upsert_to_salesforce_bulk(sf, ecclesial_affiliations_staging, 'mbfc__Affiliation__c', 'Archdpdx_Migration_Id__c', 'results_files/ecclesial_affil_upsert_results', 100)

#FIXME: There are a number of rows where a Faculties Granted is missing a date, and conversely, where there is a Faculties Granted Date but no description of the Faculties granted. This is a problem, because the application requires a date for when Faculties were granted.

# Takes approx 1.5 minutes to run

Error processing key: RecordTypeId, value: 012Dx0000003p5DIAQ, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Person__c, value: 003Dx00000nKiqAIAS, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Completion_Date__c, value: None, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Start_Date__c, value: 2021-11-02, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Context__c, value: 001Dx00001HwDsgIAF, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Category__c, value: Faculties, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Affiliation__c, value: Faculties (Confessional), error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: Archdpdx_Migration_Id__c, 

## Religious Community Affiliations

In [210]:
acc_religious_staging_2

Name        RecordTypeId  \
186         Colombiere Jesuit Community, Portland (SJ)  012Dx0000003p52IAA   
187     Abbey of Our Lady of Guadalupe, Carlton (OCSO)  012Dx0000003p52IAA   
188             JCCU Jesuit Tertianship, Portland (SJ)  012Dx0000003p52IAA   
189  Benedictine Monks of Mount Angel Abbey, Saint ...  012Dx0000003p52IAA   
190  Missionaries of the Holy Spirit Provincial Hou...  012Dx0000003p52IAA   
..                                                 ...                 ...   
251       Society of the Divine Word, Techny, IL (SVD)  012Dx0000003p52IAA   
252   Society of the Divine Saviour, Rome, Italy (SDS)  012Dx0000003p52IAA   
253  Society of Our Lady of the Most Holy Trinity, ...  012Dx0000003p52IAA   
254          Community of St. Thomas More, Eugene (OP)  012Dx0000003p52IAA   
255         Saint Benedict Lodge, McKenzie Bridge (OP)  012Dx0000003p52IAA   

    mbfc__Religious_Type__c                                     BillingStreet  \
186         Local Community                                  3220 SE 43rd Ave   
187         Local Community  Abbey of Our Lady of Guadalupe\n9200 NE Abbey Rd   
188         Local Community                                  3301 SE 45th Ave   
189         Local Community                                        1 Abbey Dr   
190         Local Community                                      PO Box 22387   
..                      ...                                               ...   
251         Local Community      Society of the Divine Word, Chicago Province   
252         Local Community                       Via della Conciliazione, 51   
253         Local Community                                       PO Box 4116   
254         Local Community                                   1386 E 18th Ave   
255         Local Community                                   56630 N Bank Rd   

         BillingCity BillingState BillingPostalCode BillingCountry  \
186         Portland           OR             97206           None   
187          Carlton           OR             97111           None   
188         Portland           OR             97206           None   
189   Saint Benedict           OR             97373           None   
190        Milwaukie           OR             97269           None   
..               ...          ...               ...            ...   
251             None         None              None           None   
252             Roma         None           I-00193          ITALY   
253   Corpus Christi           TX             78469           None   
254           Eugene           OR             97403           None   
255  McKenzie Bridge           OR             97413           None   

              Phone           Fax               mbfc__Email__c  \
186    503-595-1941          None                         None   
187    503-852-7174  503-852-7748  community@trappistabbey.org   
188            None          None    jctertianship@jesuits.org   
189    503-845-3030          None        info@mtangelabbey.edu   
190    503-324-2492  503-324-2493                         None   
..              ...           ...                          ...   
251            None          None                         None   
252  +39 06 686 291          None                         None   
253            None          None                         None   
254    541-343-0065  541-686-8028                         None   
255    541-822-3572          None           sblodge@opwest.org   

                              Website  \
186      https://www.jesuitswest.org/   
187     http://www.trappistabbey.org/   
188                              None   
189  https://www.mountangelabbey.org/   
190                   www.mspscpp.org   
..                                ...   
251       https://www.divineword.org/   
252               http://www.sds.org/   
253                 https://solt.net/   
254                      uonewman.org   
255                sblodge.opwest.org   

             

In [211]:
df_contact_staging

ADPDX_Contact_Type__c ADPDX_Clergy_Status__c  \
Record Number                                                
2766                         Priest        Transferred Out   
2337                          Staff                   None   
3244                          Staff                   None   
3295                          Staff                   None   
2164                          Staff                   None   
...                             ...                    ...   
1670                          Staff                   None   
2755                      Religious                   None   
1962                          Staff                   None   
2202                          Staff                   None   
1866                          Staff                   None   

              ADPDX_Religious_Status__c ADPDX_Login_ID__c  \
Record Number                                               
2766                               None          sabukaka   
2337                               None              None   
3244                               None              None   
3295                               None              None   
2164                               None              None   
...                                 ...               ...   
1670                               None              None   
2755                             Active         dzorrilla   
1962                               None              None   
2202                               None              None   
1866                               None              None   

              ADPDX_Access_Permission__c Salutation FirstName  \
Record Number                                                   
2766                                None       Rev.   Stephen   
2337                                None        Mr.   Rogelio   
3244                                None        Mr.      Sean   
3295                                None        Ms.   Sherril   
2164                                None        Ms.   Barbara   
...                                  ...        ...       ...   
1670                                None        Ms.     Jenny   
2755                                None        Br.    Daniel   
1962                                None        Ms.       Kim   
2202                                None        Ms.     Agnes   
1866                                None        Ms.    Laurie   

              adpdx_Preferred_Name__c MiddleName  LastName Suffix  \
Record Number                                                       
2766                             None    Ozovehe  Abaukaka   None   
2337                             None       None   Acevedo   None   
3244                             None       None   Ackroyd   None   
3295                             None       None     Acton   None   
2164                             None       None     Adams   None   
...                               ...        ...       ...    ...   
1670                             None       None  Zomerdyk   None   
2755                             None       None  Zorrilla   None   
1962                             None       None     Zuber   None   
2202                             None       None    Zueger   None   
1866                             None       None    Zupsic   None   

                  MailingCity MailingState MailingPostalCode MailingCountry  \
Record Number                                                                 
2766                 Tualatin           OR             97062           None   
2337                     None         None              None           None   
3244                     None         None              None           None   
3295                     None         None              None           None   
2164                     None         None              None           None   
...                       ...          ...               ...            ...   
1670                     None        

In [212]:
import pandas as pd

# Function to get the Salesforce record for the corresponding religious community records
def get_religious_community_id(religious_community_ID):
    if pd.isna(religious_community_ID) or religious_community_ID == '0':
        return None  # Return None or handle as appropriate if religious community name is NaN or '0'

    # Query Salesforce to find the religious community
    query = f"SELECT Id, Name FROM Account WHERE Archdpdx_Migration_Id__c = 'RelCommunities_{religious_community_ID}' LIMIT 1"
    results = sf.query(query)
    
    # If exists, return the ID
    if results['records']:
        return results['records'][0]['Id']
    else:
        raise ValueError(f"Religious community with ID '{religious_community_ID}' not found in Salesforce.")

# Function to get the Salesforce contact ID by record number
def get_contact_id_by_record_number(record_number):
    if pd.isna(record_number):
        return None
    query = f"SELECT Id FROM Contact WHERE Archdpdx_Migration_Id__c = '{record_number}'"
    results = sf.query(query)
    if results['records']:
        return results['records'][0]['Id']
    return None

# Prepare the data frame with the necessary columns
religious_affiliations_staging = pd.DataFrame(columns=['mbfc__Person__c', 'mbfc__Context__c', 'mbfc__Category__c', 'mbfc__Affiliation__c', 'Archdpdx_Migration_Id__c'])

# Populate the data frame with the contact IDs and religious community IDs
new_entries = []

for index, row in df_contact_staging_spouses.iterrows():
    religious_community_ID = row.get('Link_to_Religious_Community', None)
    if pd.notna(religious_community_ID) and religious_community_ID != '0':
        contact_id = get_contact_id_by_record_number(row['Archdpdx_Migration_Id__c'])
        religious_community_id = get_religious_community_id(religious_community_ID)
        
        affiliation_record = {
            'mbfc__Person__c': contact_id,
            'mbfc__Context__c': religious_community_id,
            'mbfc__Category__c': 'Religious Community',
            'mbfc__Affiliation__c': 'Member',
            'Archdpdx_Migration_Id__c': f"{contact_id}_{religious_community_id}_RelComm"
        }
        new_entries.append(affiliation_record)

# Convert the list of new entries to a DataFrame
religious_affiliations_staging = pd.DataFrame(new_entries)

# Cell takes >4m to run

In [214]:
# Drop the index and ensure only the required columns are included

# religious_affiliations_staging.reset_index(drop=True, inplace=True)

religious_affiliations_staging = religious_affiliations_staging[['mbfc__Person__c', 'mbfc__Context__c', 'mbfc__Category__c', 'mbfc__Affiliation__c', 'Archdpdx_Migration_Id__c']]

# Upsert the data frame to Salesforce
upsert_to_salesforce_bulk(sf, religious_affiliations_staging, 'mbfc__Affiliation__c', 'Archdpdx_Migration_Id__c', 'results_files/religious_affil_upsert_results', 100)

Error processing key: mbfc__Person__c, value: 003Dx00000nKiqHIAS, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Context__c, value: 001Dx00001HwE5OIAV, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Category__c, value: Religious Community, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Affiliation__c, value: Member, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: Archdpdx_Migration_Id__c, value: 003Dx00000nKiqHIAS_001Dx00001HwE5OIAV_RelComm, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Person__c, value: 003Dx00000nKiqLIAS, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error processing key: mbfc__Context__c, value: 001Dx00001HwE5JIAV, error: isinstance() arg 2 must be a type, a tuple of types, or a union
Error p

# AFFILIATIONS


In [572]:
# Import Assignments.csv

import pandas as pd


df_affiliations = (
    pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Assignments (1).csv')
    .set_index('Record Number', verify_integrity=True)
    .drop(index='recNum', errors='ignore')  # Added errors='ignore' to prevent errors if 'recNum' does not exist
    .drop(columns=['Historic Name'], errors='ignore')  # Added errors='ignore' for the same reason
    .rename(columns=lambda x: x.replace(' ', '_'))  # Remove whitespace in column names
    .assign(Account_Ext_Id=lambda df: df['Organization_Table_Name'] + '_' + df['Organization_Table_Link'])
    # .assign(mbfc__Person__r=lambda df: df['Assigned_Person'].apply(lambda x: {'Archdpdx_Migration_Id__c': x}))
    # .assign(mbfc__Context__r=lambda df: df['Account_Ext_Id'].apply(lambda x: {'Archdpdx_Migration_Id__c': x}))
    # .assign(mbfc__Use_Custom_Title__c= True)
    .assign(mbfc__Category__c= 'Any All')
    # .assign(Archdpdx_Migration_Id__c= df_affiliations.index)
    .drop(columns=[
        # 'Assigned_Person'
        'Organization_Table_Name'
        ,'Organization_Table_Link'
        ,'Projected_Term_End_Date'
        ,'Term_Number'
        ,'Leave_Type' # Leave out 'Leave_Type' until mapped properly
        ])
    .rename(columns={
        'Duty_Load': 'mbfc__Duty_Load__c',
        'Start_Date': 'mbfc__Start_Date__c',
        'End_Date': 'mbfc__Completion_Date__c',
        'Assignment_Title': 'mbfc__Affiliation__c',
        'Archdiocesan_Assignment': 'adpdx_Archdiocesan_Assignment__c',
    })
    .replace({'ADPDX_Archdiocesan_Assignment__c': {'Yes': True, 'No': False, None: False}})
    .fillna('')
)

# Display a sample of the DataFrame to check the new structure
df_affiliations.sample(10)



Assigned_Person              mbfc__Affiliation__c  \
Record Number                                                     
2419                     1559  Institute for Priestly Formation   
3172                     3000          Administrative Assistant   
2420                      541  Institute for Priestly Formation   
3190                     1598                     Pastoral Year   
1346                      804                      Vicar Forane   
287                       779                     Administrator   
2694                     2732                 Summer Assignment   
514                      1505         Special Projects Reporter   
2678                      767    Presbyteral Council: Consultor   
1178                     1958                         Secretary   

              adpdx_Archdiocesan_Assignment__c mbfc__Duty_Load__c  \
Record Number                                                       
2419                                                                
3172                                                                
2420                                       Yes                      
3190                                       Yes          Full Time   
1346                                       Yes                      
287                                        Yes                      
2694                                                                
514                                                                 
2678                                        No                      
1178                                                                

              mbfc__Start_Date__c mbfc__Completion_Date__c Account_Ext_Id  \
Record Number                                                               
2419                   2021-06-01               2021-08-31     Offices_22   
3172                                            2023-06-22      Offices_1   
2420                   2021-06-01               2021-08-31     Offices_22   
3190                   2023-08-01               2023-12-31     Parishes_5   
1346                   2019-10-01                           Vicariates_14   
287                    2016-07-01               2019-06-30    Parishes_68   
2694                   2022-03-25               2022-07-31    Parishes_58   
514                                             1900-01-01      Offices_3   
2678                   2022-03-05                              Offices_21   
1178                                                         Parishes_141   

              mbfc__Category__c  
Record Number                    
2419                    Any All  
3172                    Any All  
2420                    Any All  
3190                    Any All  
1346                    Any All  
287                     Any All  
2694                    Any All  
514                     Any All  
2678                    Any All  
1178                    Any All

In [573]:
df_affiliations['adpdx_Archdiocesan_Assignment__c'] = df_affiliations['adpdx_Archdiocesan_Assignment__c'].replace({'Yes': True, 'No': False, '': False}).fillna(False)

In [574]:
# Get SF Record Ids from External Ids

# Get Context Account Ids
add_salesforce_record_ids(sf, df_affiliations, 'Account_Ext_Id', 'Account', 'Archdpdx_Migration_Id__c', 'mbfc__Context__c')

Assigned_Person              mbfc__Affiliation__c  \
Record Number                                                     
3515                      780           Presbyteral Council Rep   
3514                      762           Presbyteral Council Rep   
3512                     3321                            Deacon   
3511                      803                Special Assignment   
3510                     3317  Development Operations Associate   
...                       ...                               ...   
5                         511                      Vicar Forane   
4                         511                     Administrator   
3                         511                            Pastor   
2                         318                            Deacon   
1                         318                            Deacon   

               adpdx_Archdiocesan_Assignment__c mbfc__Duty_Load__c  \
Record Number                                                        
3515                                       True          Part Time   
3514                                       True          Part Time   
3512                                       True          Full Time   
3511                                       True          Full Time   
3510                                      False                      
...                                         ...                ...   
5                                          True                      
4                                          True                      
3                                          True          Full Time   
2                                          True                      
1                                          True                      

              mbfc__Start_Date__c mbfc__Completion_Date__c Account_Ext_Id  \
Record Number                                                               
3515                   2024-01-01                           Vicariates_16   
3514                   2024-01-01                            Vicariates_3   
3512                   2024-02-19                             Parishes_83   
3511                   2024-02-10                              Offices_21   
3510                   2024-01-16                               Offices_1   
...                           ...                      ...            ...   
5                      2016-10-01               2023-09-30  Vicariates_10   
4                      2013-07-01               2017-06-30   Parishes_109   
3                      2017-07-01                            Parishes_109   
2                      2002-12-23               2016-06-30   Parishes_114   
1                      2016-09-01                            Parishes_109   

              mbfc__Category__c    mbfc__Context__c  
Record Number                                        
3515                    Any All  001Dx00001HwDx2IAF  
3514                    Any All  001Dx00001HwDwpIAF  
3512                    Any All  001Dx00001HwDzoIAF  
3511                    Any All  001Dx00001HwDyQIAV  
3510                    Any All  001Dx00001HwDyIIAV  
...                         ...                 ...  
5                       Any All  001Dx00001HwDwwIAF  
4                       Any All  001Dx00001HwE0DIAV  
3                       Any All  001Dx00001HwE0DIAV  
2                       Any All  001Dx00001HwE0IIAV  
1                       Any All  001Dx00001HwE0DIAV  

[2699 rows x 9 columns]

In [575]:
# Get Person Contact Ids
add_salesforce_record_ids(sf, df_affiliations, 'Assigned_Person', 'Contact', 'Archdpdx_Migration_Id__c', 'mbfc__Person__c')

Assigned_Person              mbfc__Affiliation__c  \
Record Number                                                     
3515                      780           Presbyteral Council Rep   
3514                      762           Presbyteral Council Rep   
3512                     3321                            Deacon   
3511                      803                Special Assignment   
3510                     3317  Development Operations Associate   
...                       ...                               ...   
5                         511                      Vicar Forane   
4                         511                     Administrator   
3                         511                            Pastor   
2                         318                            Deacon   
1                         318                            Deacon   

               adpdx_Archdiocesan_Assignment__c mbfc__Duty_Load__c  \
Record Number                                                        
3515                                       True          Part Time   
3514                                       True          Part Time   
3512                                       True          Full Time   
3511                                       True          Full Time   
3510                                      False                      
...                                         ...                ...   
5                                          True                      
4                                          True                      
3                                          True          Full Time   
2                                          True                      
1                                          True                      

              mbfc__Start_Date__c mbfc__Completion_Date__c Account_Ext_Id  \
Record Number                                                               
3515                   2024-01-01                           Vicariates_16   
3514                   2024-01-01                            Vicariates_3   
3512                   2024-02-19                             Parishes_83   
3511                   2024-02-10                              Offices_21   
3510                   2024-01-16                               Offices_1   
...                           ...                      ...            ...   
5                      2016-10-01               2023-09-30  Vicariates_10   
4                      2013-07-01               2017-06-30   Parishes_109   
3                      2017-07-01                            Parishes_109   
2                      2002-12-23               2016-06-30   Parishes_114   
1                      2016-09-01                            Parishes_109   

              mbfc__Category__c    mbfc__Context__c     mbfc__Person__c  
Record Number                                                            
3515                    Any All  001Dx00001HwDx2IAF  003Dx00000nKjOcIAK  
3514                    Any All  001Dx00001HwDwpIAF  003Dx00000nKjUcIAK  
3512                    Any All  001Dx00001HwDzoIAF  003Dx00000nKjSuIAK  
3511                    Any All  001Dx00001HwDyQIAV  003Dx00000nKiw1IAC  
3510                    Any All  001Dx00001HwDyIIAV  003Dx00000nKjDGIA0  
...                         ...                 ...                 ...  
5                       Any All  001Dx00001HwDwwIAF  003Dx00000nKjQrIAK  
4                       Any All  001Dx00001HwE0DIAV  003Dx00000nKjQrIAK  
3                       Any All  001Dx00001HwE0DIAV  003Dx00000nKjQrIAK  
2                       Any All  001Dx00001HwE0IIAV  003Dx00000nKipTIAS  
1                       Any All  001Dx00001HwE0DIAV  003Dx00000nKipTIAS  

[2699 rows x 10 columns]

In [576]:
# Set Archdpdx_Migration_Id__c External ID
df_affiliations['Archdpdx_Migration_Id__c'] = df_affiliations.index

# Create Job ID
df_affiliations['Archdpdx_Job_Id__c'] = curr_job_id

df_affiliations


Assigned_Person              mbfc__Affiliation__c  \
Record Number                                                     
3515                      780           Presbyteral Council Rep   
3514                      762           Presbyteral Council Rep   
3512                     3321                            Deacon   
3511                      803                Special Assignment   
3510                     3317  Development Operations Associate   
...                       ...                               ...   
5                         511                      Vicar Forane   
4                         511                     Administrator   
3                         511                            Pastor   
2                         318                            Deacon   
1                         318                            Deacon   

               adpdx_Archdiocesan_Assignment__c mbfc__Duty_Load__c  \
Record Number                                                        
3515                                       True          Part Time   
3514                                       True          Part Time   
3512                                       True          Full Time   
3511                                       True          Full Time   
3510                                      False                      
...                                         ...                ...   
5                                          True                      
4                                          True                      
3                                          True          Full Time   
2                                          True                      
1                                          True                      

              mbfc__Start_Date__c mbfc__Completion_Date__c Account_Ext_Id  \
Record Number                                                               
3515                   2024-01-01                           Vicariates_16   
3514                   2024-01-01                            Vicariates_3   
3512                   2024-02-19                             Parishes_83   
3511                   2024-02-10                              Offices_21   
3510                   2024-01-16                               Offices_1   
...                           ...                      ...            ...   
5                      2016-10-01               2023-09-30  Vicariates_10   
4                      2013-07-01               2017-06-30   Parishes_109   
3                      2017-07-01                            Parishes_109   
2                      2002-12-23               2016-06-30   Parishes_114   
1                      2016-09-01                            Parishes_109   

              mbfc__Category__c    mbfc__Context__c     mbfc__Person__c  \
Record Number                                                             
3515                    Any All  001Dx00001HwDx2IAF  003Dx00000nKjOcIAK   
3514                    Any All  001Dx00001HwDwpIAF  003Dx00000nKjUcIAK   
3512                    Any All  001Dx00001HwDzoIAF  003Dx00000nKjSuIAK   
3511                    Any All  001Dx00001HwDyQIAV  003Dx00000nKiw1IAC   
3510                    Any All  001Dx00001HwDyIIAV  003Dx00000nKjDGIA0   
...                         ...                 ...                 ...   
5                       Any All  001Dx00001HwDwwIAF  003Dx00000nKjQrIAK   
4                       Any All  001Dx00001HwE0DIAV  003Dx00000nKjQrIAK   
3                       Any All  001Dx00001HwE0DIAV  003Dx00000nKjQrIAK   
2                       Any All  001Dx00001HwE0IIAV  003Dx00000nKipTIAS   
1                       Any All  001Dx00001HwE0DIAV  003Dx00000nKipTIAS   

              Archdpdx_Migration_Id__c  Archdpdx_Job_Id__c  
Record Number                                               
3515                              3515                 133  
3514                              3514                 133  
3512     

In [577]:
# Final cleanup
df_affiliations.drop(columns=[
    'Account_Ext_Id',
    'Assigned_Person', 
    ], 
    inplace=True)

df_affiliations

#FIXME: INVALID_FIELD: Foreign key external ID: relcommunities_23 not found for field Archdpdx_Migration_Id__c
#FIXME: INVALID_FIELD: Foreign key external ID: offices_0 not found for field Archdpdx_Migration_Id__c
#FIXME: Record #115 > FIELD_INTEGRITY_EXCEPTION: Start Date: invalid date: Tue Aug 01 00:00:00 GMT 1021 [mbfc__Start_Date__c

mbfc__Affiliation__c  \
Record Number                                     
3515                    Presbyteral Council Rep   
3514                    Presbyteral Council Rep   
3512                                     Deacon   
3511                         Special Assignment   
3510           Development Operations Associate   
...                                         ...   
5                                  Vicar Forane   
4                                 Administrator   
3                                        Pastor   
2                                        Deacon   
1                                        Deacon   

               adpdx_Archdiocesan_Assignment__c mbfc__Duty_Load__c  \
Record Number                                                        
3515                                       True          Part Time   
3514                                       True          Part Time   
3512                                       True          Full Time   
3511                                       True          Full Time   
3510                                      False                      
...                                         ...                ...   
5                                          True                      
4                                          True                      
3                                          True          Full Time   
2                                          True                      
1                                          True                      

              mbfc__Start_Date__c mbfc__Completion_Date__c mbfc__Category__c  \
Record Number                                                                  
3515                   2024-01-01                                    Any All   
3514                   2024-01-01                                    Any All   
3512                   2024-02-19                                    Any All   
3511                   2024-02-10                                    Any All   
3510                   2024-01-16                                    Any All   
...                           ...                      ...               ...   
5                      2016-10-01               2023-09-30           Any All   
4                      2013-07-01               2017-06-30           Any All   
3                      2017-07-01                                    Any All   
2                      2002-12-23               2016-06-30           Any All   
1                      2016-09-01                                    Any All   

                 mbfc__Context__c     mbfc__Person__c  \
Record Number                                           
3515           001Dx00001HwDx2IAF  003Dx00000nKjOcIAK   
3514           001Dx00001HwDwpIAF  003Dx00000nKjUcIAK   
3512           001Dx00001HwDzoIAF  003Dx00000nKjSuIAK   
3511           001Dx00001HwDyQIAV  003Dx00000nKiw1IAC   
3510           001Dx00001HwDyIIAV  003Dx00000nKjDGIA0   
...                           ...                 ...   
5              001Dx00001HwDwwIAF  003Dx00000nKjQrIAK   
4              001Dx00001HwE0DIAV  003Dx00000nKjQrIAK   
3              001Dx00001HwE0DIAV  003Dx00000nKjQrIAK   
2              001Dx00001HwE0IIAV  003Dx00000nKipTIAS   
1              001Dx00001HwE0DIAV  003Dx00000nKipTIAS   

              Archdpdx_Migration_Id__c  Archdpdx_Job_Id__c  
Record Number                                               
3515                              3515                 133  
3514                              3514                 133  
3512                              3512                 133  
3511                              3511                 133  
3510                              3510                 133  
...                                ...                 ...  
5                                    5                 133  
4                                    4                 133  
3                                    3                 133 

In [578]:
# TEST ME
# Set Archdpdx_Migration_Id__c External ID
df_affiliations['Archdpdx_Migration_Id__c'] = df_affiliations.index.astype(str).str.replace(' ', '').str.replace('-', '')


In [579]:
df_affiliations.to_csv('staging_files/affiliations_staging.csv', encoding='utf-8', index=False)

In [580]:
upsert_to_salesforce_bulk(sf, df_affiliations, 'mbfc__Affiliation__c', 'Archdpdx_Migration_Id__c', 'results_files/affiliation_upsert_results')

# cell takes >3m to run

Batch 1 processed: 100 successful, 0 failed.
Batch 2 processed: 200 successful, 0 failed.
Batch 3 processed: 300 successful, 0 failed.
Batch 4 processed: 400 successful, 0 failed.
Batch 5 processed: 499 successful, 1 failed.
Batch 6 processed: 599 successful, 1 failed.
Batch 7 processed: 699 successful, 1 failed.
Batch 8 processed: 799 successful, 1 failed.
Batch 9 processed: 899 successful, 1 failed.
Batch 10 processed: 999 successful, 1 failed.
Batch 11 processed: 1099 successful, 1 failed.
Batch 12 processed: 1199 successful, 1 failed.
Batch 13 processed: 1299 successful, 1 failed.
Batch 14 processed: 1399 successful, 1 failed.
Batch 15 processed: 1499 successful, 1 failed.
Batch 16 processed: 1598 successful, 2 failed.
Batch 17 processed: 1698 successful, 2 failed.
Batch 18 processed: 1797 successful, 3 failed.
Batch 19 processed: 1897 successful, 3 failed.
Batch 20 processed: 1997 successful, 3 failed.
Batch 21 processed: 2096 successful, 4 failed.
Batch 22 processed: 2196 success

# Post-Migration Manual Updates

1. Convert 'Offices' that are ADPDX Pastoral Centre offices into record type: 'Groups', and set their parentID to the Diocese (there are just 6 of these accounts).
1. Update the Religous Order records 'Religious Superior' lookup.
1. Set 'organization type' field value for each account in the 'organization' load: Offices, Newman Centres, Schools, Organizations
1. Consolidate education degree titles in 'Affiliation.Affiliation' picklist into the standard value
